![](img/header.png)

## Дипломный проект на тему   
## "Модель прогнозирования стоимости жилья для агентства недвижимости "

Цель работы: разработать модель, которая помогла бы агентству недвижимости более быстро обрабатывать объявления и увеличить количество сделок и доход компании.

Описание данных:  

➔ 'status' — статус продажи;  
➔ 'private pool' и 'PrivatePool' — наличие собственного бассейна;  
➔ 'propertyType' — тип объекта недвижимости;  
➔ 'street' — адрес объекта;  
➔ 'baths' — количество ванных комнат;  
➔ 'homeFacts' — сведения о строительстве объекта (содержит несколько типов сведений, влияющих на оценку объекта);  
➔ 'fireplace' — наличие камина;  
➔ 'city' — город;  
➔ 'schools' — сведения о школах в районе;  
➔ 'sqft' — площадь в футах;  
➔ 'zipcode' — почтовый индекс;  
➔ 'beds' — количество спален;  
➔ 'state' — штат;  
➔ 'stories' — количество этажей;  
➔ 'mls-id' и 'MlsId' — идентификатор MLS (Multiple Listing Service, система мультилистинга);  
➔ 'target' — цена объекта недвижимости (целевой признак, который необходимо спрогнозировать).

In [1]:
# импортируем библиотеки, потребующиеся нам в дальнейшей работе
import pandas as pd
import numpy as np
import ydata_profiling
import re
import seaborn as sns
from scipy import stats
import statsmodels.api as sm
from sklearn import model_selection
from sklearn import feature_selection
from sklearn import linear_model
from sklearn import metrics
from sklearn import preprocessing
from sklearn import tree
from sklearn import ensemble
from sklearn.base import TransformerMixin, BaseEstimator
from sklearn.pipeline import Pipeline
import category_encoders as ce
import pickle
import matplotlib.pyplot as plt


## 1. Знакомство с данными, базовый анализ, EDA

In [2]:
# для первого взгляда на данные считаем первые несколько строк из файла
data = pd.read_csv('data.csv', nrows=5)

In [3]:
data

status  private pool        propertyType               street    baths  \
0    Active           NaN  Single Family Home       240 Heather Ln      3.5   
1  for sale           NaN  single-family home    12911 E Heroy Ave  3 Baths   
2  for sale           NaN  single-family home    2005 Westridge Rd  2 Baths   
3  for sale           NaN  single-family home  4311 Livingston Ave  8 Baths   
4  for sale           NaN            lot/land       1524 Kiscoe St      NaN   

                                           homeFacts fireplace  \
0  {'atAGlanceFacts': [{'factValue': '2019', 'fac...  Gas Logs   
1  {'atAGlanceFacts': [{'factValue': '2019', 'fac...       NaN   
2  {'atAGlanceFacts': [{'factValue': '1961', 'fac...       yes   
3  {'atAGlanceFacts': [{'factValue': '2006', 'fac...       yes   
4  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   

             city                                            schools  \
0  Southern Pines  [{'rating': ['4', '4', '7', 'NR', '4', '7', 'N...   
1  Spokane Valley  [{'rating': ['4/10', 'None/10', '4/10'], 'data...   
2     Los Angeles  [{'rating': ['8/10', '4/10', '8/10'], 'data': ...   
3          Dallas  [{'rating': ['9/10', '9/10', '10/10', '9/10'],...   
4        Palm Bay  [{'rating': ['4/10', '5/10', '5/10'], 'data': ...   

         sqft  zipcode    beds state  stories  mls-id PrivatePool       MlsId  \
0        2900    28387       4    NC      NaN     NaN         NaN      611019   
1  1,947 sqft    99216  3 Beds    WA      2.0     NaN         NaN   201916904   
2  3,000 sqft    90049  3 Beds    CA      1.0     NaN         yes  FR19221027   
3  6,457 sqft    75205  5 Beds    TX      3.0     NaN         NaN    14191809   
4         NaN    32908     NaN    FL      NaN     NaN         NaN      861745   

       target  
0    $418,000  
1    $310,000  
2  $2,895,000  
3  $2,395,000  
4      $5,000

In [4]:
# Теперь считаем файл целиком и проведем исследовательский анализ данных (EDA) при помощи библиотеки ydata_profiling
df = pd.read_csv('data.csv')
profile = ydata_profiling.ProfileReport(df, title="Profiling Report")

In [5]:
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 18/18 [01:58<00:00,  6.60s/it]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [6]:
# экспортируем данный отчет в файл, это позволит более удобно работать с ним
profile.to_file("data_report.html")

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

Поскольку MlsId и mls-id - это код в централизованной системе учёта предложений объектов недвижимости, то на цену объекта он ни как не влияет, и эти признаки можно удалить.

In [7]:
df.drop(['mls-id','MlsId'],axis=1, inplace=True)

In [8]:
# В разделе Duplicate rows отчета видно, что в наших данных присутствуют варианты строк, которые дублируются.
# Количество дублей можно посмотреть так:
df.duplicated().sum()    

np.int64(141)

In [9]:
# Удалим дубли
df_dd = df.drop_duplicates(ignore_index=True)

___
**Проанализирую два признака про наличие бассейна.**

In [10]:
df_dd['private pool']

0         NaN
1         NaN
2         NaN
3         NaN
4         NaN
         ... 
377039    NaN
377040    NaN
377041    NaN
377042    NaN
377043    NaN
Name: private pool, Length: 377044, dtype: object

In [11]:
df_dd['PrivatePool']

0         NaN
1         NaN
2         yes
3         NaN
4         NaN
         ... 
377039    Yes
377040    NaN
377041    NaN
377042    NaN
377043    NaN
Name: PrivatePool, Length: 377044, dtype: object

In [12]:
# проверим одинаковые ли признаки
df_dd['PrivatePool'].equals(df_dd['private pool'])

False

In [13]:
# посмотрим сколько расхождений
df_dd['PrivatePool'].isin(df_dd['private pool']).value_counts()

PrivatePool
True     348252
False     28792
Name: count, dtype: int64

In [14]:
# выведем только различающиеся
mask_pool = np.invert(df_dd['PrivatePool'].isin(df_dd['private pool']))
pool_diff = df_dd[mask_pool][['PrivatePool','private pool']]
pool_diff

PrivatePool private pool
2              yes          NaN
12             yes          NaN
19             yes          NaN
43             yes          NaN
67             yes          NaN
...            ...          ...
377016         yes          NaN
377026         yes          NaN
377027         yes          NaN
377030         yes          NaN
377033         yes          NaN

[28792 rows x 2 columns]

In [15]:
pool_diff['PrivatePool'].unique()

array(['yes'], dtype=object)

In [16]:
pool_diff['private pool'].unique()

array([nan], dtype=object)

Вывод: наблюдаю однозначное соответствие пропущенных значений в одном признаке значению "yes" в другом признаке.  
Причем, если посмотреть на уникальные значения признаков, то видно, что "yes" со строчной буквы появляется только в тех строках, которые имеют отличия в этих двух признаках.

In [17]:
df_dd['PrivatePool'].unique()

array([nan, 'yes', 'Yes'], dtype=object)

In [18]:
df_dd['private pool'].unique()

array([nan, 'Yes'], dtype=object)

На основании этого можно предположить две разные гипотезы. 
1. Признак 'PrivatePool' несет в себе более свежую информацию. Например бассейн могли достроить и обновить информацию в базе данных. Косвенно это подтверждается тем, что признак 'PrivatePool' находится ближе к концу списка признаков, чем признак 'private pool', то есть можно предположить, что 'PrivatePool' был добавлен гораздо позже.
2. Можно предположить и обратную ситуацию, что бассейн был демонтирован или является не рабочим, по причине каких-либо неустранимых дефектов.

Исходя из своего жизненного опыта, первая гипотеза мне представляется более правдоподобной. Поэтому принимаю первую гипотезу! После этого признак 'private pool' можно удалить, как менее информативный, а признак 'PrivatePool' закодировать булевым значением.

In [19]:
# создам новый признак наличия бассейна
df_dd["Pool"] = df_dd['PrivatePool'].notnull()

C:\Users\User\AppData\Local\Temp\ipykernel_7976\502946662.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_dd["Pool"] = df_dd['PrivatePool'].notnull()


In [20]:
# удалим первоначальные признаки бассейна
df_dd.drop(['PrivatePool','private pool'], axis=1, inplace=True)

C:\Users\User\AppData\Local\Temp\ipykernel_7976\1619028998.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_dd.drop(['PrivatePool','private pool'], axis=1, inplace=True)


с признаком бассейна закончила
___

In [21]:
# проверим не появились ли дубли после этого
df_dd.duplicated().sum() 

np.int64(0)

___

**Поработаем с пропусками**

In [22]:
# порог в наших данных от 8 и выше
df_dd.dropna(thresh=8).index

Index([     0,      1,      2,      3,      4,      5,      6,      7,      8,
            9,
       ...
       377034, 377035, 377036, 377037, 377038, 377039, 377040, 377041, 377042,
       377043],
      dtype='int64', length=377008)

In [23]:
mask_na = np.invert(df_dd.index.isin(df_dd.dropna(thresh=8).index))

In [24]:
df_dd[mask_na]

status propertyType                        street baths  \
3114      NaN          NaN   277 Washington Ave Unit 5H    NaN   
12018     NaN          NaN               488 4th Ave #1    NaN   
28624     NaN          NaN             7 Craftsfield Rd    NaN   
29182     NaN          NaN      1380 River Bend Dr #133    NaN   
34560     NaN          NaN       4701 Meridian Ave #126    NaN   
44949     NaN          NaN              Grove Park Blvd    NaN   
74558     NaN          NaN                 153 Avenue P    NaN   
92408     NaN          NaN   96 Schermerhorn St Unit 7E    NaN   
92854     NaN          NaN       9985 Shore Rd Unit 14E    NaN   
101489    NaN          NaN               427 Hopkins St    NaN   
117095    NaN          NaN            5530 Firestone Rd    NaN   
139731    NaN          NaN  96 Schermerhorn St Unit 12E    NaN   
145054    NaN          NaN               4004 Weslow St    NaN   
154979    NaN          NaN     5136 S Creston St Unit B    NaN   
171841    NaN          NaN           Undisclosed Address   NaN   
172317    NaN          NaN   10 Cascada Vista Dr Dr #10    NaN   
177505    NaN          NaN            1333 Blodgett Ave    NaN   
180596    NaN          NaN         67 Livingston St #11    NaN   
182992    NaN          NaN  96 Schermerhorn St Unit PHK    NaN   
186158    NaN          NaN               2 Sweetner Way    NaN   
204091    NaN          NaN                1215 E 8th St    NaN   
213308    NaN          NaN          67 Livingston St #5    NaN   
221292    NaN          NaN              102 Ferguson Rd    NaN   
259453    NaN          NaN               164 Nichols Rd    NaN   
276493    NaN          NaN           72 Madonna View Dr    NaN   
287600    NaN          NaN            3108 Prospect Ave    NaN   
293290    NaN          NaN          67 Livingston St #4    NaN   
319531    NaN          NaN   96 Schermerhorn St Unit 8H    NaN   
334325    NaN          NaN             45 Greene St #56    NaN   
338725    NaN          NaN              20 Pine St #808    NaN   
350580    NaN          NaN      713 Black Creek Dr #213    NaN   
351828    NaN          NaN          1406 Harvard Ave #1    NaN   
368033    NaN          NaN  4212 Winchester Southern Rd    NaN   
371156    NaN          NaN     790 Riverside Dr Unit 8T    NaN   
372013    NaN          NaN    0 Fall Creek Drive Dr #25    NaN   
376979    NaN          NaN             75 Sophie May Ln    NaN   

                                                homeFacts fireplace  \
3114    {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
12018   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
28624   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
29182   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
34560   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
44949   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
74558   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
92408   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
92854   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
101489  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
117095  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
139731  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
145054  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
154979  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
171841  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
172317  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
177505  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
180596  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
182992  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
186158  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
204091  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
21

In [25]:
df_dd[mask_na].shape

(36, 15)

Принимаю решение удалить строки минимальным для наших данных порогом = 8. Всего таких строк, как мы видим, будет 36.

In [26]:
df_dd_dna = df_dd.dropna(thresh=8)
df_dd_dna.shape

(377008, 15)

С остальными пропусками попробуем поработать.

___

В целевом признаке также есть пропуски. Такие строки не смогут участвовать в построении модели, поэтому я их удалю.
Но предварительно проверю, нет ли дубликатов строк, без признака target.

In [27]:
df_dd_dna.drop('target',axis=1).duplicated().sum() 

np.int64(41)

Видим, что есть такие строки. посмотрим на них.

In [28]:
df_dd_dna[df_dd_dna.drop('target',axis=1).duplicated(keep=False)].sort_values(by='zipcode')

status        propertyType                         street  \
373011       Active  Single Family Home  13410 Canterbury Castle Drive   
298659       Active  Single Family Home  13410 Canterbury Castle Drive   
295483     for sale            lot/land                 Riverside Pkwy   
189772     for sale            lot/land                 Riverside Pkwy   
306014     for sale            lot/land                       E 7th St   
...             ...                 ...                            ...   
162998       Active                 NaN                Unknown Address   
163478       Active                Land                       Shady Ct   
273395       Active                Land                       Shady Ct   
113311  foreclosure  single-family home                   4 Bahama Bnd   
198741  foreclosure  single-family home                   4 Bahama Bnd   

            baths                                          homeFacts  \
373011          3  {'atAGlanceFacts': [{'factValue': '', 'factLab...   
298659          3  {'atAGlanceFacts': [{'factValue': '', 'factLab...   
295483        NaN  {'atAGlanceFacts': [{'factValue': '', 'factLab...   
189772        NaN  {'atAGlanceFacts': [{'factValue': '', 'factLab...   
306014        NaN  {'atAGlanceFacts': [{'factValue': '', 'factLab...   
...           ...                                                ...   
162998        NaN  {'atAGlanceFacts': [{'factValue': '', 'factLab...   
163478        NaN  {'atAGlanceFacts': [{'factValue': '', 'factLab...   
273395        NaN  {'atAGlanceFacts': [{'factValue': '', 'factLab...   
113311  3.5 Baths  {'atAGlanceFacts': [{'factValue': '1974', 'fac...   
198741  3.5 Baths  {'atAGlanceFacts': [{'factValue': '1974', 'fac...   

       fireplace          city  \
373011       NaN     Charlotte   
298659       NaN     Charlotte   
295483       NaN       Atlanta   
189772       NaN       Atlanta   
306014       NaN  Jacksonville   
...          ...           ...   
162998       NaN    Cedar Fort   
163478       NaN      Lakewood   
273395       NaN      Lakewood   
113311       NaN      Coronado   
198741       NaN      Coronado   

                                                  schools        sqft zipcode  \
373011  [{'rating': ['7', '5', '7', '7', '3', '2', 'NR...       2,429   28273   
298659  [{'rating': ['7', '5', '7', '7', '3', '2', 'NR...       2,429   28273   
295483  [{'rating': ['9/10', '6/10', '6/10'], 'data': ...         NaN   30328   
189772  [{'rating': ['9/10', '6/10', '6/10'], 'data': ...         NaN   30328   
306014  [{'rating': ['4/10', '4/10', '6/10'], 'data': ...         NaN   32218   
...                                                   ...         ...     ...   
162998  [{'rating': [], 'data': {'Distance': [], 'Grad...         NaN   84013   
163478  [{'rating': ['4', '3', '2', 'NR', 'NR', 'NR'],...           0    8701   
273395  [{'rating': ['4', '3', '2', 'NR', 'NR', 'NR'],...           0    8701   
113311  [{'rating': ['9/10', '10/10', '8/10'], 'data':...  2,580 sqft   92118   
198741  [{'rating': ['9/10', '10/10', '8/10'], 'data':...  2,580 sqft   92118   

          beds state stories      target   Pool  
373011       3    NC     NaN    $304,999  False  
298659       3    NC     NaN    $306,999  False  
295483     NaN    GA     NaN     $94,900  False  
189772     NaN    GA     NaN    $124,900  False  
306014     NaN    FL     NaN     $25,000  False  
...        ...   ...     ...         ...    ...  
162998     NaN    UT     NaN     310,930  False  
163478     NaN    NJ     NaN    $419,000  False  
273395     NaN    NJ     NaN    $409,000  False  
113311  4 Beds    CA     NaN  $1,664,096  False  
198741  4 Beds    CA     NaN  $1,243,462  False  

[73 rows x 15 columns]

Очень странно, что есть идентичные строки, но отличающиеся только ценой. Как объяснить такое состояние? И не повлияет ли это отрицательным образом на будущую модель?

In [29]:
# тоже, но сохраним изначальную сортировку. Это нам потребуется для сохранения более свежих дублей
test = df_dd_dna[df_dd_dna.drop('target',axis=1).duplicated(keep=False)]
test

status                   propertyType  \
3558         Active             Single Family Home   
4668       for sale                       lot/land   
13989      for sale                       lot/land   
16494   foreclosure             single-family home   
21094        Active                            NaN   
...             ...                            ...   
343052       Active                           Land   
346104       Active  Condo/Townhome/Row Home/Co-Op   
365099       Active                            NaN   
367418       Active             Single Family Home   
373011       Active             Single Family Home   

                               street    baths  \
3558                2651 Daylily Lane        3   
4668                      N Hudson St      NaN   
13989                     N Hudson St      NaN   
16494                4040 Hammerly Dr  3 Baths   
21094                   0 Conklin St       NaN   
...                               ...      ...   
343052                    Magnolia St        0   
346104        224 Autumn Ridge Circle      2.5   
365099                Unknown Address      NaN   
367418                 11305 Gulf Fwy        2   
373011  13410 Canterbury Castle Drive        3   

                                                homeFacts fireplace  \
3558    {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
4668    {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
13989   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
16494   {'atAGlanceFacts': [{'factValue': '2003', 'fac...       yes   
21094   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
...                                                   ...       ...   
343052  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
346104  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
365099  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
367418  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
373011  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   

                city                                            schools  \
3558    Jacksonville  [{'rating': ['7', '4', '5', '9', '3', 'NR', 'N...   
4668         Orlando  [{'rating': ['3/10', '3/10', '7/10', '7/10', '...   
13989        Orlando  [{'rating': ['3/10', '3/10', '7/10', '7/10', '...   
16494         Dallas  [{'rating': ['3/10', '7/10', '3/10'], 'data': ...   
21094        Houston  [{'rating': ['7', '2', '1'], 'data': {'Distanc...   
...              ...                                                ...   
343052     Cleveland  [{'rating': [], 'data': {'Distance': [], 'Grad...   
346104  Pickerington  [{'rating': ['NR', '6', '6', '5', 'NR', 'NR', ...   
365099     Fairfield  [{'rating': [], 'data': {'Distance': [], 'Grad...   
367418       Houston  [{'rating': ['4', '4', '5', '2', '6', '8', 'NR...   
373011     Charlotte  [{'rating': ['7', '5', '7', '7', '3', '2', 'NR...   

              sqft zipcode    beds state stories    target   Pool  
3558         3,512   32226     5.0    FL     NaN  $320,990  False  
4668           NaN   32835     NaN    FL     NaN   $45,900  False  
13989          NaN   32835     NaN    FL     NaN   $42,500  False  
16494   2,033 sqft   75212  4 Beds    TX     NaN       NaN  False  
21094          NaN   77088     NaN    TX     NaN    40,000  False  
...            ...     ...     ...   ...     ...       ...    ...  
343052           0   77328     NaN    TX     NaN   $20,000  False  
346104       1,498   43147     2.0    OH     NaN  $154,990  False  
365099         NaN   84013     NaN    UT     NaN   279,000  False  
367418       1,860   77034     3.0    TX     NaN  $102,000  False  
373011       2,429   28273       3    NC     NaN  $304,999  False  

[73 rows x 15 columns]

Делаем предположение, что подобные записи возникли с течением времени, по причине пересмотра цены на объект. Поэтому логично оставить более свежую информацию. Более свежая соответственно будет та, которая имеет больший индекс, то есть находится ближе к концу таблицы данных.

In [30]:
# из найденных дубликатов сохраним только последний
test2 = test.drop('target',axis=1).drop_duplicates(keep='last')
test2.head()

status        propertyType               street baths  \
13989   for sale            lot/land          N Hudson St   NaN   
85540     Active  Single Family Home    2651 Daylily Lane     3   
114762    Active                Land            SW 151 Pl   NaN   
149449  for sale            lot/land         Mc Laurin Rd   NaN   
156593    Active                 NaN  Undisclosed Address   NaN   

                                                homeFacts fireplace  \
13989   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
85540   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
114762  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
149449  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
156593  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   

                city                                            schools  \
13989        Orlando  [{'rating': ['3/10', '3/10', '7/10', '7/10', '...   
85540   Jacksonville  [{'rating': ['7', '4', '5', '9', '3', 'NR', 'N...   
114762     Dunnellon  [{'rating': ['1', '4', '3', '2', '5', '6'], 'd...   
149449  Jacksonville  [{'rating': ['8/10', '5/10', '6/10'], 'data': ...   
156593  Jacksonville  [{'rating': ['9', '5', '6'], 'data': {'Distanc...   

         sqft zipcode beds state stories   Pool  
13989     NaN   32835  NaN    FL     NaN  False  
85540   3,512   32226  5.0    FL     NaN  False  
114762      0   34432  NaN    FL     NaN  False  
149449    NaN   32256  NaN    FL     NaN  False  
156593    NaN   32224  NaN    FL     NaN  False

In [31]:
# теперь нужно взять разницу индексов
mask_dubl_targ = np.invert(test.index.isin(test2.index))
# test.index[mask_dubl_targ]
# и по этой разнице дропнуть строки
test3 = test.drop(test.index[mask_dubl_targ])
test3.head()

status        propertyType               street baths  \
13989   for sale            lot/land          N Hudson St   NaN   
85540     Active  Single Family Home    2651 Daylily Lane     3   
114762    Active                Land            SW 151 Pl   NaN   
149449  for sale            lot/land         Mc Laurin Rd   NaN   
156593    Active                 NaN  Undisclosed Address   NaN   

                                                homeFacts fireplace  \
13989   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
85540   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
114762  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
149449  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
156593  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   

                city                                            schools  \
13989        Orlando  [{'rating': ['3/10', '3/10', '7/10', '7/10', '...   
85540   Jacksonville  [{'rating': ['7', '4', '5', '9', '3', 'NR', 'N...   
114762     Dunnellon  [{'rating': ['1', '4', '3', '2', '5', '6'], 'd...   
149449  Jacksonville  [{'rating': ['8/10', '5/10', '6/10'], 'data': ...   
156593  Jacksonville  [{'rating': ['9', '5', '6'], 'data': {'Distanc...   

         sqft zipcode beds state stories    target   Pool  
13989     NaN   32835  NaN    FL     NaN   $42,500  False  
85540   3,512   32226  5.0    FL     NaN  $318,990  False  
114762      0   34432  NaN    FL     NaN    $9,500  False  
149449    NaN   32256  NaN    FL     NaN   $49,000  False  
156593    NaN   32224  NaN    FL     NaN   700,000  False

In [32]:
# на сколько уменьшилось строк
test.shape[0] - test3.shape[0]

41

In [33]:
# На тестовой выборке все прошло успешно. Значит можно применить данный фильтр для всей базы
df_v1 = df_dd_dna.drop(test.index[mask_dubl_targ])

In [34]:
# проверим что количество удаленных строк совпало с тестом
df_dd_dna.shape[0]-df_v1.shape[0]

41

Итого имеем df_v1:
- очищенную от изначальных дубликатов
- преобразованным признаком Pool
- удаленными строками с порогом thresh=8
- удаленными строками дублей по признаку target. Оставив только последние записи.

Кстати можно проверить, аналогичным образом, нет ли дубликатов у остальных признаков...?

In [35]:
# проверим признак status
df_v1[df_v1.drop('status',axis=1).duplicated(keep=False)].sort_values(by='street')

status                   propertyType  \
33192   Under Contract   Showing  Condo/Townhome/Row Home/Co-Op   
228599                    Active  Condo/Townhome/Row Home/Co-Op   
95806   Under Contract   Showing             Single Family Home   
346095                    Active             Single Family Home   
62391                     Active             Single Family Home   
207278                         P             Single Family Home   
102313                    Active                           Land   
301437                   Pending                           Land   

                   street baths  \
33192   1041 E Trinity Ln     1   
228599  1041 E Trinity Ln     1   
95806      227 Oceola Ave   3.5   
346095     227 Oceola Ave   3.5   
62391      437 NE 73rd St     2   
207278     437 NE 73rd St     2   
102313         SW 92th Pl   NaN   
301437         SW 92th Pl   NaN   

                                                homeFacts fireplace  \
33192   {'atAGlanceFacts': [{'factValue': '2019', 'fac...       NaN   
228599  {'atAGlanceFacts': [{'factValue': '2019', 'fac...       NaN   
95806   {'atAGlanceFacts': [{'factValue': '2019', 'fac...         1   
346095  {'atAGlanceFacts': [{'factValue': '2019', 'fac...         1   
62391   {'atAGlanceFacts': [{'factValue': '2019', 'fac...       NaN   
207278  {'atAGlanceFacts': [{'factValue': '2019', 'fac...       NaN   
102313  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
301437  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   

             city                                            schools  sqft  \
33192   Nashville  [{'rating': ['NR', '3', '1', '2', '7', '3', 'N...   547   
228599  Nashville  [{'rating': ['NR', '3', '1', '2', '7', '3', 'N...   547   
95806   Nashville  [{'rating': ['2', '4', '3', '6', '2', 'NR', 'N...  1772   
346095  Nashville  [{'rating': ['2', '4', '3', '6', '2', 'NR', 'N...  1772   
62391     Seattle  [{'rating': ['7', '7', '10', '8', 'NR', 'NR', ...   964   
207278    Seattle  [{'rating': ['7', '7', '10', '8', 'NR', 'NR', ...   964   
102313  Dunnellon  [{'rating': ['3', '5', '3', '3', '5', '6'], 'd...     0   
301437  Dunnellon  [{'rating': ['3', '5', '3', '3', '5', '6'], 'd...     0   

       zipcode beds state stories    target   Pool  
33192    37216  0.0    TN    4.00  $175,967  False  
228599   37216  0.0    TN    4.00  $175,967  False  
95806    37209  3.0    TN    3.00  $450,000  False  
346095   37209  3.0    TN    3.00  $450,000  False  
62391    98115    2    WA     NaN  $674,950  False  
207278   98115    2    WA     NaN  $674,950  False  
102313   34432  NaN    FL     NaN   $13,900  False  
301437   34432  NaN    FL     NaN   $13,900  False

In [36]:
test_v2 = df_v1[df_v1.drop('status',axis=1).duplicated(keep=False)]

Аналогично делаю предположение, если для одного и того же объекта есть идентичные записи с разным статусом, то это связано с обновлением статуса с течением времени, но старую запись не удалили. Поэтому оставим только последнюю запись, как самую актуальную.

In [37]:
df_v1[df_v1.drop('status',axis=1).duplicated(keep=False)]

status                   propertyType  \
33192   Under Contract   Showing  Condo/Townhome/Row Home/Co-Op   
62391                     Active             Single Family Home   
95806   Under Contract   Showing             Single Family Home   
102313                    Active                           Land   
207278                         P             Single Family Home   
228599                    Active  Condo/Townhome/Row Home/Co-Op   
301437                   Pending                           Land   
346095                    Active             Single Family Home   

                   street baths  \
33192   1041 E Trinity Ln     1   
62391      437 NE 73rd St     2   
95806      227 Oceola Ave   3.5   
102313         SW 92th Pl   NaN   
207278     437 NE 73rd St     2   
228599  1041 E Trinity Ln     1   
301437         SW 92th Pl   NaN   
346095     227 Oceola Ave   3.5   

                                                homeFacts fireplace  \
33192   {'atAGlanceFacts': [{'factValue': '2019', 'fac...       NaN   
62391   {'atAGlanceFacts': [{'factValue': '2019', 'fac...       NaN   
95806   {'atAGlanceFacts': [{'factValue': '2019', 'fac...         1   
102313  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
207278  {'atAGlanceFacts': [{'factValue': '2019', 'fac...       NaN   
228599  {'atAGlanceFacts': [{'factValue': '2019', 'fac...       NaN   
301437  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
346095  {'atAGlanceFacts': [{'factValue': '2019', 'fac...         1   

             city                                            schools  sqft  \
33192   Nashville  [{'rating': ['NR', '3', '1', '2', '7', '3', 'N...   547   
62391     Seattle  [{'rating': ['7', '7', '10', '8', 'NR', 'NR', ...   964   
95806   Nashville  [{'rating': ['2', '4', '3', '6', '2', 'NR', 'N...  1772   
102313  Dunnellon  [{'rating': ['3', '5', '3', '3', '5', '6'], 'd...     0   
207278    Seattle  [{'rating': ['7', '7', '10', '8', 'NR', 'NR', ...   964   
228599  Nashville  [{'rating': ['NR', '3', '1', '2', '7', '3', 'N...   547   
301437  Dunnellon  [{'rating': ['3', '5', '3', '3', '5', '6'], 'd...     0   
346095  Nashville  [{'rating': ['2', '4', '3', '6', '2', 'NR', 'N...  1772   

       zipcode beds state stories    target   Pool  
33192    37216  0.0    TN    4.00  $175,967  False  
62391    98115    2    WA     NaN  $674,950  False  
95806    37209  3.0    TN    3.00  $450,000  False  
102313   34432  NaN    FL     NaN   $13,900  False  
207278   98115    2    WA     NaN  $674,950  False  
228599   37216  0.0    TN    4.00  $175,967  False  
301437   34432  NaN    FL     NaN   $13,900  False  
346095   37209  3.0    TN    3.00  $450,000  False

In [38]:
# индексы всех дублей
df_v1[df_v1.drop('status',axis=1).duplicated(keep=False)].index

Index([33192, 62391, 95806, 102313, 207278, 228599, 301437, 346095], dtype='int64')

In [39]:
ind_all_v2 = df_v1[df_v1.drop('status',axis=1).duplicated(keep=False)].index

In [40]:
df_v1[df_v1.drop('status',axis=1).duplicated(keep=False)].drop('status',axis=1).drop_duplicates(keep='last')

propertyType             street baths  \
207278             Single Family Home     437 NE 73rd St     2   
228599  Condo/Townhome/Row Home/Co-Op  1041 E Trinity Ln     1   
301437                           Land         SW 92th Pl   NaN   
346095             Single Family Home     227 Oceola Ave   3.5   

                                                homeFacts fireplace  \
207278  {'atAGlanceFacts': [{'factValue': '2019', 'fac...       NaN   
228599  {'atAGlanceFacts': [{'factValue': '2019', 'fac...       NaN   
301437  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
346095  {'atAGlanceFacts': [{'factValue': '2019', 'fac...         1   

             city                                            schools  sqft  \
207278    Seattle  [{'rating': ['7', '7', '10', '8', 'NR', 'NR', ...   964   
228599  Nashville  [{'rating': ['NR', '3', '1', '2', '7', '3', 'N...   547   
301437  Dunnellon  [{'rating': ['3', '5', '3', '3', '5', '6'], 'd...     0   
346095  Nashville  [{'rating': ['2', '4', '3', '6', '2', 'NR', 'N...  1772   

       zipcode beds state stories    target   Pool  
207278   98115    2    WA     NaN  $674,950  False  
228599   37216  0.0    TN    4.00  $175,967  False  
301437   34432  NaN    FL     NaN   $13,900  False  
346095   37209  3.0    TN    3.00  $450,000  False

In [41]:
# индексы только более свежих записей из дублей
df_v1[df_v1.drop('status',axis=1).duplicated(keep=False)].drop('status',axis=1).drop_duplicates(keep='last').index

Index([207278, 228599, 301437, 346095], dtype='int64')

In [42]:
ind_new_v2 = df_v1[df_v1.drop('status',axis=1).duplicated(keep=False)].drop('status',axis=1).drop_duplicates(keep='last').index

In [43]:
# теперь нужно взять разницу индексов
mask_ind_diff_v2 = np.invert(ind_all_v2.isin(ind_new_v2))

In [44]:
# применим фильтр
df_v2 = df_v1.drop(test_v2.index[mask_ind_diff_v2])

In [45]:
# проверим. должно уменьшится на 4
df_v1.shape[0]-df_v2.shape[0]

4

Итого имеем df_v2:

- очищенную от изначальных дубликатов
- преобразованным признаком Pool
- удаленными строками с порогом thresh=8
- удаленными строками дублей по признакам: target, status. Оставив только последние записи.


In [46]:
# проверим признак propertyType

In [47]:
df_v2[df_v2.drop('propertyType',axis=1).duplicated(keep=False)].sort_values(by='street')

status        propertyType           street baths  \
288299  for sale            lot/land  Nna E Pomona Rd   NaN   
361576  for sale  single-family home  Nna E Pomona Rd   NaN   
260800  for sale            lot/land    US Highway 59   NaN   
318125  for sale  single-family home    US Highway 59   NaN   

                                                homeFacts fireplace    city  \
288299  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN  Yakima   
361576  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN  Yakima   
260800  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN  Laredo   
318125  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN  Laredo   

                                                  schools sqft zipcode beds  \
288299  [{'rating': ['None/10', '4/10', 'None/10', 'No...  NaN   98901  NaN   
361576  [{'rating': ['None/10', '4/10', 'None/10', 'No...  NaN   98901  NaN   
260800  [{'rating': ['6/10', '4/10', '5/10'], 'data': ...  NaN   78041  NaN   
318125  [{'rating': ['6/10', '4/10', '5/10'], 'data': ...  NaN   78041  NaN   

       state stories    target   Pool  
288299    WA     NaN  $676,800  False  
361576    WA     NaN  $676,800  False  
260800    TX     NaN   $20,000  False  
318125    TX     NaN   $20,000  False

Делаем аналогичное предположение, что признак был обновлен с течением времени. Предпримем такие же алгоритмы

In [48]:
test_v3 = df_v2[df_v2.drop('propertyType',axis=1).duplicated(keep=False)]

In [49]:
# индексы всех дублей
ind_all_v3 = df_v2[df_v2.drop('propertyType',axis=1).duplicated(keep=False)].index

In [50]:
# индексы только более свежих записей из дублей
ind_new_v3 = df_v2[df_v2.drop('propertyType',axis=1).duplicated(keep=False)].drop('propertyType',axis=1).drop_duplicates(keep='last').index

In [51]:
# разница индексов
mask_ind_diff_v3 = np.invert(ind_all_v3.isin(ind_new_v3))

In [52]:
# применим фильтр
df_v3 = df_v2.drop(test_v3.index[mask_ind_diff_v3])

можно немного упростить код, не сохранять переменную test_v3. В дальнейшем так и буду делать.

In [53]:
df_v3a = df_v2.drop(ind_all_v3[mask_ind_diff_v3])

In [54]:
df_v3a.equals(df_v3)

True

Итого имеем df_v3:

- очищенную от изначальных дубликатов
- преобразованным признаком Pool
- удаленными строками с порогом thresh=8
- удаленными строками дублей по признакам: target, status, propertyType. Оставив только последние записи.


In [55]:
# проверим признак street
df_v3[df_v3.drop('street',axis=1).duplicated(keep=False)].sort_values(by='zipcode')

status   propertyType                      street         baths  \
349242  For sale          Condo           389 Centre St # 2           1.0   
207121  For sale          Condo           389 Centre St # 1           1.0   
63625     Active            NaN     Lot 12 N North Cove Dr            NaN   
234556    Active            NaN  Lot J Madeline Estates Dr            NaN   
86526     Active            NaN          Lot 13 Jacques Ln            NaN   
...          ...            ...                         ...           ...   
211820  For sale          Condo  1166 S Harrison St # LOT22  Bathrooms: 2   
23597   For sale  Single Family          1161 S Harrison St  Bathrooms: 2   
90680   for sale       lot/land              5 Ridgeview Ln           NaN   
231487  for sale       lot/land              4 Ridgeview Ln           NaN   
53556   For sale          Condo  1148 S Harrison St # LOT19  Bathrooms: 2   

                                                homeFacts fireplace  \
349242  {'atAGlanceFacts': [{'factValue': '1927', 'fac...       NaN   
207121  {'atAGlanceFacts': [{'factValue': '1927', 'fac...       NaN   
63625   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
234556  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
86526   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
...                                                   ...       ...   
211820  {'atAGlanceFacts': [{'factValue': '2019', 'fac...       NaN   
23597   {'atAGlanceFacts': [{'factValue': '2019', 'fac...       NaN   
90680   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
231487  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
53556   {'atAGlanceFacts': [{'factValue': '2019', 'fac...       NaN   

              city                                            schools  \
349242  Dorchester  [{'rating': ['4/10', '1/10'], 'data': {'Distan...   
207121  Dorchester  [{'rating': ['4/10', '1/10'], 'data': {'Distan...   
63625         Rome  [{'rating': [], 'data': {'Distance': [], 'Grad...   
234556     Oakland  [{'rating': [], 'data': {'Distance': [], 'Grad...   
86526      Oakland  [{'rating': [], 'data': {'Distance': [], 'Grad...   
...            ...                                                ...   
211820   Kennewick  [{'rating': ['4/10', '2/10', '7/10'], 'data': ...   
23597    Kennewick  [{'rating': ['6/10', '2/10', '4/10'], 'data': ...   
90680    Kennewick  [{'rating': ['7/10', '5/10', '9/10'], 'data': ...   
231487   Kennewick  [{'rating': ['7/10', '5/10', '9/10'], 'data': ...   
53556    Kennewick  [{'rating': ['4/10', '2/10', '7/10'], 'data': ...   

                                           sqft zipcode  beds state stories  \
349242                                    1,025   02122     3    MA     NaN   
207121                                    1,025   02122     3    MA     NaN   
63625                                       NaN   04963   NaN    ME     NaN   
234556                                      NaN   04963   NaN    ME     NaN   
86526                                       NaN   04963   NaN    ME     NaN   
...                                         ...     ...   ...   ...     ...   
211820  Total interior livable area: 1,173 sqft   99338  3 bd    WA     NaN   
23597   Total interior livable area: 1,173 sqft   99338  3 bd    WA     NaN   
90680                                       NaN   99338   NaN    WA     NaN   
231487                                      NaN   99338   NaN    WA     NaN   
53556   Total interior livable area: 1,173 sqft   99338  3 bd    WA     NaN   

          target   Pool  
349242  $439,900  False  
207121  $439,900  False  
63625    184,000  False  
234556    19,500  False  
86526     29,900  False  
...          ...    ...  
211820  $124,599  False  
23597   $124,599  False  
90680   $220,000  False  
231487  $220,000  False  
53556   $124,599  False  

[3868 rows x 15 columns]

Тут предположения аналогичные предыдущим сделать нельзя. Во-первых вряд-ли адрес объекта может измениться. Во-вторых данных получилось очень много, но это из-за того, что признак адреса является полным адресом включая квартиру, если это многоквартирный дом или например номер участка земли. Тогда соседние объекты вполне могут быть полностью идентичны по остальным показателям, например две квартиры в одном доме или два соседних участка земли.  
Поэтому оставим без изменений

In [56]:
# проверим признак baths
df_v3[df_v3.drop('baths',axis=1).duplicated(keep=False)].sort_values(by='zipcode')

Empty DataFrame
Columns: [status, propertyType, street, baths, homeFacts, fireplace, city, schools, sqft, zipcode, beds, state, stories, target, Pool]
Index: []

Совпадений нет

In [57]:
# проверим признак homeFacts
df_v3[df_v3.drop('homeFacts',axis=1).duplicated(keep=False)].sort_values(by='zipcode')

status   propertyType                 street    baths  \
104788    Active            NaN           Young St SE     1,500   
125457    Active            NaN           Young St SE     1,500   
137850  for sale          condo  100 Lovejoy Wharf #3B  2 Baths   
261373  for sale          condo  100 Lovejoy Wharf #3B  2 Baths   
372703    Active           Land         N Carolina Cir      NaN   
...          ...            ...                    ...      ...   
292262  for sale       lot/land                183xx E      NaN   
147663  For sale  Single Family  (undisclosed Address)      2.0   
239717  For sale  Single Family  (undisclosed Address)      2.0   
270710  for sale       lot/land            N Hazard Rd      NaN   
38833   for sale       lot/land            N Hazard Rd      NaN   

                                                homeFacts fireplace  \
104788  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
125457  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
137850  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
261373  {'atAGlanceFacts': [{'factValue': '2017', 'fac...       NaN   
372703  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
...                                                   ...       ...   
292262  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
147663  {'atAGlanceFacts': [{'factValue': '1961', 'fac...       NaN   
239717  {'atAGlanceFacts': [{'factValue': '1961', 'fac...       NaN   
270710  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
38833   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   

              city                                            schools  \
104788  Washington  [{'rating': ['4', '1', '1'], 'data': {'Distanc...   
125457  Washington  [{'rating': ['4', '1', '1'], 'data': {'Distanc...   
137850      Boston  [{'rating': [], 'data': {'Distance': [], 'Grad...   
261373      Boston  [{'rating': [], 'data': {'Distance': [], 'Grad...   
372703  Mocksville  [{'rating': ['6', '4', '4', '10', 'NR', 'NR'],...   
...            ...                                                ...   
292262      Renton  [{'rating': ['8/10', '7/10', '6/10'], 'data': ...   
147663  Marysville  [{'rating': ['4/10', '2/10', '1/10'], 'data': ...   
239717  Marysville  [{'rating': ['4/10', '2/10', '1/10'], 'data': ...   
270710     Spokane  [{'rating': ['7/10', '7/10', '8/10', 'None/10'...   
38833      Spokane  [{'rating': ['7/10', '7/10', '8/10', 'None/10'...   

              sqft zipcode    beds state stories      target   Pool  
104788         NaN   20020   Baths    DC     NaN     235,000  False  
125457         NaN   20020   Baths    DC     NaN     235,000  False  
137850  1,256 sqft    2114  2 Beds    MA     1.0  $1,299,000  False  
261373  1,256 sqft    2114  2 Beds    MA     1.0  $1,299,000  False  
372703           0   27028     NaN    NC     NaN     $42,000  False  
...            ...     ...     ...   ...     ...         ...    ...  
292262         NaN   98058     NaN    WA     NaN    $200,000  False  
147663       2,761   98270       6    WA     NaN    $650,000  False  
239717       2,761   98270       6    WA     NaN    $650,000  False  
270710         NaN   99208     NaN    WA     NaN    $105,000  False  
38833          NaN   99208     NaN    WA     NaN    $105,000  False  

[148 rows x 15 columns]

In [58]:
# посмотрим на признаки дубликатов:
df_v3[df_v3.drop('homeFacts',axis=1).duplicated(keep=False)].sort_values(by='zipcode')['homeFacts'][104788]

"{'atAGlanceFacts': [{'factValue': '', 'factLabel': 'Year built'}, {'factValue': '', 'factLabel': 'Remodeled year'}, {'factValue': '', 'factLabel': 'Heating'}, {'factValue': '', 'factLabel': 'Cooling'}, {'factValue': '', 'factLabel': 'Parking'}, {'factValue': '3,030 Sq. Ft.', 'factLabel': 'lotsize'}, {'factValue': None, 'factLabel': 'Price/sqft'}]}"

In [59]:
df_v3[df_v3.drop('homeFacts',axis=1).duplicated(keep=False)].sort_values(by='zipcode')['homeFacts'][125457]

"{'atAGlanceFacts': [{'factValue': '', 'factLabel': 'Year built'}, {'factValue': '', 'factLabel': 'Remodeled year'}, {'factValue': '', 'factLabel': 'Heating'}, {'factValue': '', 'factLabel': 'Cooling'}, {'factValue': '', 'factLabel': 'Parking'}, {'factValue': '2,758 Sq. Ft.', 'factLabel': 'lotsize'}, {'factValue': None, 'factLabel': 'Price/sqft'}]}"

тут изменилась общая площадь. Такое вполне может быть. Либо уточнение, либо повлияли какие-то реконструкции дома

In [60]:
# посмротрим еще одну пару дубликатов:
df_v3[df_v3.drop('homeFacts',axis=1).duplicated(keep=False)].sort_values(by='zipcode')['homeFacts'][147663]

"{'atAGlanceFacts': [{'factValue': '1961', 'factLabel': 'Year built'}, {'factValue': None, 'factLabel': 'Remodeled year'}, {'factValue': 'Forced air', 'factLabel': 'Heating'}, {'factValue': 'No Data', 'factLabel': 'Cooling'}, {'factValue': 'Off street', 'factLabel': 'Parking'}, {'factValue': '0.43 acres', 'factLabel': 'lotsize'}, {'factValue': '$235', 'factLabel': 'Price/sqft'}]}"

In [61]:
df_v3[df_v3.drop('homeFacts',axis=1).duplicated(keep=False)].sort_values(by='zipcode')['homeFacts'][239717]

"{'atAGlanceFacts': [{'factValue': '1961', 'factLabel': 'Year built'}, {'factValue': None, 'factLabel': 'Remodeled year'}, {'factValue': 'No Data', 'factLabel': 'Heating'}, {'factValue': 'No Data', 'factLabel': 'Cooling'}, {'factValue': 'No Data', 'factLabel': 'Parking'}, {'factValue': '0.43 acres', 'factLabel': 'lotsize'}, {'factValue': '$235', 'factLabel': 'Price/sqft'}]}"

Тут в более свежей записи исчезла система отопления...хм...Также исчезла парковка...Но в этих дублях не определен адрес. Вполне возможно, что это два соседних дома.

In [62]:
# посмротрим еще одну пару дубликатов:
df_v3[df_v3.drop('homeFacts',axis=1).duplicated(keep=False)].sort_values(by='zipcode')['homeFacts'][137850]

"{'atAGlanceFacts': [{'factValue': '', 'factLabel': 'Year built'}, {'factValue': '', 'factLabel': 'Remodeled year'}, {'factValue': '', 'factLabel': 'Heating'}, {'factValue': '', 'factLabel': 'Cooling'}, {'factValue': '', 'factLabel': 'Parking'}, {'factValue': '', 'factLabel': 'lotsize'}, {'factValue': '$1,034/sqft', 'factLabel': 'Price/sqft'}]}"

In [63]:
df_v3[df_v3.drop('homeFacts',axis=1).duplicated(keep=False)].sort_values(by='zipcode')['homeFacts'][261373]

"{'atAGlanceFacts': [{'factValue': '2017', 'factLabel': 'Year built'}, {'factValue': '', 'factLabel': 'Remodeled year'}, {'factValue': 'Forced Air', 'factLabel': 'Heating'}, {'factValue': 'Central', 'factLabel': 'Cooling'}, {'factValue': 'Off Street', 'factLabel': 'Parking'}, {'factValue': '', 'factLabel': 'lotsize'}, {'factValue': '$1,034/sqft', 'factLabel': 'Price/sqft'}]}"

В этих дублях в более свежей записи добавились признаки, которых не было в более старой записи.  

Делаю вывод: можно применить аналогичный алгоритм очистки. Сделаю это.

In [64]:
# индексы всех дублей
ind_all_v4 = df_v3[df_v3.drop('homeFacts',axis=1).duplicated(keep=False)].index
# индексы только более свежих записей из дублей
ind_new_v4 = df_v3[df_v3.drop('homeFacts',axis=1).duplicated(keep=False)].drop('homeFacts',axis=1).drop_duplicates(keep='last').index
# разница индексов
mask_ind_diff_v4 = np.invert(ind_all_v4.isin(ind_new_v4))
# применим фильтр
df_v4 = df_v3.drop(ind_all_v4[mask_ind_diff_v4])

In [65]:
df_v3.shape[0]-df_v4.shape[0]

77

In [66]:
# проверим признак fireplace
df_v4[df_v4.drop('fireplace',axis=1).duplicated(keep=False)].sort_values(by='zipcode')

Empty DataFrame
Columns: [status, propertyType, street, baths, homeFacts, fireplace, city, schools, sqft, zipcode, beds, state, stories, target, Pool]
Index: []

Совпадений нет

In [67]:
# проверим признак city
df_v4[df_v4.drop('city',axis=1).duplicated(keep=False)].sort_values(by='zipcode')

status propertyType                  street baths  \
135276  for sale        condo      2216 79th St #2-1C   NaN   
170456  for sale        condo      2216 79th St #2-1C   NaN   
52244   for sale     lot/land  14520 Bill Newkirk Way   NaN   
252936  for sale     lot/land  14520 Bill Newkirk Way   NaN   
258799    Active         Land    Wild Horse Valley Rd   NaN   
355337    Active         Land    Wild Horse Valley Rd   NaN   

                                                homeFacts fireplace  \
135276  {'atAGlanceFacts': [{'factValue': '1948', 'fac...       NaN   
170456  {'atAGlanceFacts': [{'factValue': '1948', 'fac...       NaN   
52244   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
252936  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
258799  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
355337  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   

                 city                                            schools  \
135276       Flushing  [{'rating': ['3/10', '3/10', '8/10', '8/10'], ...   
170456  East Elmhurst  [{'rating': ['3/10', '3/10', '8/10', '8/10'], ...   
52244    Horizon City  [{'rating': ['4/10', '6/10', '3/10'], 'data': ...   
252936        Horizon  [{'rating': ['4/10', '6/10', '3/10'], 'data': ...   
258799      Fairfield  [{'rating': ['9', '8', '6', 'NR', 'NR', 'NR', ...   
355337           Napa  [{'rating': ['9', '8', '6', 'NR', 'NR', 'NR', ...   

            sqft zipcode beds state stories      target   Pool  
135276  420 sqft   11370  NaN    NY     NaN    $329,000  False  
170456  420 sqft   11370  NaN    NY     NaN    $329,000  False  
52244        NaN   79928  NaN    TX     NaN    $395,000  False  
252936       NaN   79928  NaN    TX     NaN    $395,000  False  
258799         0   94533  NaN    CA     NaN  $1,175,000  False  
355337         0   94533  NaN    CA     NaN  $1,175,000  False

Тут достаточно понятно. Данные дубли образовались по причине нахождения объектов между двумя прилегающими территориями. Видимо по этой причине объект причисляется то к одному, то к другому городу. Но это один и тот же объект. Поэтому удаляем дубли аналогичным образом.

In [68]:
# индексы всех дублей
ind_all_v5 = df_v4[df_v4.drop('city',axis=1).duplicated(keep=False)].index
# индексы только более свежих записей из дублей
ind_new_v5 = df_v4[df_v4.drop('city',axis=1).duplicated(keep=False)].drop('city',axis=1).drop_duplicates(keep='last').index
# разница индексов
mask_ind_diff_v5 = np.invert(ind_all_v5.isin(ind_new_v5))
# применим фильтр
df_v5 = df_v4.drop(ind_all_v5[mask_ind_diff_v5])

In [69]:
df_v4.shape[0]-df_v5.shape[0]

3

In [70]:
# проверим признак schools
df_v5[df_v5.drop('schools',axis=1).duplicated(keep=False)].sort_values(by='street')

status propertyType             street  baths  \
353213    Active          NaN         0 FM 1937     NaN   
197268    Active          NaN         0 FM 1937     NaN   
58385     Active          NaN  0 Splashing Rock   4,000   
283413    Active          NaN  0 Splashing Rock   4,000   
227391    Active          NaN  0 Splashing Rock   4,000   
...          ...          ...                ...    ...   
99214   for sale     lot/land    Whippoorwill Dr    NaN   
230499    Active         Land           White St    NaN   
274202    Active         Land           White St    NaN   
325523    Active         Land   Wilson Way Lot 1    NaN   
53936     Active         Land   Wilson Way Lot 1    NaN   

                                                homeFacts fireplace  \
353213  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
197268  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
58385   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
283413  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
227391  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
...                                                   ...       ...   
99214   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
230499  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
274202  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
325523  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
53936   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   

               city                                            schools   sqft  \
353213  San Antonio  [{'rating': ['NR', '4', 'NR', 'NR', '3'], 'dat...    NaN   
197268  San Antonio  [{'rating': ['NR', '4', 'NR', 'NR', '3'], 'dat...    NaN   
58385   San Antonio  [{'rating': ['8', 'NR', '10', '10', '8'], 'dat...  7,426   
283413  San Antonio  [{'rating': ['8', 'NR', '10', '10', '8'], 'dat...  7,426   
227391  San Antonio  [{'rating': ['8', 'NR', '10', '10', '8'], 'dat...  7,426   
...             ...                                                ...    ...   
99214    Palm Coast  [{'rating': ['4/10', '5/10', '4/10'], 'data': ...    NaN   
230499     Lakewood  [{'rating': ['4', '3', '2', 'NR', 'NR', 'NR'],...      0   
274202     Lakewood  [{'rating': ['4', '3', '2', 'NR', 'NR', 'NR'],...      0   
325523    Cleveland  [{'rating': ['6', '5', '8', '7', '5', '7', 'NR...      0   
53936     Cleveland  [{'rating': [], 'data': {'Distance': [], 'Grad...      0   

       zipcode   beds state stories    target   Pool  
353213   78221    NaN    TX     NaN    35,000  False  
197268   78221    NaN    TX     NaN    35,000  False  
58385    78260  Baths    TX     NaN    50,000  False  
283413   78260  Baths    TX     NaN    50,000  False  
227391   78260  Baths    TX     NaN    50,000  False  
...        ...    ...   ...     ...       ...    ...  
99214    32164    NaN    FL     NaN  $549,000  False  
230499    8701    NaN    NJ     NaN  $687,500  False  
274202    8701    NaN    NJ     NaN  $687,500  False  
325523   37312    NaN    TN     NaN   $31,500  False  
53936    37312    NaN    TN     NaN   $31,500  False  

[168 rows x 15 columns]

In [71]:
# посмротрим пару дубликатов:
df_v5[df_v5.drop('schools',axis=1).duplicated(keep=False)].sort_values(by='street')['schools'][53936]

"[{'rating': [], 'data': {'Distance': [], 'Grades': []}, 'name': []}]"

In [72]:
df_v5[df_v5.drop('schools',axis=1).duplicated(keep=False)].sort_values(by='street')['schools'][325523]

"[{'rating': ['6', '5', '8', '7', '5', '7', 'NR', 'NR'], 'data': {'Distance': ['2.6 mi', '7.0 mi', '1.7 mi', '4.3 mi', '6.2 mi', '7.4 mi', '3.1 mi', '3.1 mi'], 'Grades': ['PK–5', '6–8', '9–12', 'PK–5', 'K–12', '3–12', '6–12', 'PK–5']}, 'name': ['Charleston Elementary School', 'Ocoee Middle School', 'Walker Valley High School', 'North Lee Elementary School', 'N. Cleveland Goal Academy School', 'Bradley County Virtual School', 'Advent Home Learning Center Private School', 'Montessori Kinder Private School']}]"

In [73]:
# посмротрим еще пару дубликатов (тут даже три получилось):
df_v5[df_v5.drop('schools',axis=1).duplicated(keep=False)].sort_values(by='street')['schools'][58385]

"[{'rating': ['8', 'NR', '10', '10', '8'], 'data': {'Distance': ['1.1 mi', '1.4 mi', '2.3 mi', '3.3 mi', '10.9 mi'], 'Grades': ['Preschool to 5', 'Preschool to 12', '6 to 8', '6 to 8', '9 to 12']}, 'name': ['Mh Specht Elementary School', 'Buckner Fanning School At Mission Springs', 'Lopez Middle School', 'Bush Middle School', 'Smithson Valley High School']}]"

In [74]:
df_v5[df_v5.drop('schools',axis=1).duplicated(keep=False)].sort_values(by='street')['schools'][283413]

"[{'rating': ['8', 'NR', '10', '10', '8'], 'data': {'Distance': ['1.1 mi', '1.3 mi', '2.3 mi', '3.3 mi', '10.9 mi'], 'Grades': ['Preschool to 5', 'Preschool to 12', '6 to 8', '6 to 8', '9 to 12']}, 'name': ['Mh Specht Elementary School', 'Buckner Fanning School At Mission Springs', 'Lopez Middle School', 'Bush Middle School', 'Smithson Valley High School']}]"

In [75]:
df_v5[df_v5.drop('schools',axis=1).duplicated(keep=False)].sort_values(by='street')['schools'][227391]

"[{'rating': ['8', 'NR', '10', '10', '8'], 'data': {'Distance': ['1.1 mi', '1.3 mi', '2.2 mi', '3.3 mi', '10.9 mi'], 'Grades': ['Preschool to 5', 'Preschool to 12', '6 to 8', '6 to 8', '9 to 12']}, 'name': ['Mh Specht Elementary School', 'Buckner Fanning School At Mission Springs', 'Lopez Middle School', 'Bush Middle School', 'Smithson Valley High School']}]"

В первом случае более свежая запись заполнена, в то время, как более старая не имеет данных. Во втором случае видим изменения в расстоянии до школы. Все это также укладывается в предположение об обновлении данных с течением времени. Удалим дубли по такому же алгоритму.

In [76]:
# индексы всех дублей
ind_all_v6 = df_v5[df_v5.drop('schools',axis=1).duplicated(keep=False)].index
# индексы только более свежих записей из дублей
ind_new_v6 = df_v5[df_v5.drop('schools',axis=1).duplicated(keep=False)].drop('schools',axis=1).drop_duplicates(keep='last').index
# разница индексов
mask_ind_diff_v6 = np.invert(ind_all_v6.isin(ind_new_v6))
# применим фильтр
df_v6 = df_v5.drop(ind_all_v6[mask_ind_diff_v6])

In [77]:
df_v5.shape[0]-df_v6.shape[0]

90

In [78]:
# проверим признак sqft
df_v6[df_v6.drop('sqft',axis=1).duplicated(keep=False)].sort_values(by='street')

status                   propertyType  \
30481   Active             Single Family Home   
372540  Active             Single Family Home   
29924   Active             Single Family Home   
105619  Active             Single Family Home   
346077  Active  Condo/Townhome/Row Home/Co-Op   
375181  Active  Condo/Townhome/Row Home/Co-Op   
201745  Active             Single Family Home   
215174  Active             Single Family Home   
41423   Active             Single Family Home   
333443  Active             Single Family Home   
108910     NaN                      Townhouse   
168200     NaN                      Townhouse   
93819   Active             Single Family Home   
250351  Active             Single Family Home   

                                  street baths  \
30481                        1 Palmer Dr   3.5   
372540                       1 Palmer Dr   3.5   
29924          3435 Heather Garden Trail     3   
105619         3435 Heather Garden Trail     3   
346077                     500 176th Ave   2.5   
375181                     500 176th Ave   2.5   
201745      7256 SW 62nd Ave.Suite 2-101     2   
215174      7256 SW 62nd Ave.Suite 2-101     2   
41423           8959 Monterey View Drive   2.5   
333443          8959 Monterey View Drive   2.5   
108910  Buildable plan: OAKLEY Baypointe   3.0   
168200  Buildable plan: OAKLEY Baypointe   3.0   
93819      SE 192nd St and  124th Ave SE   3.5   
250351     SE 192nd St and  124th Ave SE   3.5   

                                                homeFacts fireplace  \
30481   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
372540  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
29924   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
105619  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
346077  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
375181  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
201745  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
215174  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
41423   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
333443  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
108910  {'atAGlanceFacts': [{'factValue': '2019', 'fac...       NaN   
168200  {'atAGlanceFacts': [{'factValue': '2019', 'fac...       NaN   
93819   {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
250351  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   

                  city                                            schools  \
30481   Southern Pines  [{'rating': ['NR', '4', '7', '4', '6', '7', 'N...   
372540  Southern Pines  [{'rating': ['NR', '4', '7', '4', '6', '7', 'N...   
29924         Richmond  [{'rating': ['8', '9', '7', 'NR', 'NR', 'NR', ...   
105619        Richmond  [{'rating': ['8', '9', '7', 'NR', 'NR', 'NR', ...   
346077      Broomfield  [{'rating': ['8', '5', '8', '5', '3', '4', 'NR...   
375181      Broomfield  [{'rating': ['8', '5', '8', '5', '3', '4', 'NR...   
201745           Ocala  [{'rating': ['2', '4', '6', '1', '5', '4'], 'd...   
215174           Ocala  [{'rating': ['2', '4', '6', '1', '5', '4'], 'd...   
41423          Houston  [{'rating': ['2', '2', '2', 'NR', '10', '2', '...   
333443         Houston  [{'rating': ['2', '2', '2', 'NR', '10', '2', '...   
108910    Jacksonville  [{'rating': ['4/10', '2/10', '4/10'], 'data': ...   
168200    Jacksonville  [{'rating': ['4/10', '2/10', '4/10'], 'data': ...   
93819           Renton  [{'rating': ['4', '5', '5', '3', '4', 'NR', 'N...   
250351          Renton  [{'rating': ['4', '5', '5', '3', '4', 'NR', 'N...   

         sqft zipcode beds state stories    target   Pool  
30481   3,356   28387    4    NC     NaN  $410,999  False  
372540  3,364   28387    4    NC     NaN  $410,999  False  
29924   3,257   77406  4.0    TX     NaN  $435,900  False  
105619  3,258   77406  4.0    TX     NaN  $435,900  False  

Видим, что у дублей значение признака sqft изменяется на небольшие значения. Видимо со временем внесли корректировки. Применим те же алгоритмы очистки

In [79]:
# индексы всех дублей
ind_all_v7 = df_v6[df_v6.drop('sqft',axis=1).duplicated(keep=False)].index
# индексы только более свежих записей из дублей
ind_new_v7 = df_v6[df_v6.drop('sqft',axis=1).duplicated(keep=False)].drop('sqft',axis=1).drop_duplicates(keep='last').index
# разница индексов
mask_ind_diff_v7 = np.invert(ind_all_v7.isin(ind_new_v7))
# применим фильтр
df_v7 = df_v6.drop(ind_all_v7[mask_ind_diff_v7])

In [80]:
df_v6.shape[0]-df_v7.shape[0]

7

In [81]:
# проверим признак zipcode
df_v7[df_v7.drop('zipcode',axis=1).duplicated(keep=False)].sort_values(by='street')

Empty DataFrame
Columns: [status, propertyType, street, baths, homeFacts, fireplace, city, schools, sqft, zipcode, beds, state, stories, target, Pool]
Index: []

Совпадений нет

In [82]:
# проверим признак beds
df_v7[df_v7.drop('beds',axis=1).duplicated(keep=False)].sort_values(by='street')

status           propertyType           street baths  \
6598        Active     Single Family Home   11305 Gulf Fwy     2   
167968      Active     Single Family Home   11305 Gulf Fwy     2   
279823      Active     Single Family Home   11305 Gulf Fwy     2   
295762      Active     Single Family Home   11305 Gulf Fwy     2   
227429  Foreclosed  SingleFamilyResidence  5435 Boxwood Dr   NaN   
289508  Foreclosed  SingleFamilyResidence  5435 Boxwood Dr   NaN   
140071      Active     Single Family Home   6717 35th St W     2   
295419      Active     Single Family Home   6717 35th St W     2   

                                                homeFacts fireplace  \
6598    {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
167968  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
279823  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
295762  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
227429  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
289508  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
140071  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   
295419  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   

                    city                                            schools  \
6598             Houston  [{'rating': ['4', '4', '5', '2', '6', '8', 'NR...   
167968           Houston  [{'rating': ['4', '4', '5', '2', '6', '8', 'NR...   
279823           Houston  [{'rating': ['4', '4', '5', '2', '6', '8', 'NR...   
295762           Houston  [{'rating': ['4', '4', '5', '2', '6', '8', 'NR...   
227429            Dayton  [{'rating': ['3/10', '3/10'], 'data': {'Distan...   
289508            Dayton  [{'rating': ['3/10', '3/10'], 'data': {'Distan...   
140071  University Place  [{'rating': ['9', '7', '9', '9', '5', 'NR', 'N...   
295419  University Place  [{'rating': ['9', '7', '9', '9', '5', 'NR', 'N...   

         sqft zipcode        beds state stories    target   Pool  
6598    1,476   77034         4.0    TX     NaN   $85,245  False  
167968  1,800   77034         3.0    TX     NaN  $125,000  False  
279823  1,800   77034         4.0    TX     NaN  $125,000  False  
295762  1,476   77034         3.0    TX     NaN   $85,245  False  
227429    NaN   45414     -- sqft    OH     NaN       NaN  False  
289508    NaN   45414  2,614 sqft    OH     NaN       NaN  False  
140071  1,700   98466         3.0    WA     NaN  $592,900  False  
295419  1,700   98466           3    WA     NaN  $592,900  False

Также наблюдаем небольшие изменения. Примнимаем их за корректрировку. Удаляем дубли.

In [83]:
# индексы всех дублей
ind_all_v8 = df_v7[df_v7.drop('beds',axis=1).duplicated(keep=False)].index
# индексы только более свежих записей из дублей
ind_new_v8 = df_v7[df_v7.drop('beds',axis=1).duplicated(keep=False)].drop('beds',axis=1).drop_duplicates(keep='last').index
# разница индексов
mask_ind_diff_v8 = np.invert(ind_all_v8.isin(ind_new_v8))
# применим фильтр
df_v8 = df_v7.drop(ind_all_v8[mask_ind_diff_v8])

In [84]:
df_v7.shape[0]-df_v8.shape[0]

4

In [85]:
# проверим признак state
df_v8[df_v8.drop('state',axis=1).duplicated(keep=False)].sort_values(by='street')

Empty DataFrame
Columns: [status, propertyType, street, baths, homeFacts, fireplace, city, schools, sqft, zipcode, beds, state, stories, target, Pool]
Index: []

Совпадений нет

In [86]:
# проверим признак stories
df_v8[df_v8.drop('stories',axis=1).duplicated(keep=False)].sort_values(by='street')

status        propertyType                     street      baths  \
369326     for sale           townhouse         1107 Devereaux Ave    2 Baths   
347368     for sale           townhouse         1107 Devereaux Ave    2 Baths   
66436      for sale               condo     1255 N Paulina St #109    3 Baths   
195339     for sale               condo     1255 N Paulina St #109    3 Baths   
21095      for sale        multi-family           1270 Herkimer St    3 Baths   
102441     for sale        multi-family           1270 Herkimer St    3 Baths   
348865  foreclosure  single-family home  1328 E Mount Pleasant Ave    2 Baths   
76524   foreclosure  single-family home  1328 E Mount Pleasant Ave    2 Baths   
229562     for sale  single-family home          179 Pine Haven Dr    4 Baths   
97453      for sale  single-family home          179 Pine Haven Dr    4 Baths   
239128     for sale  single-family home             2125 Danner St    2 Baths   
104923     for sale  single-family home             2125 Danner St    2 Baths   
352439     for sale           townhouse           2427 Commerce St    3 Baths   
284039     for sale           townhouse           2427 Commerce St    3 Baths   
263301     for sale               condo            245 10th Ave #E    3 Baths   
4137       for sale               condo            245 10th Ave #E    3 Baths   
90231      for sale           townhouse         2493 Skyland Dr NE    4 Baths   
287277     for sale           townhouse         2493 Skyland Dr NE    4 Baths   
289251     for sale  single-family home              257 Argyle Rd    3 Baths   
46752      for sale  single-family home              257 Argyle Rd    3 Baths   
241949     for sale  single-family home       2616 Riverside Dr #E    4 Baths   
201271     for sale  single-family home       2616 Riverside Dr #E    4 Baths   
24241      for sale               condo      2930 N Lincoln Ave #1    2 Baths   
286167     for sale               condo      2930 N Lincoln Ave #1    2 Baths   
78571      for sale  single-family home        3726 1/2 Vinton Ave    4 Baths   
281896     for sale  single-family home        3726 1/2 Vinton Ave    4 Baths   
135964     for sale  single-family home          4188 Gallimore St        NaN   
362195     for sale  single-family home          4188 Gallimore St        NaN   
315492     for sale           townhouse             4202 3rd St NW    2 Baths   
268396     for sale           townhouse             4202 3rd St NW    2 Baths   
20241      for sale  single-family home       4709 Saint Thomas Pl    2 Baths   
351123     for sale  single-family home       4709 Saint Thomas Pl    2 Baths   
35167      for sale  single-family home           4808 Bonnell Ave    2 Baths   
187502     for sale  single-family home           4808 Bonnell Ave    2 Baths   
354022     for sale  single-family home            5031 Italica Rd    2 Baths   
273887     for sale  single-family home            5031 Italica Rd    2 Baths   
98829      for sale               condo     5733 N Sheridan Rd #4D    2 Baths   
69347      for sale               condo     5733 N Sheridan Rd #4D    2 Baths   
309923     for sale  single-family home          6193 Jackies Farm    3 Baths   
105877     for sale  single-family home          6193 Jackies Farm    3 Baths   
118846     for sale  single-family home          7003 Advocator Ln  2.5 Baths   
342073     for sale  single-family home          7003 Advocator Ln  2.5 Baths   
332856     for sale  single-family home        7029 Fallbrook Ct E    2 Baths   
24990      for sale  single-family home        7029 Fallbrook Ct E    2 Baths   
122659     for sale  single-family home         7300 Rocky Ford Rd    2 Baths   
274743     for sale  single-family home         7300 Rocky Ford Rd    2 Baths   
90996      for sale           townhouse                 8743 Bryam    3 Baths   
77351      for sale           townhouse                 8743 Bryam    3 Baths   
291532     for sale           townhouse     

Видно, что различия заключаются в изменении числа с дробной частью на целое число. Удаляем дубли.

In [87]:
# индексы всех дублей
ind_all_v9 = df_v8[df_v8.drop('stories',axis=1).duplicated(keep=False)].index
# индексы только более свежих записей из дублей
ind_new_v9 = df_v8[df_v8.drop('stories',axis=1).duplicated(keep=False)].drop('stories',axis=1).drop_duplicates(keep='last').index
# разница индексов
mask_ind_diff_v9 = np.invert(ind_all_v9.isin(ind_new_v9))
# применим фильтр
df_v9 = df_v8.drop(ind_all_v9[mask_ind_diff_v9])

In [88]:
df_v8.shape[0]-df_v9.shape[0]

28

In [89]:
# проверим признак state
df_v9[df_v9.drop('Pool',axis=1).duplicated(keep=False)].sort_values(by='street')

Empty DataFrame
Columns: [status, propertyType, street, baths, homeFacts, fireplace, city, schools, sqft, zipcode, beds, state, stories, target, Pool]
Index: []

Совпадений нет

___

In [90]:
# сохраним
df_v9.to_pickle("df_v9.pkl")

In [91]:
# считаем
df_v9 = pd.read_pickle("df_v9.pkl")  

In [92]:
df_v9

status        propertyType                    street    baths  \
0         Active  Single Family Home            240 Heather Ln      3.5   
1       for sale  single-family home         12911 E Heroy Ave  3 Baths   
2       for sale  single-family home         2005 Westridge Rd  2 Baths   
3       for sale  single-family home       4311 Livingston Ave  8 Baths   
4       for sale            lot/land            1524 Kiscoe St      NaN   
...          ...                 ...                       ...      ...   
377039       NaN       Single Family         20800 NE 23rd Ave      6.0   
377040  for sale               condo  3530 N Lake Shore Dr #4B  3 Baths   
377041  for sale  single-family home         15509 Linden Blvd  3 Baths   
377042       NaN                 NaN           7810 Pereida St      NaN   
377043       NaN       Single Family          5983 Midcrown Dr      2.0   

                                                homeFacts       fireplace  \
0       {'atAGlanceFacts': [{'factValue': '2019', 'fac...        Gas Logs   
1       {'atAGlanceFacts': [{'factValue': '2019', 'fac...             NaN   
2       {'atAGlanceFacts': [{'factValue': '1961', 'fac...             yes   
3       {'atAGlanceFacts': [{'factValue': '2006', 'fac...             yes   
4       {'atAGlanceFacts': [{'factValue': '', 'factLab...             NaN   
...                                                   ...             ...   
377039  {'atAGlanceFacts': [{'factValue': '1990', 'fac...             NaN   
377040  {'atAGlanceFacts': [{'factValue': '1924', 'fac...             NaN   
377041  {'atAGlanceFacts': [{'factValue': '1950', 'fac...             NaN   
377042  {'atAGlanceFacts': [{'factValue': None, 'factL...             NaN   
377043  {'atAGlanceFacts': [{'factValue': '2019', 'fac...  Not Applicable   

                  city                                            schools  \
0       Southern Pines  [{'rating': ['4', '4', '7', 'NR', '4', '7', 'N...   
1       Spokane Valley  [{'rating': ['4/10', 'None/10', '4/10'], 'data...   
2          Los Angeles  [{'rating': ['8/10', '4/10', '8/10'], 'data': ...   
3               Dallas  [{'rating': ['9/10', '9/10', '10/10', '9/10'],...   
4             Palm Bay  [{'rating': ['4/10', '5/10', '5/10'], 'data': ...   
...                ...                                                ...   
377039           Miami  [{'rating': ['10/10', '5/10'], 'data': {'Dista...   
377040         Chicago  [{'rating': ['1/10', '5/10', '7/10'], 'data': ...   
377041         Jamaica  [{'rating': ['5/10', '4/10'], 'data': {'Distan...   
377042         Houston  [{'rating': ['NA', 'NA', 'NA'], 'data': {'Dist...   
377043     San Antonio  [{'rating': ['5/10', '4/10', '3/10'], 'data': ...   

              sqft zipcode        beds state stories      target   Pool  
0             2900   28387           4    NC     NaN    $418,000  False  
1       1,947 sqft   99216      3 Beds    WA     2.0    $310,000  False  
2       3,000 sqft   90049      3 Beds    CA     1.0  $2,895,000   True  
3       6,457 sqft   75205      5 Beds    TX     3.0  $2,395,000  False  
4              NaN   32908         NaN    FL     NaN      $5,000  False  
...            ...     ...         ...   ...     ...         ...    ...  
377039       4,017   33180           5    FL     0.0  $1,249,000   True  
377040  2,000 sqft   60657      3 Beds    IL     9.0    $674,999  False  
377041  1,152 sqft   11434      3 Beds    NY       2    $528,000  False  
377042         NaN   77028  8,479 sqft    TX     NaN     $34,500  False  
377043       1,462   78218           3    TX     1.0    $204,900  False  

[376752 rows x 15 columns]

In [93]:
# проведу еще раз анализ на скорректированном датасете
profile = ydata_profiling.ProfileReport(df_v9, title="Profiling Report")
profile.to_file("df_v9_report.html")

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 15/15 [03:00<00:00, 12.03s/it]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

___

Теперь посмотрим на признаки, имеющие слишком много возможных значений (HIGH CARDINALITY)

**Попробую проанализировать признак status**

Из отчета видно, что пропущенные значения данного признака составляют 10.6%. Это достаточно большой процент, для того, чтобы просто удалить строки с пропущенными значениями. Подумаю, как можно заполнить пропущенные значения.

In [94]:
# посмотрим, какие вообще значения может принимать данный признак
df_v9.status.unique()

array(['Active', 'for sale', nan, 'New construction', 'New', 'For sale',
       'Pending', 'P', 'Active/Contingent', 'Pre-foreclosure / auction',
       ' / auction', 'Under Contract', 'Under Contract   Showing',
       'Pre-foreclosure', 'Under Contract Backups', 'foreclosure',
       'Active Under Contract', 'Foreclosed', 'Option Pending',
       'Under Contract Show', 'for rent', 'Auction', 'A Active',
       'Contingent', 'Pending   Continue To Show', 'Price Change',
       'Back on Market', 'Active Option', 'Foreclosure', 'recently sold',
       'Coming soon: Nov 21.', 'Contingent Finance And Inspection',
       'Coming soon: Dec 4.', 'P Pending Sale', 'Coming soon: Nov 23.',
       'Active With Contingencies', 'Pending Ab', 'Pf', 'Contingent Show',
       'Contract P', 'Contingent Take Backup', 'Apartment for rent',
       'Backup Contract', 'Option Contract', 'Pending Continue To Show',
       'pending', 'Pending Inspection', 'Active Option Contract', 'C',
       'Auction - Acti

Плохо, что данный признак заполнялся операторами вручную, а не методом выбора из строго определенного перечня. Это привело к множеству различного обазначения для одинакового по сути статуса. В качестве рекомендаций для заказчика, для улучшения качества базы данных, как раз сделать этот признак шаблонным!

In [95]:
# Посмотрим на наиболее часто встречающиеся значения
df_v9.status.value_counts().nlargest(10)

status
for sale                     155959
Active                       104989
For sale                      43461
foreclosure                    6420
New construction               5473
Pending                        4699
Pre-foreclosure                2119
Pre-foreclosure / auction      1560
P                              1488
Under Contract Show            1183
Name: count, dtype: int64

In [96]:
# Посмотрим на строки с пропущенными значениями в этом признаке
df_v9[df_v9.status.isna()]

status   propertyType  \
9         NaN  Single Family   
14        NaN  Single Family   
33        NaN          Condo   
52        NaN          Condo   
60        NaN  Single Family   
...       ...            ...   
377035    NaN  Single Family   
377037    NaN  Single Family   
377039    NaN  Single Family   
377042    NaN            NaN   
377043    NaN  Single Family   

                                                   street baths  \
9                                    8612 Cedar Plains Ln     3   
14                                     15351 Falmouth Ave     3   
33                               3750 NE 170th St APT 407   2.0   
52                              3131 NE 7th Ave UNIT 4801   4.0   
60                                         4761 NW 7th Dr   2.0   
...                                                   ...   ...   
377035                                    3263 Wolcott Pl   2.0   
377037  Buildable plan: The Torino (384L) Riverstone R...     2   
377039                                  20800 NE 23rd Ave   6.0   
377042                                    7810 Pereida St   NaN   
377043                                   5983 Midcrown Dr   2.0   

                                                homeFacts       fireplace  \
9       {'atAGlanceFacts': [{'factValue': '2019', 'fac...             NaN   
14      {'atAGlanceFacts': [{'factValue': '1982', 'fac...             NaN   
33      {'atAGlanceFacts': [{'factValue': '1972', 'fac...             NaN   
52      {'atAGlanceFacts': [{'factValue': '2018', 'fac...             NaN   
60      {'atAGlanceFacts': [{'factValue': '1964', 'fac...             NaN   
...                                                   ...             ...   
377035  {'atAGlanceFacts': [{'factValue': '1962', 'fac...             Yes   
377037  {'atAGlanceFacts': [{'factValue': '2019', 'fac...             NaN   
377039  {'atAGlanceFacts': [{'factValue': '1990', 'fac...             NaN   
377042  {'atAGlanceFacts': [{'factValue': None, 'factL...             NaN   
377043  {'atAGlanceFacts': [{'factValue': '2019', 'fac...  Not Applicable   

                     city                                            schools  \
9                 Houston  [{'rating': ['4/10', '3/10', '2/10'], 'data': ...   
14                Houston  [{'rating': ['4/10', '5/10', '7/10'], 'data': ...   
33      North Miami Beach  [{'rating': ['10/10', '6/10'], 'data': {'Dista...   
52                  Miami  [{'rating': ['10/10', '2/10'], 'data': {'Dista...   
60             Plantation  [{'rating': ['3/10', '6/10', '5/10'], 'data': ...   
...                   ...                                                ...   
377035            Orlando  [{'rating': ['3/10', '1/10', '3/10'], 'data': ...   
377037            Houston  [{'rating': ['7/10', '6/10', '5/10'], 'data': ...   
377039              Miami  [{'rating': ['10/10', '5/10'], 'data': {'Dista...   
377042            Houston  [{'rating': ['NA', 'NA', 'NA'], 'data': {'Dist...   
377043        San Antonio  [{'rating': ['5/10', '4/10', '3/10'], 'data': ...   

              sqft zipcode        beds state stories      target   Pool  
9            1,930   77080           3    TX     2.0    $311,995  False  
14           2,454   77084           4    TX     2.0    $168,800  False  
33           1,085   33160           2    FL     0.0    $179,000  False  
52           1,873   33137           3    FL     NaN  $1,780,000  False  
60      2,088 sqft   33317           3    FL     1.0    $333,543   True  
...            ...     ...         ...   ...     ...         ...    ...  
377035  1,829 sqft   32805           3    FL       1    $171,306  False  
377037       1,841   77089           4    TX     1.0    $252,990  False  
377039       4,017   33180           5    FL     0.0  $1,249,000   True  
377042         NaN   77028  8,479 sqft    TX     NaN     $34,500  False  
377043       1,462   78218           3    TX     1.0    $204,900  False  

[39872 rows x 15 columns]

Поскольку коментарии к входным данным мне не предоставили, а наша база данных - это база по продаже домов, то по моему субъективному мнению значение "Active" имеет тот же смысл, что и значение "For sale" - то есть дом находится на продаже.

Теперь по поводу пропущенных значений. Можно предположить две гипотезы.
1. Пропущенные значения означают, что дом уже продан и объявление о продаже снято.
2. Поскольку данный признак заполнялся вручную, то его могли просто не заполнить.

Впринципе, для построения модели предсказания цены обе гипотезы нам подходят, и можно принять решение о заполнении пропущенных значений либо наиболее часто встречающимся, либо например признаком неопределенности "undefined"

In [97]:
# заполним пропущенные значения значением "undefined"
df_v9.status.fillna('undefined', inplace=True)

C:\Users\User\AppData\Local\Temp\ipykernel_7976\1506927445.py:2: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  df_v9.status.fillna('undefined', inplace=True)


Признак может принимать одинаковые значения но написанные строчными или прописными буквами - 'for sale', 'For sale', 'For Sale'. Объединим их в один. Да и вообще можно все значения этого признака перевести в нижний регистр.

In [98]:
df_v9.status = df_v9.status.str.lower()

In [99]:
# Посмотрим теперь на наиболее часто встречающиеся значения
df_v9.status.value_counts().nlargest(10)

status
for sale                     199422
active                       104989
undefined                     39872
foreclosure                    6763
new construction               5473
pending                        4804
pre-foreclosure                2119
pre-foreclosure / auction      1560
p                              1488
under contract show            1183
Name: count, dtype: int64

Также у признака есть значения 'active' и 'a active'. Объединим их в одно

In [100]:
df_v9.status = df_v9.status.str.replace('a active','active')

In [101]:
df_v9.status.unique()

array(['active', 'for sale', 'undefined', 'new construction', 'new',
       'pending', 'p', 'active/contingent', 'pre-foreclosure / auction',
       ' / auction', 'under contract', 'under contract   showing',
       'pre-foreclosure', 'under contract backups', 'foreclosure',
       'active under contract', 'foreclosed', 'option pending',
       'under contract show', 'for rent', 'auction', 'contingent',
       'pending   continue to show', 'price change', 'back on market',
       'active option', 'recently sold', 'coming soon: nov 21.',
       'contingent finance and inspection', 'coming soon: dec 4.',
       'p pending sale', 'coming soon: nov 23.',
       'active with contingencies', 'pending ab', 'pf', 'contingent show',
       'contract p', 'contingent take backup', 'apartment for rent',
       'backup contract', 'option contract', 'pending continue to show',
       'pending inspection', 'active option contract', 'c',
       'auction - active', 'contingent   show', 'pi',
       'du

Встречаются значения, отличающиеся запятой или наличием лишнего пробела, например 'pending, continue to show', 'pending continue to show', 'pending   continue to show'. Чтобы избавится от подобного удалим все пробелы и запятые

In [102]:
df_v9.status = df_v9.status.str.replace(' ','').str.replace(',','')

Также присутствуют значения 'pendingwithcontingencies' и 'pendingw/cont.'. Объединим их в одно.

In [103]:
df_v9.status = df_v9.status.str.replace('pendingw/cont.','pendingwithcontingencies')

Объединим 'active-contingent', 'active/contingent', 'activecontingency', 'activewithcontingencies', 'activecontingent' в одно

In [104]:
df_v9.status = df_v9.status \
.str.replace('active-contingent','activecontingent') \
.str.replace('active/contingent','activecontingent') \
.str.replace('activecontingency','activecontingent') \
.str.replace('activewithcontingencies','activecontingent')

Объединим '/auction' с 'auction', а 'auction-active' с 'active-auction'

In [105]:
df_v9.status = df_v9.status \
.str.replace('/auction','auction') \
.str.replace('active-auction','auction-active')

Объединим 'undercontract' с 'uundercontract', а 'undercontractshowing' с 'undercontractshow' и 'undercontract-show'

In [106]:
df_v9.status = df_v9.status \
.str.replace('uundercontract','undercontract') \
.str.replace('undercontractshowing','undercontractshow') \
.str.replace('undercontract-show','undercontractshow') 

In [107]:
df_v9.status.unique()

array(['active', 'forsale', 'undefined', 'newconstruction', 'new',
       'pending', 'p', 'activecontingent', 'pre-foreclosureauction',
       'auction', 'undercontract', 'undercontractshow', 'pre-foreclosure',
       'undercontractbackups', 'foreclosure', 'activeundercontract',
       'foreclosed', 'optionpending', 'forrent', 'contingent',
       'pendingcontinuetoshow', 'pricechange', 'backonmarket',
       'activeoption', 'recentlysold', 'comingsoon:nov21.',
       'contingentfinanceandinspection', 'comingsoon:dec4.',
       'ppendingsale', 'comingsoon:nov23.', 'pendingab', 'pf',
       'contingentshow', 'contractp', 'contingenttakebackup',
       'apartmentforrent', 'backupcontract', 'optioncontract',
       'pendinginspection', 'activeoptioncontract', 'c', 'auction-active',
       'pi', 'duediligenceperiod', 'contractcontingentonbuyersale',
       'comingsoon:nov29.', 'comingsoon:dec2.',
       'pendingwithcontingencies', 'lease/purchasepending',
       'pendingbringbackup', 'ccon

значения "Coming soon:...". Считаю, что конкретная дата в данном признаке является избыточной для построения модели. Поэтому объединим все эти значения по первым двум словам, исключив конкретную дату "скорого выхода"

In [108]:
df_v9.status.str.match('^comingsoon.*').sum()

np.int64(110)

In [109]:
df_v9.status = df_v9.status.str.replace('^comingsoon.*','comingsoon', regex=True)

Есть значения 'recentlysold' и 'sold:...' с какой-то суммой. Объединим их.

In [110]:
df_v9.status = df_v9.status.str.replace('^sold.*','recentlysold', regex=True)

In [111]:
df_v9.status.unique()

array(['active', 'forsale', 'undefined', 'newconstruction', 'new',
       'pending', 'p', 'activecontingent', 'pre-foreclosureauction',
       'auction', 'undercontract', 'undercontractshow', 'pre-foreclosure',
       'undercontractbackups', 'foreclosure', 'activeundercontract',
       'foreclosed', 'optionpending', 'forrent', 'contingent',
       'pendingcontinuetoshow', 'pricechange', 'backonmarket',
       'activeoption', 'recentlysold', 'comingsoon',
       'contingentfinanceandinspection', 'ppendingsale', 'pendingab',
       'pf', 'contingentshow', 'contractp', 'contingenttakebackup',
       'apartmentforrent', 'backupcontract', 'optioncontract',
       'pendinginspection', 'activeoptioncontract', 'c', 'auction-active',
       'pi', 'duediligenceperiod', 'contractcontingentonbuyersale',
       'pendingwithcontingencies', 'lease/purchasepending',
       'pendingbringbackup', 'ccontinueshow', 'pendingtakingbackups',
       'offerpendingsignature', 'contingentlienholderrelease',
    

In [112]:
# Посмотрим теперь на наиболее часто встречающиеся значения
df_v9.status.value_counts().nlargest(20)

status
forsale                   199422
active                    105431
undefined                  39872
foreclosure                 6763
newconstruction             5473
pending                     4804
pre-foreclosure             2119
undercontractshow           1982
pre-foreclosureauction      1560
p                           1488
auction                     1472
activeundercontract          718
undercontract                702
new                          690
contingent                   581
pricechange                  563
foreclosed                   458
forrent                      398
recentlysold                 289
undercontractbackups         252
Name: count, dtype: int64

In [113]:
# Посмотрим на наименее часто встречающиеся значения
df_v9.status.value_counts().nsmallest(10)

status
temporaryactive          1
pendingbringbackup       1
contingentnoshow         1
pendingbackupswanted     1
pendingw/escapeclause    1
contract                 1
pendingw/backupwanted    1
conditionalcontract      1
contingent-saleofhome    1
lease/purchase           1
Name: count, dtype: int64

In [114]:
df_v9.status.nunique()

95

Стоит наверное ограничить количество значений до какого-то числа, а те значения, которых встречается всего по несколько раз объединить в одну группу "other". Оставлю эту мысль на попозже.

Потратил целый день времени на анализ этого признака. Но потом возникла мысль, что этот признак - это признак присущий не продаваемому объекту, а это признак состояния самого объявления о продаже. На эту мысль навел меня анализ значений данного признака. И тогда этот признак влияния на цену не имеет.  
Но с другой стороны есть несколько значений, например 'New construction', 'Auction', 'foreclosure' и их варианты, которые при логическом анализе этих значений вполне себе могут влиять на значение стартовой цены.   
Вобщем еще раз убеждаюсь, что без качественного описания входных данных и не находясь достаточно погруженным в данную тематику можно очень долго рассуждать и предполагать, но к истине так и не приблизиться.

на этом пока закончу анализ признака Статус
___

**Перехожу к анализу признака propertyType**

In [115]:
# много чего придется с этим признаком сделать. поэтому сохраню в отдельный файл
df_v9.to_pickle("data/df_v10.pkl")

In [116]:
# считаем
df_v10 = pd.read_pickle("data/df_v10.pkl")  

In [117]:
# дабы убрать различия в наличии прописных букв, переведем все в строчные
df_v10.propertyType = df_v10.propertyType.str.lower()

In [118]:
# посмотрю какие вообще бывают значения
df_v10.propertyType.sort_values(ascending=False).unique().tolist()

['yes',
 'warehouse',
 'walk-out ranch',
 'villa',
 'victorian/federal',
 'victorian, craftsman',
 'victorian, bilevel',
 'victorian',
 'urban contemporary',
 'unknown',
 'two story, tri-level',
 'two story, split-level',
 'two story, spanish/mediterranean',
 'two story, low rise',
 'two story, duplex',
 'two story',
 'tuscan',
 'tudor/provincial',
 'tudor',
 'triplex',
 'trinity',
 'tri-level, traditional',
 'tri-level, northwestern contemporary',
 'tri-level, modern',
 'tri-level, craftsman',
 'tri-level, contemporary',
 'tri-level',
 'transitional, williamsburg',
 'transitional, colonial',
 'transitional',
 'traditional, zero-lot line',
 'traditional, williamsburg',
 'traditional, victorian',
 'traditional, transitional, williamsburg',
 'traditional, transitional, cottage',
 'traditional, transitional',
 'traditional, texas hill country',
 'traditional, straight thru',
 'traditional, loft with bedrooms',
 'traditional, federal',
 'traditional, cottage',
 'traditional, contemporary',

Поскольку уникальных значений этого признака слишком много, считаю целесообразным объединить их в схожие группы по анализу названий

Присутствуют значения 'single-family home','single family home','single family'. Объединим их

In [119]:
df_v10.propertyType = df_v10.propertyType \
.str.replace('single-family home','single family') \
.str.replace('single family home','single family') 

In [120]:
# Объединим по первому слову
df_v10.propertyType = df_v10.propertyType.str.replace('^victorian.*','victorian', regex=True)

Есть предположение, что propertyType начинающийся со слов two story указывает на количество этажей. Кстати это же подтверждает тот факт, что почти у всех таких строк в признаке stories пропущено значение (за исключением 7 строк). 

In [121]:
df_v10[df_v10.propertyType.str.contains('^two.*',na=False, regex=True)].sort_values('stories').head(9)

status            propertyType                   street baths  \
65167   active  two story, split-level          414 Rovino Ave    NaN   
204775  active  two story, split-level     16574 Segovia Cir S    NaN   
255131  active  two story, split-level       10120 SW 140th St    NaN   
300109  active  two story, split-level         460 N Mashta Dr    NaN   
315300  active  two story, split-level          7845 SW 164 Pl    NaN   
201763  active               two story       10593 NW 67th Ter    NaN   
232923  active    two story, tri-level       650 Curtiswood Dr    NaN   
890     active               two story  6423 Osprey Landing St    NaN   
1600    active               two story         972 NW 204th St    NaN   

                                                homeFacts fireplace  \
65167   {'atAGlanceFacts': [{'factValue': '1996', 'fac...       NaN   
204775  {'atAGlanceFacts': [{'factValue': '1997', 'fac...       NaN   
255131  {'atAGlanceFacts': [{'factValue': '1977', 'fac...       NaN   
300109  {'atAGlanceFacts': [{'factValue': '2015', 'fac...       NaN   
315300  {'atAGlanceFacts': [{'factValue': '2005', 'fac...       NaN   
201763  {'atAGlanceFacts': [{'factValue': '2016', 'fac...       NaN   
232923  {'atAGlanceFacts': [{'factValue': '1996', 'fac...       NaN   
890     {'atAGlanceFacts': [{'factValue': '2018', 'fac...       NaN   
1600    {'atAGlanceFacts': [{'factValue': '2007', 'fac...       NaN   

                  city                                            schools  \
65167     Coral Gables  [{'rating': ['10', '10', 'NR', '7', '6'], 'dat...   
204775  Pembroke Pines  [{'rating': ['8', '10', '8'], 'data': {'Distan...   
255131           Miami  [{'rating': ['8', '10', 'NR', '7', '4'], 'data...   
300109    Key Biscayne  [{'rating': ['9', 'NR', '10', '5', '5'], 'data...   
315300           Miami  [{'rating': ['8', '10', 'NR', '7', '6'], 'data...   
201763           Doral  [{'rating': ['7', '10', 'NR', '4', '8'], 'data...   
232923    Key Biscayne  [{'rating': ['9', 'NR', '10', '5', '5'], 'data...   
890              Davie  [{'rating': ['8', '6', '4'], 'data': {'Distanc...   
1600     Miami Gardens  [{'rating': ['6', '10', 'NR', '3', '4'], 'data...   

          sqft zipcode beds state        stories      target   Pool  
65167    5,831   33156  NaN    FL    Multi/Split   3,399,000  False  
204775   3,751   33331  NaN    FL    Multi/Split     640,000  False  
255131   2,324   33176  NaN    FL    Multi/Split     749,000  False  
300109  10,875   33149  NaN    FL    Multi/Split  18,500,000  False  
315300     NaN   33193  NaN    FL    Multi/Split     569,000  False  
201763   4,097   33178  NaN    FL  Three Or More   2,049,000  False  
232923   3,572   33149  NaN    FL  Three Or More   2,350,000  False  
890      2,252   33314  NaN    FL            NaN     494,900  False  
1600     3,572   33169  NaN    FL            NaN     550,000  False

Заполню пустые значения признака stories значением 2 при значении propertyType начинающийся со слов two story

In [122]:
mask_story = df_v10.propertyType.str.contains('^two story.*',na=False, regex=True)
# Очень странно, но пытался через параметр inplace=True заполнить. Не работает! Сработало только через явное =...??
df_v10.loc[mask_story,'stories'] = df_v10.loc[mask_story,'stories'].fillna('2')

In [123]:
df_v10[df_v10.propertyType.str.contains('^two.*',na=False, regex=True)].sort_values('stories').tail(10)

status            propertyType                   street baths  \
139753  active               two story  13200 Biscayne Bay Ter    NaN   
139113  active               two story           18 NE 42nd St    NaN   
376518  active               two story        627 NE 191st Ter    NaN   
65167   active  two story, split-level          414 Rovino Ave    NaN   
204775  active  two story, split-level     16574 Segovia Cir S    NaN   
315300  active  two story, split-level          7845 SW 164 Pl    NaN   
300109  active  two story, split-level         460 N Mashta Dr    NaN   
255131  active  two story, split-level       10120 SW 140th St    NaN   
232923  active    two story, tri-level       650 Curtiswood Dr    NaN   
201763  active               two story       10593 NW 67th Ter    NaN   

                                                homeFacts fireplace  \
139753  {'atAGlanceFacts': [{'factValue': '2002', 'fac...       NaN   
139113  {'atAGlanceFacts': [{'factValue': '1924', 'fac...       NaN   
376518  {'atAGlanceFacts': [{'factValue': '2014', 'fac...       NaN   
65167   {'atAGlanceFacts': [{'factValue': '1996', 'fac...       NaN   
204775  {'atAGlanceFacts': [{'factValue': '1997', 'fac...       NaN   
315300  {'atAGlanceFacts': [{'factValue': '2005', 'fac...       NaN   
300109  {'atAGlanceFacts': [{'factValue': '2015', 'fac...       NaN   
255131  {'atAGlanceFacts': [{'factValue': '1977', 'fac...       NaN   
232923  {'atAGlanceFacts': [{'factValue': '1996', 'fac...       NaN   
201763  {'atAGlanceFacts': [{'factValue': '2016', 'fac...       NaN   

                  city                                            schools  \
139753     North Miami  [{'rating': ['6', '10', 'NR', '3', '6'], 'data...   
139113           Miami  [{'rating': ['4', '10', 'NR', '2', '2'], 'data...   
376518           Miami  [{'rating': ['6', '10', 'NR', '5', '5'], 'data...   
65167     Coral Gables  [{'rating': ['10', '10', 'NR', '7', '6'], 'dat...   
204775  Pembroke Pines  [{'rating': ['8', '10', '8'], 'data': {'Distan...   
315300           Miami  [{'rating': ['8', '10', 'NR', '7', '6'], 'data...   
300109    Key Biscayne  [{'rating': ['9', 'NR', '10', '5', '5'], 'data...   
255131           Miami  [{'rating': ['8', '10', 'NR', '7', '4'], 'data...   
232923    Key Biscayne  [{'rating': ['9', 'NR', '10', '5', '5'], 'data...   
201763           Doral  [{'rating': ['7', '10', 'NR', '4', '8'], 'data...   

          sqft zipcode beds state        stories      target   Pool  
139753   4,094   33181  NaN    FL              2   1,899,000  False  
139113   2,760   33137  NaN    FL              2   1,150,000  False  
376518   2,223   33179  NaN    FL              2     550,000  False  
65167    5,831   33156  NaN    FL    Multi/Split   3,399,000  False  
204775   3,751   33331  NaN    FL    Multi/Split     640,000  False  
315300     NaN   33193  NaN    FL    Multi/Split     569,000  False  
300109  10,875   33149  NaN    FL    Multi/Split  18,500,000  False  
255131   2,324   33176  NaN    FL    Multi/Split     749,000  False  
232923   3,572   33149  NaN    FL  Three Or More   2,350,000  False  
201763   4,097   33178  NaN    FL  Three Or More   2,049,000  False

Теперь можно объединить значения "two story" путем отсечения всего, что после этих двух слов

In [124]:
df_v10.propertyType = df_v10.propertyType.str.replace('^two story.*','two story', regex=True)

Посмотрим на следующую группу

In [125]:
df_v10[df_v10.propertyType.str.contains('^tri-level.*',na=False, regex=True)].stories.value_counts(dropna=False)

stories
Three Or More    49
NaN              41
Name: count, dtype: int64

In [126]:
# Точно также заполним пропущенные значения
mask_story2 = df_v10.propertyType.str.contains('^tri-level.*',na=False, regex=True)

df_v10.loc[mask_story2,'stories'] = df_v10.loc[mask_story2,'stories'].fillna('Three Or More')
# проверим
df_v10[df_v10.propertyType.str.contains('^tri-level.*',na=False, regex=True)].stories.value_counts(dropna=False)

stories
Three Or More    90
Name: count, dtype: int64

In [127]:
# Объединим их в одну группу
df_v10.propertyType = df_v10.propertyType.str.replace('^tri-level.*','tri-level', regex=True)

Посмотрим на следующую группу transitional  
— это временное жилье для определенных слоев бездомного населения, включая работающих бездомных, которые зарабатывают слишком мало денег, чтобы позволить себе долгосрочное жилье. Временное жилье предназначено для перехода жильцов в постоянное доступное жилье.

In [128]:
df_v10[df_v10.propertyType.str.contains('^transitional.*',na=False, regex=True)].stories.value_counts(dropna=False)

stories
NaN    562
Name: count, dtype: int64

In [129]:
# Чаще всего эта группа домов имеет от 1 до 2 этажей. Заполним пропущенные значения двойкой
mask_story3 = df_v10.propertyType.str.contains('^transitional.*',na=False, regex=True)

df_v10.loc[mask_story3,'stories'] = df_v10.loc[mask_story3,'stories'].fillna('2')
# проверим
df_v10[df_v10.propertyType.str.contains('^transitional.*',na=False, regex=True)].stories.value_counts(dropna=False)

stories
2    562
Name: count, dtype: int64

In [130]:
# Объединим их в одну группу
df_v10.propertyType = df_v10.propertyType.str.replace('^transitional.*','transitional', regex=True)

Посмотрим на следующую группу traditional  
Дом в традиционном стиле - самый популярный стиль дома в США сегодня. Стиль представляет собой смесь классических элементов, вытянутых из домов, с современными элементами домашнего дизайна. Общие элементы этого стиля включают симметрично расположенные окна, простые руфлины и скромные детали.

In [131]:
df_v10[df_v10.propertyType.str.contains('^traditional.*',na=False, regex=True)].stories.value_counts(dropna=False)

stories
NaN                        2110
1                          1675
2                          1637
3                           278
Two                         142
One                         141
1.5                          38
4                            37
Three Or More                 9
Multi/Split                   3
Other, Two, Multi/Split       1
1.2                           1
2.5                           1
Name: count, dtype: int64

Видно, что очень много пропущенных значений, а из заполненных 1 и 2 имеют одинаковое количество. Заполним 50% пропущенных значений 1, а остальные 50% - 2, чтобы не нарушать данное распределение.

In [132]:
mask_story4 = df_v10.propertyType.str.contains('^traditional.*',na=False, regex=True) & df_v10.stories.isna()
# заполним первую половину "1"
index4 = df_v10.loc[mask_story4,'stories'].sample(frac=0.5).index
df_v10.loc[index4,'stories'] = df_v10.loc[index4,'stories'].fillna('1')
# поскольку часть значений заполнили, то нужно снова обновить маску, перед заполнением остальной части
mask_story4 = df_v10.propertyType.str.contains('^traditional.*',na=False, regex=True) & df_v10.stories.isna()
# заполним оставшиеся пропуски "2"
df_v10.loc[mask_story4,'stories'] = '2'

In [133]:
df_v10[df_v10.propertyType.str.contains('^traditional.*',na=False, regex=True)].stories.value_counts(dropna=False)

stories
1                          2730
2                          2692
3                           278
Two                         142
One                         141
1.5                          38
4                            37
Three Or More                 9
Multi/Split                   3
Other, Two, Multi/Split       1
1.2                           1
2.5                           1
Name: count, dtype: int64

In [134]:
# Объединим их в одну группу
df_v10.propertyType = df_v10.propertyType.str.replace('^traditional.*','traditional', regex=True)

Посмотрим на следующую группу townhouse

In [135]:
# Также считаю, что townhouse и townhome - это один и тот же тип. Объединим их тоже
df_v10.propertyType = df_v10.propertyType.str.replace('^townhome.*','townhouse', regex=True)

In [136]:
df_v10[df_v10.propertyType.str.contains('^townhouse.*',na=False, regex=True)].stories.value_counts(dropna=False)

stories
2.0       6337
NaN       3938
3.0       3306
1.0       1788
2          953
3          578
0.0        474
4.0        425
0          296
1          248
5.0         63
4           59
9.0         26
7.0         12
6.0         11
5            6
9            2
16.0         2
8            1
7            1
8.0          1
56           1
56.0         1
6            1
1002.0       1
Name: count, dtype: int64

Чтобы сильно не исказить распределение признака stories, заполним пропущенные значения таким образом: 50% - 2, 25% - 1, 25%-3

In [137]:
mask_story5 = df_v10.propertyType.str.contains('^townhouse.*',na=False, regex=True) & df_v10.stories.isna()
# заполним первую половину "1"
index5 = df_v10.loc[mask_story5,'stories'].sample(frac=0.5).index
df_v10.loc[index5,'stories'] = df_v10.loc[index5,'stories'].fillna('2.0')
# поскольку часть значений заполнили, то нужно снова обновить маски, перед заполнением остальной части
mask_story5 = df_v10.propertyType.str.contains('^townhouse.*',na=False, regex=True) & df_v10.stories.isna()
index5 = df_v10.loc[mask_story5,'stories'].sample(frac=0.5).index
df_v10.loc[index5,'stories'] = df_v10.loc[index5,'stories'].fillna('1.0')
# заполним оставшиеся пропуски "3" предварительно снова обновив маску
mask_story5 = df_v10.propertyType.str.contains('^townhouse.*',na=False, regex=True) & df_v10.stories.isna()
df_v10.loc[mask_story5,'stories'] = '3.0'

In [138]:
df_v10[df_v10.propertyType.str.contains('^townhouse.*',na=False, regex=True)].stories.value_counts(dropna=False)

stories
2.0       8306
3.0       4291
1.0       2772
2          953
3          578
0.0        474
4.0        425
0          296
1          248
5.0         63
4           59
9.0         26
7.0         12
6.0         11
5            6
9            2
16.0         2
8            1
7            1
8.0          1
56           1
56.0         1
6            1
1002.0       1
Name: count, dtype: int64

In [139]:
# Объединим их в одну группу
df_v10.propertyType = df_v10.propertyType.str.replace('^townhouse.*','townhouse', regex=True)

Посмотрим на следующую группу texas hill

In [140]:
# Объединим их в одну группу
df_v10.propertyType = df_v10.propertyType.str.replace('^texas hill country.*','texas hill country', regex=True)

Посмотрим на следующую группу straight thru

In [141]:
# Объединим их в одну группу
df_v10.propertyType = df_v10.propertyType.str.replace('^straight thru.*','straight thru', regex=True)

Посмотрим на следующую группу split...

In [142]:
# Объединим их в одну группу
df_v10.propertyType = df_v10.propertyType.str.replace('^split.*','split', regex=True)

In [143]:
# пропуски в этажности
df_v10[df_v10.propertyType.str.contains('^split.*',na=False, regex=True)]['stories'].value_counts(dropna=False)

stories
Multi/Split                   111
NaN                           106
2                              26
1                               9
3                               5
Three Or More, Multi/Split      4
4                               1
Name: count, dtype: int64

In [144]:
# заполним пропуски в этажности самым частым значением Multi/Split
mask_story6 = df_v10.propertyType.str.contains('^split.*',na=False, regex=True)

df_v10.loc[mask_story6,'stories'] = df_v10.loc[mask_story6,'stories'].fillna('Multi/Split')
# проверим
df_v10[df_v10.propertyType.str.contains('^split.*',na=False, regex=True)].stories.value_counts(dropna=False)

stories
Multi/Split                   217
2                              26
1                               9
3                               5
Three Or More, Multi/Split      4
4                               1
Name: count, dtype: int64

Посмотрим на следующую группу spanish..

In [145]:
# Объединим их в одну группу
df_v10.propertyType = df_v10.propertyType.str.replace('^spanish.*','spanish', regex=True)

In [146]:
# пропуски в этажности
df_v10[df_v10.propertyType.str.contains('^spanish.*',na=False, regex=True)]['stories'].value_counts(dropna=False)

stories
Two                           111
One                           107
NaN                            97
Three Or More                  18
2                               8
3                               6
1                               5
4                               2
Multi/Split                     2
Multi Level                     1
Multi Level, Three or More      1
5                               1
Name: count, dtype: int64

In [147]:
# половину пропусков заполним Two, половину - One
mask_story7 = df_v10.propertyType.str.contains('^spanish.*',na=False, regex=True) & df_v10.stories.isna()
# заполним первую половину "Two"
index7 = df_v10.loc[mask_story7,'stories'].sample(frac=0.5).index
df_v10.loc[index7,'stories'] = df_v10.loc[index7,'stories'].fillna('Two')
# поскольку часть значений заполнили, то нужно снова обновить маску, перед заполнением остальной части
mask_story7 = df_v10.propertyType.str.contains('^spanish.*',na=False, regex=True) & df_v10.stories.isna()
# заполним оставшиеся пропуски "One"
df_v10.loc[mask_story7,'stories'] = 'One'

In [148]:
# проверим
df_v10[df_v10.propertyType.str.contains('^spanish.*',na=False, regex=True)]['stories'].value_counts(dropna=False)

stories
Two                           159
One                           156
Three Or More                  18
2                               8
3                               6
1                               5
4                               2
Multi/Split                     2
Multi Level                     1
Multi Level, Three or More      1
5                               1
Name: count, dtype: int64

Посмотрим на следующую группу single wide

In [149]:
# Объединим их в одну группу
df_v10.propertyType = df_v10.propertyType \
.str.replace('^single wide.*','single wide', regex=True) \
.str.replace('^single-wide.*','single wide', regex=True)

In [150]:
# пропуски в этажности
df_v10[df_v10.propertyType.str.contains('^single wide.*',na=False, regex=True)]['stories'].value_counts(dropna=False)

stories
NaN    10
1       2
Name: count, dtype: int64

In [151]:
# Это тип одноэтажных зданий, поэтому заполним пропуски этажности - 1
mask_story8 = df_v10.propertyType.str.contains('^single wide.*',na=False, regex=True)

df_v10.loc[mask_story8,'stories'] = df_v10.loc[mask_story8,'stories'].fillna('1')
# проверим
df_v10[df_v10.propertyType.str.contains('^single wide.*',na=False, regex=True)].stories.value_counts(dropna=False)

stories
1    12
Name: count, dtype: int64

Посмотрим на следующую группу single detached.  
Такая категори домов встречается только в штате Техас и в основно такие дома одноэтажные

In [152]:
df_v10[df_v10.propertyType.str.contains('^single detached.*',na=False, regex=True)]['state'].value_counts(dropna=False)

state
TX    3065
Name: count, dtype: int64

In [153]:
df_v10[df_v10.propertyType.str.contains('^single detached.*',na=False, regex=True)]['stories'].value_counts(dropna=False)

stories
NaN    3063
1         1
2         1
Name: count, dtype: int64

Объединим в одну категорию, и заполним пропуски -1

In [154]:
df_v10.propertyType = df_v10.propertyType.str.replace('^single detached.*','single detached', regex=True)

In [155]:
mask_story9 = df_v10.propertyType.str.contains('^single detached.*',na=False, regex=True)

df_v10.loc[mask_story9,'stories'] = df_v10.loc[mask_story9,'stories'].fillna('1')
# проверим
df_v10[df_v10.propertyType.str.contains('^single detached.*',na=False, regex=True)].stories.value_counts(dropna=False)

stories
1    3064
2       1
Name: count, dtype: int64

Посмотрим на следующую группу side-by-side

In [156]:
df_v10.propertyType = df_v10.propertyType.str.replace('^side-by-side.*','side-by-side', regex=True)

Посмотрим на группу rustic

In [157]:
df_v10.propertyType = df_v10.propertyType.str.replace('^rustic.*','rustic', regex=True)

Посмотрим на группу resort property

In [158]:
df_v10.propertyType = df_v10.propertyType.str.replace('^resort property.*','resort property', regex=True)

Посмотрим на группу ranch

In [159]:
df_v10[df_v10.propertyType.str.contains('^ranch.*',na=False, regex=True)].sort_values('propertyType').stories.value_counts(dropna=False)

stories
NaN            1432
One             316
1               288
2                27
Two               6
1.5               3
4                 2
Multi/Split       2
Name: count, dtype: int64

Видим, что этот тип в основном одноэтажный. Поэтому заполним пропуски 1 и объединим в один тип

In [160]:
df_v10.propertyType = df_v10.propertyType.str.replace('^ranch.*','ranch', regex=True)

In [161]:
df_v10[df_v10.propertyType.str.contains('^ranch.*',na=False, regex=True)].sort_values('propertyType').stories.value_counts(dropna=False)

stories
NaN            1432
One             316
1               288
2                27
Two               6
1.5               3
Multi/Split       2
4                 2
Name: count, dtype: int64

In [162]:
mask_story10 = df_v10.propertyType.str.contains('^ranch.*',na=False, regex=True)

df_v10.loc[mask_story10,'stories'] = df_v10.loc[mask_story10,'stories'].fillna('1')
# проверим
df_v10[df_v10.propertyType.str.contains('^ranch.*',na=False, regex=True)].stories.value_counts(dropna=False)

stories
1              1720
One             316
2                27
Two               6
1.5               3
4                 2
Multi/Split       2
Name: count, dtype: int64

Посмотрим на группу raised ranch  
Приподнятое ранчо - это дом в стиле ранчо, который был установлен на фундаменте

In [163]:
df_v10[df_v10.propertyType.str.contains('^raised.*',na=False, regex=True)].sort_values('propertyType').stories.value_counts(dropna=False)

stories
NaN    17
1       1
1.5     1
Name: count, dtype: int64

In [164]:
df_v10.propertyType = df_v10.propertyType.str.replace('^raised ranch.*','raised ranch', regex=True)

In [165]:
mask_story11 = df_v10.propertyType.str.contains('^raised ranch.*',na=False, regex=True)

df_v10.loc[mask_story11,'stories'] = df_v10.loc[mask_story11,'stories'].fillna('1')
# проверим
df_v10[df_v10.propertyType.str.contains('^raised ranch.*',na=False, regex=True)].stories.value_counts(dropna=False)

stories
1      18
1.5     1
Name: count, dtype: int64

Посмотрим на группу penthouse

In [166]:
df_v10[df_v10.propertyType.str.contains('^penthouse.*',na=False, regex=True)].sort_values('propertyType').stories.value_counts(dropna=False)

stories
NaN              73
Multi/Split       5
Three Or More     1
Name: count, dtype: int64

In [167]:
# Объединим и заполним пробелы Multi/Split
df_v10.propertyType = df_v10.propertyType.str.replace('^penthouse.*','penthouse', regex=True)

In [168]:
mask_story12 = df_v10.propertyType.str.contains('^penthouse.*',na=False, regex=True)

df_v10.loc[mask_story12,'stories'] = df_v10.loc[mask_story12,'stories'].fillna('Multi/Split')
# проверим
df_v10[df_v10.propertyType.str.contains('^penthouse.*',na=False, regex=True)].stories.value_counts(dropna=False)

stories
Multi/Split      78
Three Or More     1
Name: count, dtype: int64

Посмотрим на группу patio

In [169]:
df_v10[df_v10.propertyType.str.contains('^patio.*',na=False, regex=True)].sort_values('propertyType').stories.value_counts(dropna=False)

stories
One    10
NaN     4
Two     3
Name: count, dtype: int64

In [170]:
# заполним пробелы
mask_story13 = df_v10.propertyType.str.contains('^patio home, one story.*',na=False, regex=True)
df_v10.loc[mask_story13,'stories'] = df_v10.loc[mask_story13,'stories'].fillna('One')

mask_story13 = df_v10.propertyType.str.contains('^patio home, two story.*',na=False, regex=True)
df_v10.loc[mask_story13,'stories'] = df_v10.loc[mask_story13,'stories'].fillna('Two')
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^patio.*','patio', regex=True)
# Заполним остальные пропуски
mask_story13 = df_v10.propertyType.str.contains('^patio.*',na=False, regex=True)
df_v10.loc[mask_story13,'stories'] = df_v10.loc[mask_story13,'stories'].fillna('One')
# проверим
df_v10[df_v10.propertyType.str.contains('^patio.*',na=False, regex=True)].stories.value_counts(dropna=False)

stories
One    12
Two     5
Name: count, dtype: int64

Посмотрим на группу other

In [171]:
df_v10[df_v10.propertyType.str.contains('^other.*',na=False, regex=True)].sort_values('propertyType').stories.value_counts(dropna=False)

stories
NaN              214
1                156
2                148
3                 44
One               35
Two               28
1.5                7
4                  5
1.0                3
2.5                2
3.0                1
Three Or More      1
Name: count, dtype: int64

In [172]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^other.*','other', regex=True)

Пропущенные значения заполним поровну 1 и 2

In [173]:
mask_story11 = df_v10.propertyType.str.contains('^other.*',na=False, regex=True) & df_v10.stories.isna()
# заполним первую половину "1"
index11 = df_v10.loc[mask_story11,'stories'].sample(frac=0.5).index
df_v10.loc[index11,'stories'] = df_v10.loc[index11,'stories'].fillna('1')
# поскольку часть значений заполнили, то нужно снова обновить маску, перед заполнением остальной части
mask_story11 = df_v10.propertyType.str.contains('^other.*',na=False, regex=True) & df_v10.stories.isna()
# заполним оставшиеся пропуски "2"
df_v10.loc[mask_story11,'stories'] = '2'
# проверим
df_v10[df_v10.propertyType.str.contains('^other.*',na=False, regex=True)].sort_values('propertyType').stories.value_counts(dropna=False)

stories
1                263
2                255
3                 44
One               35
Two               28
1.5                7
4                  5
1.0                3
2.5                2
3.0                1
Three Or More      1
Name: count, dtype: int64

Посмотрим на группу one story

In [174]:
df_v10[df_v10.propertyType.str.contains('^one story.*',na=False, regex=True)].sort_values('propertyType').stories.value_counts(dropna=False)

stories
NaN            619
Multi/Split      4
Name: count, dtype: int64

In [175]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^one story.*','one story', regex=True)

In [176]:
# Так как это one story, то заполним пропуски 1
mask_story13 = df_v10.propertyType.str.contains('^one story.*',na=False, regex=True)

df_v10.loc[mask_story13,'stories'] = df_v10.loc[mask_story13,'stories'].fillna('1')
# проверим
df_v10[df_v10.propertyType.str.contains('^one story.*',na=False, regex=True)].stories.value_counts(dropna=False)

stories
1              619
Multi/Split      4
Name: count, dtype: int64

Посмотрим на группу old world

In [177]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^old world.*','old world', regex=True)

Посмотрим на группу new build 2019, traditional

In [178]:
# Заменим
df_v10.propertyType = df_v10.propertyType.str.replace('^new build.*','traditional', regex=True)

Посмотрим на группу multiplex

In [179]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^multiplex.*','multiplex', regex=True)

Посмотрим на группу multi-level

In [180]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^multi-level.*','multi-level', regex=True)

Посмотрим на группу multi family

In [181]:
# Объединим
df_v10.propertyType = df_v10.propertyType \
.str.replace('^multi-family.*','multi family', regex=True) \
.str.replace('^multi-family home.*','multi family', regex=True)

Посмотрим на группу multi generational

In [182]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^multi generational.*','multi generational', regex=True)

Посмотрим на группу modernist и modern

In [183]:
# Объединим
df_v10.propertyType = df_v10.propertyType \
.str.replace('^modernist.*','modern', regex=True) \
.str.replace('^modern.*','modern', regex=True)

Посмотрим на группу mobile.  
Переносные дома — сборные дома, построенные на заводе, а не на месте, а затем доставленные в месторасположение

In [184]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^mobile.*','mobile home', regex=True)

In [185]:
# соответственно в основном эта категория имеет 1 этаж. Заполним
mask_story14 = df_v10.propertyType.str.contains('^mobile.*',na=False, regex=True)

df_v10.loc[mask_story14,'stories'] = df_v10.loc[mask_story14,'stories'].fillna('1')
# проверим
df_v10[df_v10.propertyType.str.contains('^mobile.*',na=False, regex=True)].stories.value_counts(dropna=False)

stories
1          1386
1.0         882
0           216
0.0         186
2.0          11
9.0           3
4.0           2
1 Level       1
Name: count, dtype: int64

Посмотрим на группу mid-rise

In [186]:
# В группе mid-rise (4-7 stories) заполним пропуски - 4
mask_story15 = df_v10.propertyType.str.contains('^mid-rise .*',na=False, regex=True)
df_v10.loc[mask_story15,'stories'] = df_v10.loc[mask_story15,'stories'].fillna('4')

В группе mid-rise анализ через интернет-карты показал, что в такую категорию могут входить абсолютно разной этажности дома, от 4 и до 12. Поэтому заполнять каким-то определенным числом пропуски этажности в этой группе смысла нет.

А вот что пишут сами америкосы про этот тип зданий:  
A mid-rise apartment building is typically a building that has more than four (4) but less than twelve (12) floors.  
If the building has more than 12 floors, it is typically considered a high-rise. If it is lower than four floors, it is considered a low-rise or garden-style apartment.    

In [187]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^mid-rise.*','mid-rise', regex=True)
# и этот туда же
df_v10.propertyType = df_v10.propertyType.str.replace('^mid rise.*','mid-rise', regex=True)

Посмотрим на группу mid-century

In [188]:
df_v10[df_v10.propertyType.str.contains('^mid-century.*',na=False, regex=True)].sort_values('propertyType').stories.value_counts(dropna=False)

stories
NaN              32
One              16
Two               6
Three Or More     3
Name: count, dtype: int64

In [189]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^mid-century.*','mid-century', regex=True)
# и этот туда же
df_v10.propertyType = df_v10.propertyType.str.replace('^mid century.*','mid-century', regex=True)

In [190]:
# Заполним пропуски в пропорции 0.75 - 1, 0.25 - 2
mask_story15 = df_v10.propertyType.str.contains('^mid-century.*',na=False, regex=True) & df_v10.stories.isna()
# заполним первую половину "1"
index15 = df_v10.loc[mask_story15,'stories'].sample(frac=0.75).index
df_v10.loc[index15,'stories'] = df_v10.loc[index15,'stories'].fillna('1')
# поскольку часть значений заполнили, то нужно снова обновить маску, перед заполнением остальной части
mask_story15 = df_v10.propertyType.str.contains('^mid-century.*',na=False, regex=True) & df_v10.stories.isna()
# заполним оставшиеся пропуски "2"
df_v10.loc[mask_story15,'stories'] = '2'
# проверим
df_v10[df_v10.propertyType.str.contains('^mid-century.*',na=False, regex=True)].sort_values('propertyType').stories.value_counts(dropna=False)

stories
1                25
One              16
2                 8
Two               6
Three Or More     3
Name: count, dtype: int64

Посмотрим на группу mfd/mobile home

In [191]:
df_v10[df_v10.propertyType.str.contains('^mfd/mobile.*',na=False, regex=True)].sort_values('propertyType').stories.value_counts(dropna=False)

stories
1                          470
NaN                        210
1 Story                     24
1.00                        23
1.0000                      18
Manufactured Doublewide     13
One Story                    7
Mobile                       7
One                          7
Manufactured Singlewide      6
1 Level                      4
1.0                          2
Double Wide                  1
Name: count, dtype: int64

In [192]:
# Заполним пропуски -1 
mask_story16 = df_v10.propertyType.str.contains('^mfd/mobile.*',na=False, regex=True)
df_v10.loc[mask_story16,'stories'] = df_v10.loc[mask_story16,'stories'].fillna('1')

In [193]:
# Объединим
df_v10.propertyType = df_v10.propertyType \
.str.replace('^mfd/mobile.*','mfd/mobile', regex=True) \
.str.replace('^manuf/mobile.*','mfd/mobile', regex=True)

Посмотрим на группу mediterranean

In [194]:
df_v10[df_v10.propertyType.str.contains('^mediterranean.*',na=False, regex=True)].sort_values('propertyType').stories.value_counts(dropna=False)

stories
2      82
3      61
NaN    17
4      14
1       8
1.5     2
Name: count, dtype: int64

In [195]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^mediterranean.*','mediterranean', regex=True)

In [196]:
# Заполним пропуски - 2
mask_story17 = df_v10.propertyType.str.contains('^mediterranean.*',na=False, regex=True)
df_v10.loc[mask_story17,'stories'] = df_v10.loc[mask_story17,'stories'].fillna('2')

Посмотрим на группу manufactured

In [197]:
df_v10[df_v10.propertyType.str.contains('^manufactured.*',na=False, regex=True)].sort_values('propertyType').stories.value_counts(dropna=False)

stories
NaN                                  72
Manufactured Home, Non-Site Built     1
1 Level, Non-Site Built               1
Name: count, dtype: int64

Как показал анализ, эта категория в основном однаэтажная

In [198]:
# Заполним все значения -1 
mask_story18 = df_v10.propertyType.str.contains('^manufactured.*',na=False, regex=True)
df_v10.loc[mask_story18,'stories'] = '1'

In [199]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^manufactured.*','manufactured', regex=True)

Посмотрим на группу low rise

In [200]:
df_v10[df_v10.propertyType.str.contains('^low-rise.*',na=False, regex=True)].sort_values('propertyType').stories.value_counts(dropna=False)

stories
NaN    90
Name: count, dtype: int64

In [201]:
# Объединим
df_v10.propertyType = df_v10.propertyType \
.str.replace('^low-rise.*','low rise', regex=True) \
.str.replace('^low rise.*','low rise', regex=True)

In [202]:
# В основном это двухэтажные дома, заполним 2
mask_story19 = df_v10.propertyType.str.contains('^low rise.*',na=False, regex=True)
df_v10.loc[mask_story19,'stories'] = '2'

Посмотрим на группу log

In [203]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^log.*','log', regex=True)

In [204]:
df_v10[df_v10.propertyType.str.contains('^log.*',na=False, regex=True)].sort_values('propertyType').stories.value_counts(dropna=False)

stories
NaN    3
1.5    1
Name: count, dtype: int64

In [205]:
# Это тип - сруб, заполним 1,5
mask_story20 = df_v10.propertyType.str.contains('^log.*',na=False, regex=True)
df_v10.loc[mask_story20,'stories'] = '1.5'

Посмотрим на группу loft

In [206]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^loft.*','loft', regex=True)
# Прогнизировать этажность этого типа сложно

Посмотрим на группу less than 4 floors

In [207]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^less than 4 floors.*','less than 4 floors', regex=True)
# Прогнизировать этажность этого типа сложно

Посмотрим на группу lake house

In [208]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^lake house.*','lake house', regex=True)

Посмотрим на группу key west

In [209]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^key west.*','key west', regex=True)

In [210]:
mask_story21 = df_v10.propertyType.str.contains('^key west.*',na=False, regex=True)
df_v10.loc[mask_story21,'stories'] = df_v10.loc[mask_story21,'stories'].fillna('Two')

Посмотрим на группу houseboat

In [211]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^houseboat.*','houseboat', regex=True)

Посмотрим на группу historical

In [212]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^historical, traditional.*','historical', regex=True)
df_v10.propertyType = df_v10.propertyType.str.replace('^historical/conservation district.*','historical/conservation district', regex=True)
# туда же
df_v10.propertyType = df_v10.propertyType.str.replace('^historic.*','historical', regex=True)

Посмотрим на группу high rise

In [213]:
# Объединим
df_v10.propertyType = df_v10.propertyType \
.str.replace('^high-rise.*','high rise', regex=True) \
.str.replace('^high rise.*','high rise', regex=True) \
.str.replace('^hi-rise.*','high rise', regex=True)

In [214]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^hi ranch.*','high ranch', regex=True)

Посмотрим на группу georgian

In [215]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^georgian.*','georgian', regex=True)

Посмотрим на группу garden/zero lot line

In [216]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^garden/zero lot line.*','garden/zero lot line', regex=True)

Посмотрим на группу garden home

In [217]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^garden home.*','garden home', regex=True)

Посмотрим на группу french

In [218]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^french.*','french', regex=True)

Посмотрим на группу florida

In [219]:
# Заполним
mask_story22 = df_v10.propertyType.str.contains('^florida, two story.*',na=False, regex=True)
df_v10.loc[mask_story22,'stories'] = '2'

mask_story22 = df_v10.propertyType.str.contains('^florida, ranch, one story.*',na=False, regex=True)
df_v10.loc[mask_story22,'stories'] = '1'

# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^florida.*','florida', regex=True)

# Заполним пропуски в пропорции 0.8 - One, 0.2 - Two
mask_story22 = df_v10.propertyType.str.contains('^florida.*',na=False, regex=True) & df_v10.stories.isna()
# заполним первую половину "One"
index22 = df_v10.loc[mask_story22,'stories'].sample(frac=0.8).index
df_v10.loc[index22,'stories'] = df_v10.loc[index22,'stories'].fillna('One')
# поскольку часть значений заполнили, то нужно снова обновить маску, перед заполнением остальной части
mask_story22 = df_v10.propertyType.str.contains('^florida.*',na=False, regex=True) & df_v10.stories.isna()
# заполним оставшиеся пропуски "Two"
df_v10.loc[mask_story22,'stories'] = 'Two'

flat

In [220]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^flat.*','flat', regex=True)

federal

In [221]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^federal.*','federal', regex=True)

farmhouse

In [222]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^farmhouse.*','farmhouse', regex=True)

farms/ranches

In [223]:
df_v10[df_v10.propertyType.str.contains('^farms/ranches.*',na=False, regex=True)].sort_values('propertyType').stories.value_counts(dropna=False)

stories
NaN             179
1               141
2                37
Farm              6
Two               2
Farm House        1
1.000             1
3                 1
Contemporary      1
1.5               1
1.5 Story         1
Name: count, dtype: int64

In [224]:
# Заполним пропуски в пропорции 0.8 - 1, 0.2 - 2
mask_story22 = df_v10.propertyType.str.contains('^farms/ranches.*',na=False, regex=True) & df_v10.stories.isna()
# заполним первую половину "2"
index22 = df_v10.loc[mask_story22,'stories'].sample(frac=0.8).index
df_v10.loc[index22,'stories'] = df_v10.loc[index22,'stories'].fillna('1')
# поскольку часть значений заполнили, то нужно снова обновить маску, перед заполнением остальной части
mask_story22 = df_v10.propertyType.str.contains('^farms/ranches.*',na=False, regex=True) & df_v10.stories.isna()
# заполним оставшиеся пропуски "2"
df_v10.loc[mask_story22,'stories'] = '2'

farm/ranch

In [225]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^farm/ranch.*','farm/ranch', regex=True)

farm house

In [226]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^farm house.*','farm house', regex=True)

european

In [227]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^european.*','european', regex=True)

english

In [228]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^english.*','english', regex=True)

end unit

In [229]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^end unit.*','end unit', regex=True)

elevated

In [230]:
df_v10[df_v10.propertyType.str.contains('^elevated.*',na=False, regex=True)].sort_values('propertyType').stories.value_counts(dropna=False)

stories
One              23
Two              18
Three Or More     9
NaN               3
Name: count, dtype: int64

In [231]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^elevated.*','elevated', regex=True)

In [232]:
# В основном это 1-2этажные дома, заполним 2
mask_story16 = df_v10.propertyType.str.contains('^elevated.*',na=False, regex=True)
df_v10.loc[mask_story16,'stories'] = df_v10.loc[mask_story16,'stories'].fillna('Two')

dutch

In [233]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^dutch.*','dutch', regex=True)

duplex

In [234]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^duplex.*','duplex', regex=True)

detached

Там где встречается обозначение этажа в этом признаке и пропуски в stories, заполним соответствующим значением

In [235]:
# создам маску для 1 
mask_d = df_v10.propertyType.str.contains('^detached',na=False, regex=True) & df_v10.propertyType.str.contains('one story',na=False, regex=True)
df_v10[mask_d].propertyType.value_counts()

propertyType
detached, one story                           1614
detached, ranch, one story                      81
detached, one story, spanish/mediterranean      53
detached, manufactured home, one story           9
detached, one story, split-level                 7
detached, patio home, one story                  6
detached, one story, two story                   6
detached, one story, duplex                      2
detached, one story, tri-level                   1
Name: count, dtype: int64

In [236]:
df_v10.loc[mask_d,'stories'].isna().sum()

np.int64(1770)

In [237]:
# заполним 1
df_v10.loc[mask_d,'stories'] = df_v10.loc[mask_d,'stories'].fillna('1')

In [238]:
# создам маску для 2
mask_d = df_v10.propertyType.str.contains('^detached',na=False, regex=True) & df_v10.propertyType.str.contains('two story',na=False, regex=True)
df_v10[mask_d].propertyType.value_counts()

propertyType
detached, two story                           638
detached, two story, spanish/mediterranean     67
detached, patio home, two story                13
detached, two story, split-level                9
detached, one story, two story                  6
detached, ranch, two story                      5
detached, two story, tri-level                  2
Name: count, dtype: int64

In [239]:
df_v10.loc[mask_d,'stories'].isna().sum()

np.int64(722)

In [240]:
# заполним 2
df_v10.loc[mask_d,'stories'] = df_v10.loc[mask_d,'stories'].fillna('2')

In [241]:
# Объединим теперь всех в одну
df_v10.propertyType = df_v10.propertyType.str.replace('^detached.*','detached', regex=True)

designated historical home

In [242]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^designated historical home.*','designated historical home', regex=True)

custom home

In [243]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^custom.*','custom', regex=True)

craftsman

In [244]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^craftsman.*','craftsman', regex=True)

courtyard

In [245]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^courtyard.*','courtyard', regex=True)

cottage

In [246]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^cottage.*','cottage', regex=True)

coop

In [247]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^cooperative.*','coop', regex=True)

contemporary

In [248]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^contemporary.*','contemporary', regex=True)

condominium

In [249]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^condominium.*','condominium', regex=True)

condo/unit

In [250]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^condo/unit.*','condo/unit', regex=True)

condo/townhome

In [251]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^condo/townhome.*','condo/townhome', regex=True)

In [252]:
df_v10.propertyType = df_v10.propertyType.str.replace('^condo, other.*','condo', regex=True)

colonial

In [253]:
df_v10.propertyType = df_v10.propertyType.str.replace('^colonial.*','colonial', regex=True)

coastal

In [254]:
# заполним 2
mask_story22 = df_v10.propertyType.str.contains('^coastal two story.*',na=False, regex=True)
df_v10.loc[mask_story22,'stories'] = '2'

In [255]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^coastal.*','coastal', regex=True)

coach/carriage

In [256]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^coach/carriage.*','coach/carriage', regex=True)

co-op

In [257]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^co-op.*','coop', regex=True)

cluster home

In [258]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^cluster home.*','cluster home', regex=True)

charleston

In [259]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^charleston.*','charleston', regex=True)

chalet

In [260]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^chalet.*','chalet', regex=True)

carriage

In [261]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^carriage.*','carriage', regex=True)

cape

In [262]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^cape.*','cape', regex=True)

camp

In [263]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^camp.*','camp', regex=True)

cabin

In [264]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^cabin.*','cabin', regex=True)

bungalow

In [265]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^bungalow.*','bungalow', regex=True)

bilevel

In [266]:
# Объединим
df_v10.propertyType = df_v10.propertyType \
.str.replace('^bilevel.*','bilevel', regex=True) \
.str.replace('^bi-level.*','bilevel', regex=True)

attached

In [267]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^attached.*','attached', regex=True)

arts & crafts

In [268]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^arts & crafts.*','arts & crafts', regex=True)

art deco

In [269]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^art deco.*','art deco', regex=True)

apartment

In [270]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^apartment.*','apartment', regex=True)

a-frame

In [271]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^a-frame.*','a-frame', regex=True)

4+ floors

In [272]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^4\+ floors.*','4plus floors', regex=True)

3+ stories

In [273]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^3\+ stories.*','3plus stories', regex=True)

3 story

In [274]:
# заполним 3
mask_story22 = df_v10.propertyType.str.contains('^3 story.*',na=False, regex=True)
df_v10.loc[mask_story22,'stories'] = '3'

2.5 story

In [275]:
# заполним 2.5
mask_story22 = df_v10.propertyType.str.contains('^2.5 story.*',na=False, regex=True)
df_v10.loc[mask_story22,'stories'] = '2.5'

2 stories

In [276]:
# Объединим
df_v10.propertyType = df_v10.propertyType \
.str.replace('^2 stories.*','2 stories', regex=True) \
.str.replace('^2 story.*','2 stories', regex=True) \
.str.replace('^2-story.*','2 stories', regex=True)

In [277]:
# В основном это 2этажные дома, заполним 2
mask_story16 = df_v10.propertyType.str.contains('^2 stories.*',na=False, regex=True)
df_v10.loc[mask_story16,'stories'] = df_v10.loc[mask_story16,'stories'].fillna('2')

1 story

In [278]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^1 story.*','1 story', regex=True)

In [279]:
# В основном это 1этажные дома, заполним 1
mask_story16 = df_v10.propertyType.str.contains('^1 story.*',na=False, regex=True)
df_v10.loc[mask_story16,'stories'] = df_v10.loc[mask_story16,'stories'].fillna('1')

1 1/2 story

In [280]:
# Объединим
df_v10.propertyType = df_v10.propertyType.str.replace('^1 1/2 story.*','1.5 story', regex=True)

In [281]:
# заполним 1.5
mask_story16 = df_v10.propertyType.str.contains('^1.5 story.*',na=False, regex=True)
df_v10.loc[mask_story16,'stories'] = df_v10.loc[mask_story16,'stories'].fillna('1.5')

Осталось заполнить пропуски ' ' и nan

In [282]:
# заполним unknown
df_v10.loc[df_v10.propertyType==' ','propertyType'] = 'unknown'
df_v10.propertyType = df_v10.propertyType.fillna('unknown')

Наконец-то с этим признаком покончено!
___

In [283]:
# сохраним промежуточный результат
df_v10.to_pickle("data/df_v11.pkl")

___

**Признак street**

In [284]:
# считаем
df_v11 = pd.read_pickle("data/df_v11.pkl")

Информация в этом признаке мало пригодна для построения модели.  
Было бы намного удобнее использовать информацию о конкретном районе, есть благополучные и неблагополучные районы, от этого цена должна значительно зависеть.  
Впринципе вариант решения данной задачи есть. Есть сервисы, которые по адресу выдают координаты Latitude/Longitude. Но вручную прогонять все адреса - это смерти подобно. Хотя у них есть подписка, или даже можно api наверное купить, которая позволит разом загнать весь список адресов.  
Но это задача не для нашей дипломной работы.  

___
**Признак baths**

In [285]:
df_v11.baths.unique()

array(['3.5', '3 Baths', '2 Baths', '8 Baths', nan, '2', '3',
       'Bathrooms: 2', '1,750', '4 Baths', '2 ba', 'Bathrooms: 5',
       '1,000', '7 Baths', '2.0', '3.0', 'Bathrooms: 1', '4.0',
       '2.1 Baths', '2.5 Baths', '1', 'Bathrooms: 3', '4.5', '6 Baths',
       'Bathrooms: 4', '3 ba', '5', '2,500', '5.5 Baths', '1.0',
       '5 Baths', '1.5', '4', '~', '2.5', '4,000', '3.5 Baths', '2,000',
       '3,000', '8.0', '1 ba', '3.5 ba', '0', '5.0', '1,500', '7.0',
       '1,250', '9 Baths', '2,250', '6.0', '12 Baths', '5.5', '3,500',
       '1.5 Baths', '2,750', 'Bathrooms: 6', '4.5 Baths', '750', '5.5+',
       '6', '10 Baths', '6 ba', 'Bathrooms: 19', '10.0', '1.5 ba', '4 ba',
       '12 ba', '2.5+', '8', '7.5+', 'Bathrooms: 10', '0 / 0', 'Sq. Ft. ',
       '5 ba', '4.5+', '18 Baths', '-- baths', 'Bathrooms: 7', '7', '18',
       '3.5+', '1.5+', '11 Baths', '5,000', '1.75 Baths', '9', '12.0',
       '1.1 Baths', '6.5', 'Bathrooms: 8', '10', '19 Baths',
       'Bathrooms: 9', '16 B

In [286]:
# Удалим все буквы, поскольку нам важно только количество
df_v11.baths = df_v11.baths.str.replace('[a-zA-Z]','', regex=True)
# Удалим все пробелы
df_v11.baths = df_v11.baths.str.replace(' ','', regex=True)
# Удалим все :
df_v11.baths = df_v11.baths.str.replace(':','', regex=True)

In [287]:
df_v11.baths.unique()

array(['3.5', '3', '2', '8', nan, '1,750', '4', '5', '1,000', '7', '2.0',
       '3.0', '1', '4.0', '2.1', '2.5', '4.5', '6', '2,500', '5.5', '1.0',
       '1.5', '~', '4,000', '2,000', '3,000', '8.0', '0', '5.0', '1,500',
       '7.0', '1,250', '9', '2,250', '6.0', '12', '3,500', '2,750', '750',
       '5.5+', '10', '19', '10.0', '2.5+', '7.5+', '0/0', '..', '4.5+',
       '18', '--', '3.5+', '1.5+', '11', '5,000', '1.75', '12.0', '1.1',
       '6.5', '16', '13', '14', '9.0', '8.5+', '17', '241', '16.0',
       '10.5+', '6.5+', '7,500+', '7.5', '11.0', '20', '40', '1-0/1-0/1',
       '14.0', '2.75', '24', '22.0', '0.00', '2.25', '3.1', '3.25', '—',
       '22', '32', '18.0', '0.0', '27', '26', '20.0', '9.5', '8.5', '15',
       '35', '3.75', '29', '116/116/116', '21', '5.2', '14.5+', '76',
       '13.0', '', '3-1/2-2', '15.0', '23', '3.3', '43', '1.25', '34',
       '2.2', '1/1/1/1', '55.0', '25', '12.5+', '44', '0.5', '4.25',
       '4.75', '0.75', '4.1', '5.25', '41.0', '1.8', '10.5

Анализ и поиск по интернету дал мне следующую информацию:  
A 2.5 bath would mean two full bathrooms, and one half bathroom. A 1.75 bath would mean one full bathroom, and one three-quarter bathroom. A 1.5 bath would mean one full bathroom, and one half bathroom. And a 2.25 bath would be a full bathroom, a three-quarter bathroom, and a half bathroom.    

Также встречаются значения разделенные запятой, например '1,750', '1,000', и т.д. 
И вот тут непонятно, что это? Размеры самой ванны или площадь ванных комнат..?

Так как четкого понимани нет, что есть допустимое значение, а что есть ошибка в записи. То оставим все полученные значения как есть, за исключением явных несоответствий и пропусков. Замена пустых строк кодируется так: str.replace(r'^\s*$','unknown', regex=True)

Еще один из непонятных вариантов значений это значения через /. Но это разово встречающиеся значения, поэтому заменю их на unknown

In [288]:
df_v11.baths = df_v11.baths.fillna('unknown')
df_v11.baths = df_v11.baths \
.str.replace('~','unknown', regex=True) \
.str.replace('\.\.','unknown', regex=True) \
.str.replace('--','unknown', regex=True) \
.str.replace('—','unknown', regex=True) \
.str.replace('^\s*$','unknown', regex=True) \
.str.replace('1-0/1-0/1','unknown', regex=True) \
.str.replace('116/116/116','unknown', regex=True) \
.str.replace('3-1/2-2','unknown', regex=True) \
.str.replace('1/1/1/1','unknown', regex=True) \
.str.replace('2-1/2-1/1-1/1-1','unknown', regex=True) \
.str.replace('1/1-0/1-0/1-0','unknown', regex=True) \
.str.replace('.*unknown.*','unknown', regex=True) \
.str.replace('1-2','unknown', regex=True) \
.str.replace('^0.0+','0', regex=True)

In [289]:
df_v11.baths.sort_values().unique()

array(['0', '0.5', '0.75', '1', '1,000', '1,250', '1,500', '1,750', '1.0',
       '1.1', '1.25', '1.5', '1.5+', '1.75', '1.8', '10', '10.0', '10.5',
       '10.5+', '11', '11.0', '11.5', '11.5+', '12', '12.0', '12.5',
       '12.5+', '13', '13.0', '14', '14.0', '14.5+', '15', '15.0', '16',
       '16.0', '17', '17.0', '18', '18.0', '19', '2', '2,000', '2,250',
       '2,500', '2,750', '2.0', '2.1', '2.2', '2.25', '2.5', '2.5+',
       '2.75', '2.8', '20', '20.0', '21', '22', '22.0', '23', '23.0',
       '24', '24.0', '241', '25', '26', '27', '28', '29', '3', '3,000',
       '3,500', '3.0', '3.1', '3.2', '3.25', '3.3', '3.5', '3.5+', '3.75',
       '30', '30.0', '32', '34', '34.0', '35', '36', '39', '4', '4,000',
       '4.0', '4.1', '4.25', '4.5', '4.5+', '4.75', '40', '41.0', '42',
       '43', '44', '44.0', '5', '5,000', '5.0', '5.2', '5.25', '5.5',
       '5.5+', '55.0', '6', '6.0', '6.5', '6.5+', '6.75', '60', '64.0',
       '68', '7', '7,500+', '7.0', '7.5', '7.5+', '750', '76', '

In [290]:
df_v11.baths.unique().shape

(134,)

Проверим одну гипотезу, что значения целого числа и дробного с одной цифрой после запятой - это одно и то же

In [291]:
df_v11[df_v11.baths.isin(['10.0'])].sort_values('street')

status   propertyType                        street baths  \
50670     forsale  single family         (undisclosed Address)  10.0   
333880    forsale  single family             1006 Chantilly Rd  10.0   
206902  undefined  single family             101 N Hibiscus Dr  10.0   
202132  undefined  single family             10255 Lakeside Dr  10.0   
63860     forsale  single family             10410 Bellagio Rd  10.0   
131414  undefined  single family              10835 SW 36th St  10.0   
74831     forsale  single family              12745 Hanover St  10.0   
24711     forsale  single family          1307 Sierra Alta Way  10.0   
264031    forsale  single family               13151 Rivers Rd  10.0   
285556  undefined  single family             13920 Stirling Rd  10.0   
47402   undefined  single family                1401 W 27th St  10.0   
141273    forsale  single family               14035 Aubrey Rd  10.0   
119848    forsale  single family            141 S Carolwood Dr  10.0   
205525    forsale  single family               1421 N Astor St  10.0   
169397  undefined  single family                1510 W 25th St  10.0   
5811    undefined   multi family             1650 Micanopy Ave  10.0   
208047    forsale  single family                17111 El Vuelo  10.0   
149251  undefined  single family                 2111 Lake Ave  10.0   
217882  undefined  single family             2180 Eventide Ave  10.0   
48630     forsale  single family           225 Blackland Rd NW  10.0   
83606     forsale  single family               23 Needle Grass  10.0   
1359    undefined          condo  2417 Fisher Island Dr # 5107  10.0   
140533  undefined      townhouse       251 Crandon Blvd TH 161  10.0   
190518  undefined  single family                252 Bal Bay Dr  10.0   
51599     forsale  single family               2555 Webster St  10.0   
53264     forsale   multi family             2601 E Lamona Ave  10.0   
224279    forsale  single family        2645 Howell Mill Rd NW  10.0   
78572   undefined  single family              333 Elizabeth Rd  10.0   
111146    forsale  single family             3617 Tuxedo Ct NW  10.0   
275042  undefined  single family          3650 University Blvd  10.0   
268446  undefined   multi family        3907 E Southcross Blvd  10.0   
346018    forsale  single family    4320 Rancho Las Brisas Trl  10.0   
4214      forsale  single family  450 W Lake Sammamish Pkwy SE  10.0   
141057  undefined  single family               500 Arvida Pkwy  10.0   
195585  undefined  single family                 5004 N Bay Rd  10.0   
373990    forsale  single family          5026 S Greenwood Ave  10.0   
282470  undefined  single family       515 Casuarina Concourse  10.0   
97869     forsale  single family          5156 Scenic Ridge Dr  10.0   
276722  undefined  single family                 5242 N Bay Rd  10.0   
218523  undefined  single family               5880 SW 94th St  10.0   
71112   undefined  single family              6301 Pinetree Dr  10.0   
79120   undefined  single family               6520 SW 94th St  10.0   
162332  undefined          condo  6893 Fisher Island Dr # 6893  10.0   
166532    forsale  single family        7400 Vista Del Mar Ave  10.0   
202184  undefined   multi family           745 Lenox Ave # 747  10.0   
26282   undefined  single family                777 E Olmos Dr  10.0   
348540    forsale  single family            7863 Mulholland Dr  10.0   
53970     forsale  single family                8 Beverly Park  10.0   
282712    forsale  single family        8185 Clearwater Pointe  10.0   
87782     forsale  single family           8366 Sunset View Dr  10.0   
352089    forsale  single family             8854 Thrasher Ave  10.0   
14904   undefined  single family               9175 SW 63rd Ct  10.0   
38064   undefined  single family              9320 Gallardo St  10.0   
370564  undefined  single family           9530 W Broadview Dr  10.0   
35115     forsale  single family              99 Ha

Видимо так и есть, так как встречаются идентичные записи, отличающиеся только этим нюансом. Есть смысл объединить эти значения. Также есть одно значение '241', считаю это явной опечаткой, и скорее всего лишняя последняя 1.

In [292]:
df_v11.baths = df_v11.baths \
.str.replace('23.0','23', regex=True) \
.str.replace('44.0','44', regex=True) \
.str.replace('34.0','34', regex=True) \
.str.replace('30.0','30', regex=True) \
.str.replace('24.0','24', regex=True) \
.str.replace('241','24', regex=True) \
.str.replace('22.0','22', regex=True) \
.str.replace('20.0','20', regex=True) \
.str.replace('18.0','18', regex=True) \
.str.replace('17.0','17', regex=True) \
.str.replace('16.0','16', regex=True) \
.str.replace('15.0','15', regex=True) \
.str.replace('14.0','14', regex=True) \
.str.replace('13.0','13', regex=True) \
.str.replace('12.0','12', regex=True) \
.str.replace('11.0','11', regex=True) \
.str.replace('10.0','10', regex=True)

Со значениями менее 10 у меня почему-то нет уверенности, что их можно также объединить. Оставлю как есть.

In [293]:
df_v11.baths.unique().shape

(117,)

___
**Анализ признака homeFacts**

С помощью регулярных выражений выдерним из этого признака значения для factValue и factLabel

In [294]:
# factValue
ser_val = df_v11.homeFacts.str.findall(r"\bfactValue': ([\s\S]+?), 'factLabel\b")
ser_val

0         ['2019', '', 'Central A/C, Heat Pump', '', '',...
1         ['2019', '', '', '', '', '5828 sqft', '$159/sq...
2         ['1961', '1967', 'Forced Air', 'Central', 'Att...
3         ['2006', '2006', 'Forced Air', 'Central', 'Det...
4                 ['', '', '', '', '', '10,019 sqft', None]
                                ...                        
377039    ['1990', '1990', 'Other', 'Central', '2 spaces...
377040    ['1924', '', 'Radiant', '', 'None', '', '$337/...
377041    ['1950', '1950', 'Other', '', '2', '1,600 sqft...
377042           [None, None, None, None, None, None, None]
377043    ['2019', None, 'Electric', 'Central', 'No Data...
Name: homeFacts, Length: 376752, dtype: object

In [295]:
ser_val[0]

["'2019'", "''", "'Central A/C, Heat Pump'", "''", "''", 'None', "'$144'"]

In [296]:
len(ser_val[0])

7

In [297]:
ser_val_len = pd.Series(ser_val.apply(lambda x: len(x)))
ser_val_len.unique()

array([7])

Видим, что структура одинаковая по размерности для каждой записи

In [298]:
# factLabel
ser_labl = df_v11.homeFacts.str.findall(r"\bfactLabel': ([\s\S]+?)'factValue\b")

In [299]:
ser_labl[0]

["'Year built'}, {",
 "'Remodeled year'}, {",
 "'Heating'}, {",
 "'Cooling'}, {",
 "'Parking'}, {",
 "'lotsize'}, {"]

In [300]:
ser_labl_len = pd.Series(ser_labl.apply(lambda x: len(x)))
ser_labl_len.unique()

array([6])

А вот тут странно! Почему 6, а не 7 элементов?

Немного изменим запрос в регулярном выражении:

In [301]:
ser_label = df_v11.homeFacts.str.findall(r"\bfactLabel': ([\s\S]+?)[}\b]")

In [302]:
ser_label[100]

["'Year built'",
 "'Remodeled year'",
 "'Heating'",
 "'Cooling'",
 "'Parking'",
 "'lotsize'",
 "'Price/sqft'"]

In [303]:
ser_label_len = pd.Series(ser_label.apply(lambda x: len(x)))
ser_label_len.unique()

array([7])

Осталось оформить это в виде фрейма и присоединить к нашему рабочему фрейму

Поскольку структура одинаковая, и названия factLabel одни и те же, то создадим список этих названий

In [304]:
# создадим список названий признаков, удалив лишние кавычки
list_priznak = ','.join(ser_label[0]).replace("'","").split(',')
list_priznak

['Year built',
 'Remodeled year',
 'Heating',
 'Cooling',
 'Parking',
 'lotsize',
 'Price/sqft']

In [305]:
# Создадим эти признаки в нашем фрейме
for i, val in enumerate(list_priznak):
    df_v11[val]=ser_val.apply(lambda x: x[i])

In [306]:
df_v11.head()

status   propertyType               street    baths  \
0   active  single family       240 Heather Ln      3.5   
1  forsale  single family    12911 E Heroy Ave        3   
2  forsale  single family    2005 Westridge Rd        2   
3  forsale  single family  4311 Livingston Ave        8   
4  forsale       lot/land       1524 Kiscoe St  unknown   

                                           homeFacts fireplace  \
0  {'atAGlanceFacts': [{'factValue': '2019', 'fac...  Gas Logs   
1  {'atAGlanceFacts': [{'factValue': '2019', 'fac...       NaN   
2  {'atAGlanceFacts': [{'factValue': '1961', 'fac...       yes   
3  {'atAGlanceFacts': [{'factValue': '2006', 'fac...       yes   
4  {'atAGlanceFacts': [{'factValue': '', 'factLab...       NaN   

             city                                            schools  \
0  Southern Pines  [{'rating': ['4', '4', '7', 'NR', '4', '7', 'N...   
1  Spokane Valley  [{'rating': ['4/10', 'None/10', '4/10'], 'data...   
2     Los Angeles  [{'rating': ['8/10', '4/10', '8/10'], 'data': ...   
3          Dallas  [{'rating': ['9/10', '9/10', '10/10', '9/10'],...   
4        Palm Bay  [{'rating': ['4/10', '5/10', '5/10'], 'data': ...   

         sqft zipcode  ... stories      target   Pool Year built  \
0        2900   28387  ...     NaN    $418,000  False     '2019'   
1  1,947 sqft   99216  ...     2.0    $310,000  False     '2019'   
2  3,000 sqft   90049  ...     1.0  $2,895,000   True     '1961'   
3  6,457 sqft   75205  ...     3.0  $2,395,000  False     '2006'   
4         NaN   32908  ...     NaN      $5,000  False         ''   

   Remodeled year                   Heating    Cooling            Parking  \
0              ''  'Central A/C, Heat Pump'         ''                 ''   
1              ''                        ''         ''                 ''   
2          '1967'              'Forced Air'  'Central'  'Attached Garage'   
3          '2006'              'Forced Air'  'Central'  'Detached Garage'   
4              ''                        ''         ''                 ''   

         lotsize   Price/sqft  
0           None       '$144'  
1    '5828 sqft'  '$159/sqft'  
2   '8,626 sqft'  '$965/sqft'  
3   '8,220 sqft'  '$371/sqft'  
4  '10,019 sqft'         None  

[5 rows x 22 columns]

In [307]:
# Теперь признак homeFacts можно удалить
df_v11 = df_v11.drop('homeFacts', axis=1)

Посмотрим на каждый новый признак более пристально

In [308]:
df_v11['Year built'].value_counts()

Year built
''        58408
'2019'    32146
'2006'     8007
'2005'     7503
'2007'     7151
          ...  
'1019'        1
'1805'        1
'1843'        1
'1808'        1
'1804'        1
Name: count, Length: 231, dtype: int64

In [309]:
# удалим лишние кавычки
df_v11['Year built'] = df_v11['Year built'].str.replace("'",'', regex=True)

In [310]:
df_v11['Year built'].sort_values().unique()

array(['', '1', '1019', '1057', '1060', '1208', '1700', '1703', '1735',
       '1740', '1750', '1780', '1788', '1790', '1794', '1795', '1796',
       '1799', '1800', '1802', '1803', '1804', '1805', '1807', '1808',
       '1809', '1810', '1811', '1812', '1815', '1816', '1817', '1818',
       '1820', '1822', '1823', '1824', '1825', '1828', '1829', '1830',
       '1831', '1832', '1834', '1835', '1836', '1840', '1842', '1843',
       '1844', '1845', '1846', '1847', '1848', '1850', '1851', '1852',
       '1853', '1854', '1855', '1856', '1857', '1858', '1859', '1860',
       '1861', '1862', '1863', '1864', '1865', '1866', '1867', '1868',
       '1869', '1870', '1871', '1872', '1873', '1874', '1875', '1876',
       '1877', '1878', '1879', '1880', '1881', '1882', '1883', '1884',
       '1885', '1886', '1887', '1888', '1889', '1890', '1891', '1892',
       '1893', '1894', '1895', '1896', '1897', '1898', '1899', '1900',
       '1901', '1902', '1903', '1904', '1905', '1906', '1907', '1908',
     

Для начала удалим пустые строки, вернее заменим их на 'None'

In [311]:
df_v11['Year built'] = df_v11['Year built'].str.replace('^\s*$','None', regex=True)

Также есть значения, которые тоже придется заменить на 'None' - это '1', '1208', '559990649990' и 'No Data'

In [312]:
# создам маску
mask_year = df_v11['Year built'].isin(['1','1208','559990649990','No Data'])
# заменю по маске
df_v11.loc[mask_year,'Year built'] = 'None'

Также есть значения '1019', '1057', '1060' это тоже не корректные значения и их можно было бы занести в группу 'None', но у меня есть предположение, что это ошибка ввода человеческого фактора, то есть человек просто промазал и нажал 0 вместо 9, так как кнопки рядом находятся.

In [313]:
# Заменим в этих трех случаях 0 на 9
df_v11.loc[df_v11['Year built']=='1019','Year built'] = '1919'
df_v11.loc[df_v11['Year built']=='1057','Year built'] = '1957'
df_v11.loc[df_v11['Year built']=='1060','Year built'] = '1960'

In [314]:
df_v11['Year built'].sort_values().unique()

array(['1700', '1703', '1735', '1740', '1750', '1780', '1788', '1790',
       '1794', '1795', '1796', '1799', '1800', '1802', '1803', '1804',
       '1805', '1807', '1808', '1809', '1810', '1811', '1812', '1815',
       '1816', '1817', '1818', '1820', '1822', '1823', '1824', '1825',
       '1828', '1829', '1830', '1831', '1832', '1834', '1835', '1836',
       '1840', '1842', '1843', '1844', '1845', '1846', '1847', '1848',
       '1850', '1851', '1852', '1853', '1854', '1855', '1856', '1857',
       '1858', '1859', '1860', '1861', '1862', '1863', '1864', '1865',
       '1866', '1867', '1868', '1869', '1870', '1871', '1872', '1873',
       '1874', '1875', '1876', '1877', '1878', '1879', '1880', '1881',
       '1882', '1883', '1884', '1885', '1886', '1887', '1888', '1889',
       '1890', '1891', '1892', '1893', '1894', '1895', '1896', '1897',
       '1898', '1899', '1900', '1901', '1902', '1903', '1904', '1905',
       '1906', '1907', '1908', '1909', '1910', '1911', '1912', '1913',
      

In [315]:
# Какую часть занимают строки с незаполненным Year built
df_v11[df_v11['Year built']=='None'].shape[0]/df_v11.shape[0]*100

16.78663948698348

Таких пропусков почти 17%, это достаточно много, чтобы просто удалить строки, но мало, чтобы удалить весь признак.  
К тому же есть предположение, что пропуски будут в основном там где типом является земельный участок, а не дом.

In [316]:
df_v11[df_v11['propertyType'].isin(['lot/land','land'])]['Year built'].value_counts()

Year built
None    26755
1940      189
1950      173
1920      139
2017      127
        ...  
1879        1
1877        1
1883        1
1884        1
1853        1
Name: count, Length: 154, dtype: int64

И перевести данный признак в числовой тип или в тип даты тоже не получится из-за наличия 'None'. Придется оставить так как есть и закончить с разбором этого признака

Посмотрим на признак Remodeled year

In [317]:
df_v11['Remodeled year'].value_counts()

Remodeled year
''        199135
None       26556
'2006'      5537
'2005'      4817
'2007'      4386
           ...  
'1853'         1
'1800'         1
'1888'         1
'1738'         1
'1862'         1
Name: count, Length: 155, dtype: int64

In [318]:
df_v11['Remodeled year'].sort_values().unique()

array(["''", "'0'", "'1111'", "'1738'", "'1800'", "'1845'", "'1846'",
       "'1853'", "'1862'", "'1869'", "'1870'", "'1874'", "'1876'",
       "'1877'", "'1880'", "'1883'", "'1884'", "'1885'", "'1886'",
       "'1887'", "'1888'", "'1889'", "'1890'", "'1891'", "'1892'",
       "'1893'", "'1894'", "'1895'", "'1896'", "'1897'", "'1898'",
       "'1899'", "'1900'", "'1901'", "'1902'", "'1903'", "'1904'",
       "'1905'", "'1906'", "'1907'", "'1908'", "'1909'", "'1910'",
       "'1911'", "'1912'", "'1913'", "'1914'", "'1915'", "'1916'",
       "'1917'", "'1918'", "'1919'", "'1920'", "'1921'", "'1922'",
       "'1923'", "'1924'", "'1925'", "'1926'", "'1927'", "'1928'",
       "'1929'", "'1930'", "'1931'", "'1932'", "'1933'", "'1934'",
       "'1935'", "'1936'", "'1937'", "'1938'", "'1939'", "'1940'",
       "'1941'", "'1942'", "'1943'", "'1944'", "'1945'", "'1946'",
       "'1947'", "'1948'", "'1949'", "'1950'", "'1951'", "'1952'",
       "'1953'", "'1954'", "'1955'", "'1956'", "'1957'", "'

Пропуски в этом признаке составляют:

In [319]:
df_v11[df_v11['Remodeled year'].isin(["''", "'0'", "'1111'",'None'])].shape[0]/df_v11.shape[0]*100

59.97632394784899

60 % пропусков в признаке -это явный кандидат ну удаление. Удалим данный признак

In [320]:
# удалим признак 'Remodeled year'
df_v11 = df_v11.drop('Remodeled year', axis=1)

Посмотрим на признак 'Heating'

In [321]:
df_v11['Heating'].str.lower().nunique()

1919

In [322]:
df_v11['Heating'].str.lower().value_counts().head(30)

Heating
'forced air'                     134283
''                               105434
'other'                           29615
'electric'                        10209
'gas'                              9289
'heat pump'                        8850
'no data'                          8607
'central air'                      7814
'central electric'                 7112
'central'                          6247
'central, electric'                4253
'baseboard'                        3813
none                               3531
'wall'                             3301
'electric heat'                    3064
'heating system'                   2706
'forced air, heat pump'            1767
'radiant'                          1485
'central air, ceiling fan(s)'      1432
'natural gas heat'                 1383
'central furnace'                  1036
'forced air, gas'                   962
'central electric, zoned'           873
'forced air heating'                810
', gas hot air/furnace'         

Что показывает анализ данного признака? Во-первых, очень большое количество уникальных значений, что будет доставлять определенные сложности для построения модели. Во-вторых, пропуски составляют порядка 117572 значений, а это составляет 31% от всех значений. Ну и в-третьих, считаю, что тип отопления не будет заметно сказываться на формировании цены. По всему этому принимаю решение удалить этот признак.

In [323]:
# удалим признак 'Heating'
df_v11 = df_v11.drop('Heating', axis=1)

Посмотрим на признак Cooling

In [324]:
df_v11['Cooling'].str.lower().nunique()

1439

In [325]:
df_v11['Cooling'].str.lower().value_counts().head(30)

Cooling
'central'                                            158710
''                                                   120059
'central air'                                         14384
'no data'                                             10612
'has cooling'                                          9730
'none'                                                 7387
'central electric'                                     6154
'wall'                                                 4017
'central gas'                                          3573
none                                                   3531
'central heating'                                      2807
'cooling system'                                       2697
'central a/c'                                          2051
'other'                                                1840
'central a/c (electric), central heat (gas)'           1646
'central a/c (electric), central heat (electric)'      1429
'refrigeration'                 

Что показывает анализ данного признака?   
Ситуация схожая с признаком 'Heating'. Во-первых, очень большое количество уникальных значений, что будет доставлять определенные сложности для построения модели. Во-вторых, пропуски составляют порядка 141589 значений, а это составляет 37% от всех значений.  По всему этому принимаю решение удалить этот признак.

In [326]:
# удалим признак 'Cooling'
df_v11 = df_v11.drop('Cooling', axis=1)

Посмотрим на признак Parking

In [327]:
df_v11['Parking'].str.lower().nunique()

3321

In [328]:
df_v11['Parking'].str.lower().value_counts().head(30)

Parking
''                                    171509
'attached garage'                      70727
'2 spaces'                             28058
'1 space'                              14250
'no data'                              13329
'detached garage'                      13198
'carport'                               7741
'off street'                            5278
'3 spaces'                              4724
none                                    3531
'carport, attached garage'              3025
'1'                                     2935
'4 spaces'                              2917
'2'                                     2753
'none'                                  2367
'on street'                             1707
'attached garage, detached garage'      1354
'0'                                     1114
'attached garage, carport'               993
'parking desc'                           900
'6 spaces'                               755
'detached garage, attached garage'       726
'd

Наблюдаем похожую ситуацию. Очень много уникальных значений! Пропуски составляют порядка 190736 значений, а это составляет 50% от всех значений. По всему этому принимаю решение удалить этот признак.

In [329]:
# удалим признак 'Parking'
df_v11 = df_v11.drop('Parking', axis=1)

Посмотрим на признак lotsize

В терминах недвижимости lot size указывает на размер участка земли, на котором находится недвижимость.

In [330]:
df_v11['lotsize'].str.lower().nunique()

36605

In [331]:
df_v11['lotsize'].str.lower().value_counts().head(30)

lotsize
''               33038
none             28322
'—'              25215
'no data'         5328
'-- sqft lot'     3818
'0.26 acres'      3135
'0.25 acres'      2721
'0.28 acres'      2613
'0.27 acres'      2472
'0.29 acres'      2351
'0.34 acres'      1951
'0.31 acres'      1720
'0.32 acres'      1581
'6,098 sqft'      1524
'0.3 acres'       1436
'0.33 acres'      1412
'7,405 sqft'      1357
'0.35 acres'      1354
'1 acre'          1346
'6,534 sqft'      1292
'0.46 acres'      1284
'4,356 sqft'      1270
'10,000 sqft'     1260
'0.36 acres'      1224
'5,227 sqft'      1175
'0.37 acres'      1172
'5,000 sqft'      1117
'8,712 sqft'      1030
'0.38 acres'       994
'3,920 sqft'       993
Name: count, dtype: int64

Вообще данный признак считаю достаточно значимым для формирования цены. Но!  
Снова имеем много пропусков 91903, что составляет 24%

Впринципе, имея опять же много свободного времени, можно было бы поработать с этим признаком. Перевести акры в футы. Очистить от лишних символов. Но есть например значение '-- sqft lot', что оно означает, то-ли пропуск, то-ли что-то значимое?

Еще раз выражаю мнение, что данные Очень замусорены! С такими данными ожидать качественного предсказания не приходится!

In [332]:
# удалим признак 'lotsize'
df_v11 = df_v11.drop('lotsize', axis=1)

Посмотрим на признак Price/sqft

Данный признак напрямую зависит от целевого признака. Поэтому оставлять его нельзя, иначе будет утечка данных.

In [333]:
# удалим признак 'Price/sqft'
df_v11 = df_v11.drop('Price/sqft', axis=1)

**Посмотрим на признак fireplace**

In [334]:
df_v11['fireplace'].str.lower().nunique()

1651

In [335]:
df_v11['fireplace'].isna().sum()

np.int64(273656)

Пропусков много больше половины, удаляем данный признак

In [336]:
# удалим признак 'fireplace'
df_v11 = df_v11.drop('fireplace', axis=1)

**Посмотрим на признак city**

In [337]:
df_v11['city'].nunique()

2026

посмотрим есть ли различное написание в разрезе заглавных букв

In [338]:
df_v11['city'].str.title().nunique()

1909

Предположение подтвердилось. Значит стоит привести к единообразию:

In [339]:
df_v11['city'] = df_v11['city'].str.title()

In [340]:
city_list = df_v11['city'].sort_values().unique().tolist()
city_list[1000:1020]

['Mallie',
 'Manchaca',
 'Mangonia Park',
 'Manhattan',
 'Manor',
 'Mansfield',
 'Manvel',
 'Maple Heights',
 'Maple Springs',
 'Maple Valley',
 'Margate',
 'Marina Del Rey',
 'Marion',
 'Marion Oaks',
 'Marshall',
 'Marstons Mills',
 'Martinez',
 'Marysville',
 'Mason City',
 'Maspeth']

Есть в этом признаке один момент, который стоит обработать. Существуют значения, например 'Allentown' и 'Allentown City'; 'Anderson Township' и 'Anderson Twp'; 'Asheville' и 'Asheville City'; 'Atlaanta' и 'Atlanta'и т.д. Которые явно обозначают один и тот же город, но имеют немного разное написание.

In [341]:
df_v11.city = df_v11.city \
.replace({'Allentown City':'Allentown'}) \
.replace({'Anderson Twp':'Anderson Township'}) \
.replace({'Asheville City':'Asheville'}) \
.replace({'Atlaanta':'Atlanta'}) \
.replace({'Bainbridge Is':'Bainbridge Island'}) \
.replace({'Bay Harbor Is':'Bay Harbor Islands'}) \
.replace({'Bedford Hts':'Bedford Heights'}) \
.replace({'Bee Caves':'Bee Cave'}) \
.replace({'Belllingham':'Bellingham'}) \
.replace({'Bonita Spgs':'Bonita Springs'}) \
.replace({'College Pt':'College Point'}) \
.replace({'Columbia Twp':'Columbia Township'}) \
.replace({'Commercecity':'Commerce City'}) \
.replace({'Doctor Philips':'Doctor Phillips'}) \
.replace({'Fairfield Twp.':'Fairfield Twp'}) \
.replace({'Federalheights':'Federal Heights'}) \
.replace({'Ft Lauderdale':'Fort Lauderdale'}) \
.replace({'Ft Worth':'Fort Worth'}) \
.replace({'Ft. Worth':'Fort Worth'}) \
.replace({'Herkimer Ny':'Herkimer'}) \
.replace({'Hide A Way Hills':'Hideaway Hills'}) \
.replace({'High Pt':'High Point'}) \
.replace({'Hollywood Pa':'Hollywood Park'}) \
.replace({'Jamaica Est':'Jamaica Estates'}) \
.replace({'Jc':'Johnson City'}) \
.replace({'Lakewood Twp.':'Lakewood'}) \
.replace({'Lehigh':'Lehigh Acres'}) \
.replace({'Los Feliz L':'Los Angeles'}) \
.replace({'Other City Value Out Of Area':'Jacksonville'}) \
.replace({'Jacinto City':'Houston'}) \
.replace({'St Albans City':'St. Albans City'}) \
.replace({'Poughkeepsie City':'Poughkeepsie'}) \
.replace({'New York City':'New York'}) \
.replace({'West Panama City Beach':'Panama City Beach'}) \
.replace({'P C Beach':'Panama City Beach'}) \
.replace({'Spring City':'Cleveland'}) \
.replace({'Citrus Heights':'Sacramento'}) \
.replace({'Allentown City':'Allentown'})

In [342]:
# Также случайно наткнулся на ошибку в названии города у записи 47347
df_v11.loc[47347]

status                                                    forsale
propertyType                                        single family
street                                             712 N 74th Ave
baths                                                         3.0
city                                                          Ave
schools         [{'rating': ['9/10', '4/10', '4/10'], 'data': ...
sqft                                                        2,403
zipcode                                                     98908
beds                                                            4
state                                                          WA
stories                                                         0
target                                                   $489,900
Pool                                                        False
Year built                                                   2015
Name: 47347, dtype: object

In [343]:
# У этого объекта город на самом деле Yakima. Снова сталкиваемся с отвратительным качеством входных данных. Исправим.
df_v11.loc[47347,'city']='Yakima'

In [344]:
# Наткнулся еще на одну ошибку в записи строки 321986
df_v11.loc[321986]

status                                                    forsale
propertyType                                             lot/land
street                                     31-4 S 14w Panama #14W
baths                                                     unknown
city                                                   City Beach
schools         [{'rating': ['3/10', '4/10', '8/10'], 'data': ...
sqft                                                          NaN
zipcode                                                     32408
beds                                                          NaN
state                                                          FL
stories                                                       NaN
target                                                   $100,000
Pool                                                        False
Year built                                                   None
Name: 321986, dtype: object

In [345]:
# У этого объекта город на самом деле Panama City Beach.
df_v11.loc[321986,'city']='Panama City Beach'

In [346]:
# Наткнулся еще на одну ошибку в записи строки 238856
df_v11.loc[238856]

status                                                    forsale
propertyType                                                condo
street                                3726 Las Vegas Blvd S #2404
baths                                                     unknown
city                                                  City Center
schools         [{'rating': ['7/10', '4/10', 'None/10'], 'data...
sqft                                                     548 sqft
zipcode                                                     89158
beds                                                          NaN
state                                                          NV
stories                                                       9.0
target                                                   $345,000
Pool                                                        False
Year built                                                   2007
Name: 238856, dtype: object

In [347]:
# У этого объекта город на самом деле Las Vegas.
df_v11.loc[238856,'city']='Las Vegas'

In [348]:
# Наткнулся еще на одну ошибку в записи строки 189616
df_v11.loc[189616]

status                                                    forsale
propertyType                                        single family
street                                             304 Carlton Dr
baths                                                           2
city                                                      De Witt
schools         [{'rating': ['4/10', '3/10'], 'data': {'Distan...
sqft                                                   1,120 sqft
zipcode                                                     13214
beds                                                       3 Beds
state                                                          NY
stories                                                         1
target                                                   $129,900
Pool                                                        False
Year built                                                   1958
Name: 189616, dtype: object

In [349]:
# У этого объекта город на самом деле Syracuse
df_v11.loc[189616,'city']='Syracuse'

In [350]:
# Такого города не существует. Удалим такие строки
df_v11 = df_v11[df_v11.city!='Highway 30']
df_v11 = df_v11[df_v11.city!='Ijames Church Rd']
df_v11 = df_v11[df_v11.city!='Ldhl']
df_v11 = df_v11[df_v11.city!='Other City Not In The State Of Florida']

Хватит с меня! Идем дальше

In [351]:
# посмотрим есть ли пропуски
df_v11['city'].isna().sum()

np.int64(31)

In [352]:
df_v11[df_v11['city'].isna()]

status    propertyType                                    street  \
7830         active   single family                       13155 W Highway 316   
21529        active            land                              SE 117th Ter   
26466        active            land          Blk 4 N America Lareedo Rd Lot 8   
60989        active            land                                     Ocala   
122330       active            land                                 Sw149 Ter   
123474       active            land                             26484 Deer Rd   
130546      forsale   single family                 20003 Mar Rojo Y Mar Egeo   
131258       active            land                           19212 Roosevelt   
170319       active   single family                        2678 Calistoga Ave   
171274       active            land         Block 4 N America Laredo Rd Lot 9   
186758       active            land                                    Sw 110   
199625       active            land                                 SW 128 Pl   
215040       active            land                               NE 147th Ct   
221233       active            land        Block 4 N America Laredo Rd Lot 11   
221822       active            land        Block 4 N America Laredo Rd Lot 10   
262281    undefined            land                         2 Booga Bottom Rd   
270848       active            land       Block 4 N American Laredo Rd Lot 12   
277381       active            land                       13155 W Highway 316   
278435       active   single family                           7518 Marker Ave   
281938       active   single family                              290 Burma St   
304841  pendingsale            land                     Address Not Available   
309169       active  condo/townhome                8032 Lost Shaker Ln Unit 1   
312872       active            land                 Unditermined Unditermined   
325677       active            land                           11395 Ninth Ave   
331068       active            land                             Bay Place Run   
342229       active            land           Blk 4 N America Laredo Rd Lot 7   
346172      forsale   single family  Jose Correa 6 De Diciembre Quito Ecuador   
355273       active            land                           11398 Tenth Ave   
358810       active   single family                       8101 Surf Street Ln   
369946       active   farms/ranches               135 NE Pohang Colonia Corea   
370373       active            land                             17392 SE 65th   

          baths city                                            schools  \
7830          2  NaN  [{'rating': ['1', '4', '3', '3', '6', '6'], 'd...   
21529   unknown  NaN  [{'rating': [], 'data': {'Distance': [], 'Grad...   
26466   unknown  NaN  [{'rating': [], 'data': {'Distance': [], 'Grad...   
60989   unknown  NaN  [{'rating': [], 'data': {'Distance': [], 'Grad...   
122330  unknown  NaN  [{'rating': [], 'data': {'Distance': [], 'Grad...   
123474  unknown  NaN  [{'rating': ['6', '5', '7', '7', '2', '10', 'N...   
130546        6  NaN  [{'rating': ['5/10', 'NA', '4/10'], 'data': {'...   
131258  unknown  NaN  [{'rating': ['5', '4', '6', 'NR', '5', 'NR', '...   
170319      7.5  NaN  [{'rating': ['2', '4', '6', '4', '3', '10', 'N...   
171274  unknown  NaN  [{'rating': [], 'data': {'Distance': [], 'Grad...   
186758  unknown  NaN  [{'rating': [], 'data': {'Distance': [], 'Grad...   
199625  unknown  NaN  [{'rating': [], 'data': {'Distance': [], 'Grad...   
215040  unknown  NaN  [{'rating': [], 'data': {'Distance': [], 'Grad...   
221233  unknown  NaN  [{'rating': [], 'data': {'Distance': [], 'Grad...   
221822  unknown  NaN  [{'rating': [], 'data': {'Distance': [], 'Grad...   
262281  unknown  NaN  [{'rating': [], 'data': {'Distance': [], 'Grad...   
270848  unknown  NaN  [{'rating': [], 'data': {'Distance': [], 'Grad...   
277381  unknown  NaN  [{'rating': ['1', '4', '3', '3', '6', '6'], 'd..

Можно дропнуть такие строки, их не так много на общем фоне. А можно при наличии желания и времени пробить эти адреса по интернет картам и узнать название города. Сделаю несколько таких манипуляций, пока не надоест.  
А может даже правильнее будет не дропнуть такие строки а установить им признак в значение 'Other', потому как для определения нахождения объекта гораздо важнее почтовый индекс, чем название города. 
Кстати в разделе 'Other' также присутствуют записи, которые при большом желании можно идентифицировать вручную по индексу и названию улицы.

Прихожу к такой мысли. Названия городов могут повторяться в разных штатах, а вот в одном городе может быть несколько различных зон с разными почтовыми индексами. Может быть даже впоследствии придется дропнуть признак с названием города...  

In [353]:
df_v11.loc[7830,'city']="Reddick"
df_v11.loc[21529,'city']="Morriston"

df_v11.loc[342229,'city']="Laredo"
df_v11.loc[355273,'city']="Punta Gorda"
df_v11.loc[358810,'city']="Reunion"
df_v11.loc[370373,'city']="Ocklawaha"

df_v11.loc[348460,'city']="San Antonio"
df_v11.loc[338718,'city']="San Antonio"
df_v11.loc[337720,'city']="San Antonio"

In [354]:
df_v11.loc[df_v11['city'].isna(),'city'] = 'Other'

In [355]:
df_v11[df_v11['city']=='Other']

status    propertyType                                    street  \
20091        active         unknown                        7607 Triple Acres    
26466        active            land          Blk 4 N America Lareedo Rd Lot 8   
59758        active         unknown                      12604 Horseshoe Bay    
60989        active            land                                     Ocala   
78834        active         unknown                            34 Trophy Rdg    
101103       active         unknown                             2403 Ruth St    
107395       active         unknown                        8115 Ventura Blvd    
109170      forsale        lot/land                               Virginriver   
122330       active            land                                 Sw149 Ter   
123474       active            land                             26484 Deer Rd   
128284       active         unknown                       Undisclosed Address   
130546      forsale   single family                 20003 Mar Rojo Y Mar Egeo   
131258       active            land                           19212 Roosevelt   
131810       active         unknown                        22821 Linwood Rdg    
140135       active         unknown                       10163 WESTOVER Blf    
170319       active   single family                        2678 Calistoga Ave   
171274       active            land         Block 4 N America Laredo Rd Lot 9   
171672       active         unknown                        14719 Rifleman Rd    
186758       active            land                                    Sw 110   
193428       active         unknown                         55 E 1476 Land W    
199625       active            land                                 SW 128 Pl   
201812       active         unknown                       25003 Flying Arrow    
213404       active         unknown                      12405 Applewhite Rd    
215040       active            land                               NE 147th Ct   
221233       active            land        Block 4 N America Laredo Rd Lot 11   
221822       active            land        Block 4 N America Laredo Rd Lot 10   
245784       active         unknown                               231 Helena    
248938       active         unknown                       1401 S Flores #123    
262281    undefined            land                         2 Booga Bottom Rd   
270848       active            land       Block 4 N American Laredo Rd Lot 12   
276346       active         unknown                          6322 Mallard Pt    
277381       active            land                       13155 W Highway 316   
278435       active   single family                           7518 Marker Ave   
281938       active   single family                              290 Burma St   
287907       active         unknown                           1502 S Walters    
302652       active         unknown                          303 Shelburn Dr    
304841  pendingsale            land                     Address Not Available   
309169       active  condo/townhome                8032 Lost Shaker Ln Unit 1   
312872       active            land                 Unditermined Unditermined   
325677       active            land                           11395 Ninth Ave   
331068       active            land                             Bay Place Run   
346172      forsale   single family  Jose Correa 6 De Diciembre Quito Ecuador   
369946       active   farms/ranches               135 NE Pohang Colonia Corea   

          baths   city                                            schools  \
20091   unknown  Other  [{'rating': ['2', '2', '3'], 'data': {'Distanc...   
26466   unknown  Other  [{'rating': [], 'data': {'Distance': [], 'Grad...   
59758   unknown  Other  [{'rating': ['8', '8', '7', '7'], 'data': {'Di...   
60989   unknown  Other  [{'rating': [], 'data': {'Distance': [], 'Grad...   
78834     3,500  Other  [{'rating': ['9', '10', '8'], 'data': {

In [356]:
# сохраним
df_v11.to_pickle("data/df_v12.pkl")

___

**Переходим к признаку schools**

In [357]:
# считаем
df_v12 = pd.read_pickle("data/df_v12.pkl")

In [358]:
# вот такая структура
df_v12.schools[5]

"[{'rating': [], 'data': {'Distance': [], 'Grades': []}, 'name': []}]"

In [359]:
df_v12.schools[50]

"[{'rating': ['4/10', '5/10', '4/10'], 'data': {'Distance': ['5.92mi', '4.01mi', '7.58mi'], 'Grades': ['PK-6', '9-12', '7-8']}, 'name': ['Bunnell Elementary School', 'Flagler-Palm Coast High School', 'Buddy Taylor Middle School']}]"

In [360]:
# но есть первое значение, а может и еще есть такие же, с нарушенным синтаксисом
df_v12.schools[0]

'[{\'rating\': [\'4\', \'4\', \'7\', \'NR\', \'4\', \'7\', \'NR\', \'NR\'], \'data\': {\'Distance\': [\'2.7 mi\', \'3.6 mi\', \'5.1 mi\', \'4.0 mi\', \'10.5 mi\', \'12.6 mi\', \'2.7 mi\', \'3.1 mi\'], \'Grades\': [\'3–5\', \'6–8\', \'9–12\', \'PK–2\', \'6–8\', \'9–12\', \'PK–5\', \'K–12\']}, \'name\': [\'Southern Pines Elementary School\', \'Southern Middle School\', \'Pinecrest High School\', \'Southern Pines Primary School\', "Crain\'s Creek Middle School", \'Union Pines High School\', \'Episcopal Day Private School\', \'Calvary Christian Private School\']}]'

In [361]:
# странно, глюк какой-то чтоли!? А тут первая стока нормально показывает признак schools
df_v12

status   propertyType                    street    baths  \
0          active  single family            240 Heather Ln      3.5   
1         forsale  single family         12911 E Heroy Ave        3   
2         forsale  single family         2005 Westridge Rd        2   
3         forsale  single family       4311 Livingston Ave        8   
4         forsale       lot/land            1524 Kiscoe St  unknown   
...           ...            ...                       ...      ...   
377039  undefined  single family         20800 NE 23rd Ave      6.0   
377040    forsale          condo  3530 N Lake Shore Dr #4B        3   
377041    forsale  single family         15509 Linden Blvd        3   
377042  undefined        unknown           7810 Pereida St  unknown   
377043  undefined  single family          5983 Midcrown Dr      2.0   

                  city                                            schools  \
0       Southern Pines  [{'rating': ['4', '4', '7', 'NR', '4', '7', 'N...   
1       Spokane Valley  [{'rating': ['4/10', 'None/10', '4/10'], 'data...   
2          Los Angeles  [{'rating': ['8/10', '4/10', '8/10'], 'data': ...   
3               Dallas  [{'rating': ['9/10', '9/10', '10/10', '9/10'],...   
4             Palm Bay  [{'rating': ['4/10', '5/10', '5/10'], 'data': ...   
...                ...                                                ...   
377039           Miami  [{'rating': ['10/10', '5/10'], 'data': {'Dista...   
377040         Chicago  [{'rating': ['1/10', '5/10', '7/10'], 'data': ...   
377041         Jamaica  [{'rating': ['5/10', '4/10'], 'data': {'Distan...   
377042         Houston  [{'rating': ['NA', 'NA', 'NA'], 'data': {'Dist...   
377043     San Antonio  [{'rating': ['5/10', '4/10', '3/10'], 'data': ...   

              sqft zipcode        beds state stories      target   Pool  \
0             2900   28387           4    NC     NaN    $418,000  False   
1       1,947 sqft   99216      3 Beds    WA     2.0    $310,000  False   
2       3,000 sqft   90049      3 Beds    CA     1.0  $2,895,000   True   
3       6,457 sqft   75205      5 Beds    TX     3.0  $2,395,000  False   
4              NaN   32908         NaN    FL     NaN      $5,000  False   
...            ...     ...         ...   ...     ...         ...    ...   
377039       4,017   33180           5    FL     0.0  $1,249,000   True   
377040  2,000 sqft   60657      3 Beds    IL     9.0    $674,999  False   
377041  1,152 sqft   11434      3 Beds    NY       2    $528,000  False   
377042         NaN   77028  8,479 sqft    TX     NaN     $34,500  False   
377043       1,462   78218           3    TX     1.0    $204,900  False   

       Year built  
0            2019  
1            2019  
2            1961  
3            2006  
4            None  
...           ...  
377039       1990  
377040       1924  
377041       1950  
377042       None  
377043       2019  

[376747 rows x 14 columns]

In [362]:
# rating
s_rating = df_v12.schools.str.findall(r"\brating': ([\s\S]+?), 'data\b")
s_rating

0         [['4', '4', '7', 'NR', '4', '7', 'NR', 'NR']]
1                         [['4/10', 'None/10', '4/10']]
2                            [['8/10', '4/10', '8/10']]
3                   [['9/10', '9/10', '10/10', '9/10']]
4                            [['4/10', '5/10', '5/10']]
                              ...                      
377039                              [['10/10', '5/10']]
377040                       [['1/10', '5/10', '7/10']]
377041                               [['5/10', '4/10']]
377042                             [['NA', 'NA', 'NA']]
377043                       [['5/10', '4/10', '3/10']]
Name: schools, Length: 376747, dtype: object

Небольшой ликбез по типу rating:  
The Summary Rating calculation is based on four ratings, each of which is designed to show different facets of school success: the Student Progress Rating or Academic Progress Rating, College Readiness Rating, Equity Rating, and Test Score Rating. The ratings for each school vary based on data availability or relevance to a school level (for example, high schools have a College Readiness Rating, but elementary schools do not).

In [363]:
# Distance
s_distance = df_v12.schools.str.findall(r"\bDistance': ([\s\S]+?), 'Grades\b")
s_distance

0         [['2.7 mi', '3.6 mi', '5.1 mi', '4.0 mi', '10....
1                          [['1.65mi', '1.32mi', '1.01mi']]
2                          [['1.19mi', '2.06mi', '2.63mi']]
3                 [['1.05mi', '0.1mi', '1.05mi', '0.81mi']]
4                          [['5.96mi', '3.25mi', '3.03mi']]
                                ...                        
377039                              [['32.1 mi', '1.1 mi']]
377040                     [['10.61mi', '1.42mi', '0.4mi']]
377041                               [['0.48mi', '0.73mi']]
377042                     [['1.3 mi', '0.5 mi', '1.9 mi']]
377043                     [['0.3 mi', '1.1 mi', '4.1 mi']]
Name: schools, Length: 376747, dtype: object

In [364]:
# Grades
s_grades = df_v12.schools.str.findall(r"\bGrades': ([\s\S]+?)}, 'name\b")
s_grades

0         [['3–5', '6–8', '9–12', 'PK–2', '6–8', '9–12',...
1                                 [['9-12', '3-8', 'PK-8']]
2                                  [['6-8', 'K-5', '9-12']]
3                          [['5-6', 'PK-4', '7-8', '9-12']]
4                                 [['7-8', '9-12', 'PK-6']]
                                ...                        
377039                                   [['PK-8', '9-12']]
377040                           [['9-12', '9-12', 'PK-8']]
377041                                    [['PK-5', '6-8']]
377042                            [['PK-5', '6-8', '9-12']]
377043                            [['PK-5', '6-8', '9-12']]
Name: schools, Length: 376747, dtype: object

Небольшой ликбез по типу Grades:  
К-12 расшифровывается как «от Детского сада до 12 класса». Это примерно равняется школьному начальному возрасту от пяти до 12 лет в возрасте около 18 лет. Система разбита на три этапа: начальная школа (классы К-5), средняя школа (классы 6-8) и средняя школа (классы 9-12).

Дошкольный сад (также называемый Pre-K или PK) - добровольная дошкольная программа для детей в возрасте до пяти лет в США

In [365]:
# name
s_name = df_v12.schools.str.findall(r"\bname': ([\s\S]+?)[}\b]")
s_name

0         [['Southern Pines Elementary School', 'Souther...
1         [['East Valley High School&Extension', 'Eastva...
2         [['Paul Revere Middle School', 'Brentwood Scie...
3         [['Mcculloch Intermediate School', 'Bradfield ...
4         [['Southwest Middle School', 'Bayside High Sch...
                                ...                        
377039    [['Air Base Elementary School', 'Dr Michael M....
377040    [['Hope College Prep High School', 'Lake View ...
377041    [['Ps 48 William Wordsworth', 'Jhs 8 Richard S...
377042    [['Hiliard El', 'Forest Brook Middle', 'North ...
377043    [['Mary Lou Hartman', 'Woodlake Hills Middle S...
Name: schools, Length: 376747, dtype: object

Делаю следующие выводы:  
1. С название школы работать нет смысла, удалим признак
2. С признаком Grades технически можно было бы поработать, там структура довольна четкая. Но логического обоснования зависимости цены лота от этого признака я не усматриваю. Поэтому тоже дропну этот признак.
3. С райтингом школы можно попробовать поработать. Например взять средний рейтинг из ближайших школ - это косвенно даст понимание о благополучности района, что в свою очередь должно влиять на цену объекта.
4. Расстояние до школы. Тут конечно можно тоже среднее расстояние взять, но понимание общей картины может сильно искажаться из-за одной самой удаленной школы. Да и важнее наверное понимать есть ли школа в шаговой доступности. Поэтому из этого признака будем брать минимальное значение.

Приступим к s_rating

In [366]:
s_rating

0         [['4', '4', '7', 'NR', '4', '7', 'NR', 'NR']]
1                         [['4/10', 'None/10', '4/10']]
2                            [['8/10', '4/10', '8/10']]
3                   [['9/10', '9/10', '10/10', '9/10']]
4                            [['4/10', '5/10', '5/10']]
                              ...                      
377039                              [['10/10', '5/10']]
377040                       [['1/10', '5/10', '7/10']]
377041                               [['5/10', '4/10']]
377042                             [['NA', 'NA', 'NA']]
377043                       [['5/10', '4/10', '3/10']]
Name: schools, Length: 376747, dtype: object

In [367]:
s_rating = s_rating.apply(lambda x: x[0])
s_rating

0         ['4', '4', '7', 'NR', '4', '7', 'NR', 'NR']
1                         ['4/10', 'None/10', '4/10']
2                            ['8/10', '4/10', '8/10']
3                   ['9/10', '9/10', '10/10', '9/10']
4                            ['4/10', '5/10', '5/10']
                             ...                     
377039                              ['10/10', '5/10']
377040                       ['1/10', '5/10', '7/10']
377041                               ['5/10', '4/10']
377042                             ['NA', 'NA', 'NA']
377043                       ['5/10', '4/10', '3/10']
Name: schools, Length: 376747, dtype: object

In [368]:
s_rating = s_rating.str.replace('/10','', regex=False)
s_rating

0         ['4', '4', '7', 'NR', '4', '7', 'NR', 'NR']
1                                  ['4', 'None', '4']
2                                     ['8', '4', '8']
3                               ['9', '9', '10', '9']
4                                     ['4', '5', '5']
                             ...                     
377039                                    ['10', '5']
377040                                ['1', '5', '7']
377041                                     ['5', '4']
377042                             ['NA', 'NA', 'NA']
377043                                ['5', '4', '3']
Name: schools, Length: 376747, dtype: object

In [369]:
s_rating = s_rating.str.replace('[a-zA-Z]','', regex=True)

In [370]:
s_rating = s_rating.str.findall(r'\b([0-9])\'')
s_rating

0         [4, 4, 7, 4, 7]
1                  [4, 4]
2               [8, 4, 8]
3               [9, 9, 9]
4               [4, 5, 5]
               ...       
377039                [5]
377040          [1, 5, 7]
377041             [5, 4]
377042                 []
377043          [5, 4, 3]
Name: schools, Length: 376747, dtype: object

In [371]:
s_rating = s_rating.apply(lambda x: [float(i) for i in x])
s_rating

0         [4.0, 4.0, 7.0, 4.0, 7.0]
1                        [4.0, 4.0]
2                   [8.0, 4.0, 8.0]
3                   [9.0, 9.0, 9.0]
4                   [4.0, 5.0, 5.0]
                    ...            
377039                        [5.0]
377040              [1.0, 5.0, 7.0]
377041                   [5.0, 4.0]
377042                           []
377043              [5.0, 4.0, 3.0]
Name: schools, Length: 376747, dtype: object

In [372]:
s_rating = s_rating.apply(lambda x: np.average([int(i) for i in x]))
s_rating

c:\Users\User\AppData\Local\Programs\Python\Python39\lib\site-packages\numpy\lib\_function_base_impl.py:557: RuntimeWarning: Mean of empty slice.
  avg = a.mean(axis, **keepdims_kw)
c:\Users\User\AppData\Local\Programs\Python\Python39\lib\site-packages\numpy\_core\_methods.py:138: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)


0         5.200000
1         4.000000
2         6.666667
3         9.000000
4         4.666667
            ...   
377039    5.000000
377040    4.333333
377041    4.500000
377042         NaN
377043    4.000000
Name: schools, Length: 376747, dtype: float64

In [373]:
s_rating.fillna(-1)

0         5.200000
1         4.000000
2         6.666667
3         9.000000
4         4.666667
            ...   
377039    5.000000
377040    4.333333
377041    4.500000
377042   -1.000000
377043    4.000000
Name: schools, Length: 376747, dtype: float64

In [374]:
# Создадим признак rating_mean в нашем наборе данных. Пропуски заполним -1 
df_v12['r_sch_mean']= s_rating.fillna(-1).round(1)

In [375]:
df_v12.tail()

status   propertyType                    street    baths  \
377039  undefined  single family         20800 NE 23rd Ave      6.0   
377040    forsale          condo  3530 N Lake Shore Dr #4B        3   
377041    forsale  single family         15509 Linden Blvd        3   
377042  undefined        unknown           7810 Pereida St  unknown   
377043  undefined  single family          5983 Midcrown Dr      2.0   

               city                                            schools  \
377039        Miami  [{'rating': ['10/10', '5/10'], 'data': {'Dista...   
377040      Chicago  [{'rating': ['1/10', '5/10', '7/10'], 'data': ...   
377041      Jamaica  [{'rating': ['5/10', '4/10'], 'data': {'Distan...   
377042      Houston  [{'rating': ['NA', 'NA', 'NA'], 'data': {'Dist...   
377043  San Antonio  [{'rating': ['5/10', '4/10', '3/10'], 'data': ...   

              sqft zipcode        beds state stories      target   Pool  \
377039       4,017   33180           5    FL     0.0  $1,249,000   True   
377040  2,000 sqft   60657      3 Beds    IL     9.0    $674,999  False   
377041  1,152 sqft   11434      3 Beds    NY       2    $528,000  False   
377042         NaN   77028  8,479 sqft    TX     NaN     $34,500  False   
377043       1,462   78218           3    TX     1.0    $204,900  False   

       Year built  r_sch_mean  
377039       1990         5.0  
377040       1924         4.3  
377041       1950         4.5  
377042       None        -1.0  
377043       2019         4.0

Теперь признак Distance

In [376]:
s_distance

0         [['2.7 mi', '3.6 mi', '5.1 mi', '4.0 mi', '10....
1                          [['1.65mi', '1.32mi', '1.01mi']]
2                          [['1.19mi', '2.06mi', '2.63mi']]
3                 [['1.05mi', '0.1mi', '1.05mi', '0.81mi']]
4                          [['5.96mi', '3.25mi', '3.03mi']]
                                ...                        
377039                              [['32.1 mi', '1.1 mi']]
377040                     [['10.61mi', '1.42mi', '0.4mi']]
377041                               [['0.48mi', '0.73mi']]
377042                     [['1.3 mi', '0.5 mi', '1.9 mi']]
377043                     [['0.3 mi', '1.1 mi', '4.1 mi']]
Name: schools, Length: 376747, dtype: object

In [377]:
s_distance = s_distance.apply(lambda x: x[0])
s_distance

0         ['2.7 mi', '3.6 mi', '5.1 mi', '4.0 mi', '10.5...
1                            ['1.65mi', '1.32mi', '1.01mi']
2                            ['1.19mi', '2.06mi', '2.63mi']
3                   ['1.05mi', '0.1mi', '1.05mi', '0.81mi']
4                            ['5.96mi', '3.25mi', '3.03mi']
                                ...                        
377039                                ['32.1 mi', '1.1 mi']
377040                       ['10.61mi', '1.42mi', '0.4mi']
377041                                 ['0.48mi', '0.73mi']
377042                       ['1.3 mi', '0.5 mi', '1.9 mi']
377043                       ['0.3 mi', '1.1 mi', '4.1 mi']
Name: schools, Length: 376747, dtype: object

In [378]:
s_distance = s_distance.str.replace('[a-zA-Z]','', regex=True)
s_distance

0         ['2.7 ', '3.6 ', '5.1 ', '4.0 ', '10.5 ', '12....
1                                  ['1.65', '1.32', '1.01']
2                                  ['1.19', '2.06', '2.63']
3                           ['1.05', '0.1', '1.05', '0.81']
4                                  ['5.96', '3.25', '3.03']
                                ...                        
377039                                    ['32.1 ', '1.1 ']
377040                             ['10.61', '1.42', '0.4']
377041                                     ['0.48', '0.73']
377042                             ['1.3 ', '0.5 ', '1.9 ']
377043                             ['0.3 ', '1.1 ', '4.1 ']
Name: schools, Length: 376747, dtype: object

In [379]:
s_distance = s_distance.str.findall(r'\b([0-9]+.[0-9]+)')
s_distance

0         [2.7, 3.6, 5.1, 4.0, 10.5, 12.6, 2.7, 3.1]
1                                 [1.65, 1.32, 1.01]
2                                 [1.19, 2.06, 2.63]
3                            [1.05, 0.1, 1.05, 0.81]
4                                 [5.96, 3.25, 3.03]
                             ...                    
377039                                   [32.1, 1.1]
377040                            [10.61, 1.42, 0.4]
377041                                  [0.48, 0.73]
377042                               [1.3, 0.5, 1.9]
377043                               [0.3, 1.1, 4.1]
Name: schools, Length: 376747, dtype: object

In [380]:
s_distance = s_distance.apply(lambda x: [float(i) for i in x])
s_distance

0         [2.7, 3.6, 5.1, 4.0, 10.5, 12.6, 2.7, 3.1]
1                                 [1.65, 1.32, 1.01]
2                                 [1.19, 2.06, 2.63]
3                            [1.05, 0.1, 1.05, 0.81]
4                                 [5.96, 3.25, 3.03]
                             ...                    
377039                                   [32.1, 1.1]
377040                            [10.61, 1.42, 0.4]
377041                                  [0.48, 0.73]
377042                               [1.3, 0.5, 1.9]
377043                               [0.3, 1.1, 4.1]
Name: schools, Length: 376747, dtype: object

In [381]:
# пропусков нет
s_distance.isna().sum()

np.int64(0)

Но есть пустые списки. Для пустых списков также выставим значение -1

In [382]:
dist_sch_min = s_distance.apply(lambda x: -1 if len(x)==0 else min(x))
dist_sch_min

0         2.70
1         1.01
2         1.19
3         0.10
4         3.03
          ... 
377039    1.10
377040    0.40
377041    0.48
377042    0.50
377043    0.30
Name: schools, Length: 376747, dtype: float64

In [383]:
dist_sch_min[5]

np.float64(-1.0)

In [384]:
df_v12['dist_sch_min'] = dist_sch_min

In [385]:
df_v12.head()

status   propertyType               street    baths            city  \
0   active  single family       240 Heather Ln      3.5  Southern Pines   
1  forsale  single family    12911 E Heroy Ave        3  Spokane Valley   
2  forsale  single family    2005 Westridge Rd        2     Los Angeles   
3  forsale  single family  4311 Livingston Ave        8          Dallas   
4  forsale       lot/land       1524 Kiscoe St  unknown        Palm Bay   

                                             schools        sqft zipcode  \
0  [{'rating': ['4', '4', '7', 'NR', '4', '7', 'N...        2900   28387   
1  [{'rating': ['4/10', 'None/10', '4/10'], 'data...  1,947 sqft   99216   
2  [{'rating': ['8/10', '4/10', '8/10'], 'data': ...  3,000 sqft   90049   
3  [{'rating': ['9/10', '9/10', '10/10', '9/10'],...  6,457 sqft   75205   
4  [{'rating': ['4/10', '5/10', '5/10'], 'data': ...         NaN   32908   

     beds state stories      target   Pool Year built  r_sch_mean  \
0       4    NC     NaN    $418,000  False       2019         5.2   
1  3 Beds    WA     2.0    $310,000  False       2019         4.0   
2  3 Beds    CA     1.0  $2,895,000   True       1961         6.7   
3  5 Beds    TX     3.0  $2,395,000  False       2006         9.0   
4     NaN    FL     NaN      $5,000  False       None         4.7   

   dist_sch_min  
0          2.70  
1          1.01  
2          1.19  
3          0.10  
4          3.03

In [386]:
# откинем признак schools и сохраним
df_v12.drop('schools',axis=1).to_pickle("data/df_v13.pkl")

___

**Признак sqft**

In [387]:
# считаем
df_v13 = pd.read_pickle("data/df_v13.pkl")

In [388]:
df_v13

status   propertyType                    street    baths  \
0          active  single family            240 Heather Ln      3.5   
1         forsale  single family         12911 E Heroy Ave        3   
2         forsale  single family         2005 Westridge Rd        2   
3         forsale  single family       4311 Livingston Ave        8   
4         forsale       lot/land            1524 Kiscoe St  unknown   
...           ...            ...                       ...      ...   
377039  undefined  single family         20800 NE 23rd Ave      6.0   
377040    forsale          condo  3530 N Lake Shore Dr #4B        3   
377041    forsale  single family         15509 Linden Blvd        3   
377042  undefined        unknown           7810 Pereida St  unknown   
377043  undefined  single family          5983 Midcrown Dr      2.0   

                  city        sqft zipcode        beds state stories  \
0       Southern Pines        2900   28387           4    NC     NaN   
1       Spokane Valley  1,947 sqft   99216      3 Beds    WA     2.0   
2          Los Angeles  3,000 sqft   90049      3 Beds    CA     1.0   
3               Dallas  6,457 sqft   75205      5 Beds    TX     3.0   
4             Palm Bay         NaN   32908         NaN    FL     NaN   
...                ...         ...     ...         ...   ...     ...   
377039           Miami       4,017   33180           5    FL     0.0   
377040         Chicago  2,000 sqft   60657      3 Beds    IL     9.0   
377041         Jamaica  1,152 sqft   11434      3 Beds    NY       2   
377042         Houston         NaN   77028  8,479 sqft    TX     NaN   
377043     San Antonio       1,462   78218           3    TX     1.0   

            target   Pool Year built  r_sch_mean  dist_sch_min  
0         $418,000  False       2019         5.2          2.70  
1         $310,000  False       2019         4.0          1.01  
2       $2,895,000   True       1961         6.7          1.19  
3       $2,395,000  False       2006         9.0          0.10  
4           $5,000  False       None         4.7          3.03  
...            ...    ...        ...         ...           ...  
377039  $1,249,000   True       1990         5.0          1.10  
377040    $674,999  False       1924         4.3          0.40  
377041    $528,000  False       1950         4.5          0.48  
377042     $34,500  False       None        -1.0          0.50  
377043    $204,900  False       2019         4.0          0.30  

[376747 rows x 15 columns]

In [389]:
df_v13.sqft.nunique()

25405

In [390]:
df_v13.sqft.isna().sum()

np.int64(40426)

In [391]:
# Посмотрим как распределены значения propertyType в разрезе пропусков sqft
df_v13[df_v13.sqft.isna()].propertyType.value_counts()

propertyType
unknown           17985
lot/land          16373
single family      2247
condo               925
multi family        642
                  ...  
mid-rise              1
airlite               1
expanded ranch        1
spanish               1
farmhouse             1
Name: count, Length: 64, dtype: int64

Видно, что подавляющее большинство пропусков имеют лоты с типом unknown и lot/land

In [392]:
s_sqft = df_v13.sqft[df_v13.sqft.notna()]

In [393]:
s_sqft

0               2900
1         1,947 sqft
2         3,000 sqft
3         6,457 sqft
5           897 sqft
             ...    
377038         1,417
377039         4,017
377040    2,000 sqft
377041    1,152 sqft
377043         1,462
Name: sqft, Length: 336321, dtype: object

In [394]:
s_sqft = s_sqft.str.findall(r"\d+")

In [395]:
s_sqft

0           [2900]
1         [1, 947]
2         [3, 000]
3         [6, 457]
5            [897]
            ...   
377038    [1, 417]
377039    [4, 017]
377040    [2, 000]
377041    [1, 152]
377043    [1, 462]
Name: sqft, Length: 336321, dtype: object

In [396]:
s_sqft = s_sqft.apply(lambda x: ''.join(x))

In [397]:
s_sqft.info()

<class 'pandas.core.series.Series'>
Index: 336321 entries, 0 to 377043
Series name: sqft
Non-Null Count   Dtype 
--------------   ----- 
336321 non-null  object
dtypes: object(1)
memory usage: 5.1+ MB


In [398]:
df_v13.loc[df_v13.sqft.notna(), 'sqft']=s_sqft

In [399]:
# Заменю пропуски в признаке sqft на значение-маркер "-1"
df_v13.sqft = df_v13.sqft.fillna(-1)

In [400]:
# также есть пустые строки вместо значения. заменим их тоже -1
df_v13.loc[df_v13.sqft=='','sqft']=-1

In [401]:
df_v13.sqft = df_v13.sqft.astype(int)

In [402]:
df_v13.info()

<class 'pandas.core.frame.DataFrame'>
Index: 376747 entries, 0 to 377043
Data columns (total 15 columns):
 #   Column        Non-Null Count   Dtype  
---  ------        --------------   -----  
 0   status        376747 non-null  object 
 1   propertyType  376747 non-null  object 
 2   street        376745 non-null  object 
 3   baths         376747 non-null  object 
 4   city          376747 non-null  object 
 5   sqft          376747 non-null  int64  
 6   zipcode       376747 non-null  object 
 7   beds          285756 non-null  object 
 8   state         376747 non-null  object 
 9   stories       247225 non-null  object 
 10  target        374306 non-null  object 
 11  Pool          376747 non-null  bool   
 12  Year built    376747 non-null  object 
 13  r_sch_mean    376747 non-null  float64
 14  dist_sch_min  376747 non-null  float64
dtypes: bool(1), float64(2), int64(1), object(11)
memory usage: 43.5+ MB


In [403]:
df_v13[df_v13.sqft==df_v13.sqft.max()]

status   propertyType         street baths        city       sqft  \
62731  forsale  single family  1723 Pulte St     2  Cincinnati  795979430   

      zipcode    beds state stories   target   Pool Year built  r_sch_mean  \
62731   45225  2 Beds    OH     1.0  $27,500  False       1901         2.5   

       dist_sch_min  
62731          0.78

In [404]:
# Это снова пример ошибки ввода значений. Такой площади быть не может. Удалим эту строку.
df_v13 = df_v13.drop(62731)

In [405]:
df_v13[df_v13.sqft==df_v13.sqft.max()]

status  propertyType            street    baths      city       sqft  \
376389  active  multi family  5382 S Dixie Hwy  unknown  Glendale  456602479   

       zipcode beds state stories    target   Pool Year built  r_sch_mean  \
376389   42740  NaN    KY     NaN  $198,000  False       2012         6.3   

        dist_sch_min  
376389           3.1

Данный лот тоже считаю ошибочным, так как слишком большое значение sqft при достаточно низком значении цены. Удалим.

In [406]:
df_v13 = df_v13.drop(376389)

In [407]:
# посмотрим следующий максимум
df_v13[df_v13.sqft==df_v13.sqft.max()]

status propertyType       street    baths    city     sqft zipcode  \
74209  forsale     lot/land  Out Of Area  unknown  Laredo  7078574   78041   

      beds state stories   target   Pool Year built  r_sch_mean  dist_sch_min  
74209  NaN    TX     NaN  $98,000  False       None         7.0          2.53

Данный лот - это кусок земли, но даже для земли считаю такую цену за такую площадь это ничтожно мало. Но даже если это не ошибка, то это будет явным выбросом. Удаляем!

In [408]:
df_v13 = df_v13.drop(74209)

In [409]:
# посмотрим следующий максимум
df_v13[df_v13.sqft==df_v13.sqft.max()]

status propertyType        street    baths    city     sqft zipcode  \
142128  forsale     lot/land  Nka Solar Ln  unknown  Yakima  5728968   98901   

       beds state stories    target   Pool Year built  r_sch_mean  \
142128  NaN    WA     NaN  $289,000  False       None         4.0   

        dist_sch_min  
142128          7.97

Ну а вот этот хоть и тоже похож на выброс, но открыв карту и посмотрев на этот кусок земли я решил, что это не ошибочная запись. Этот кусок земли - это район в холмах(даже почти горах), там нет почти никакой растительности суда по фото со спутника. Так что думаю это действительно дешевая земля. Оставляем ее в наборе данных.

___

**Переходим к признаку zipcode**

In [410]:
df_v13.zipcode.nunique()

4549

In [411]:
df_v13.zipcode.isna().sum()

np.int64(0)

In [412]:
df_v13.zipcode.sort_values().unique()[:10]

array(['--', '0', '00000', '02108', '02109', '02110', '02111', '02113',
       '02114', '02115'], dtype=object)

Посмотрим на значения = '--'

In [413]:
df_v13[df_v13.zipcode=='--']

status propertyType                   street    baths  \
231230  newconstruction      unknown     0 N Gopher Canyon Rd  unknown   
235154        undefined    townhouse  1744 N Dixie Hwy # 1744      3.0   

                   city  sqft zipcode       beds state stories       target  \
231230          Bonsall    -1      --  449 acres    CA     NaN  $60,000,000   
235154  Fort Lauderdale  2043      --          3    FL     3.0     $425,000   

         Pool Year built  r_sch_mean  dist_sch_min  
231230  False       None         5.7           2.9  
235154  False       2010         5.0           0.5

Запись с индексом 231230 помимо пропуска в zipcode, еще и beds и sqft как-то сранно заполнены. Удалю!  
Запись с индексом 235154 вполне похожа на правду. Индекс по картам легко найти и исправить. Сделаем это.

In [414]:
df_v13 = df_v13.drop(231230)

In [415]:
df_v13.loc[235154,'zipcode']='33305'

Посмотрим на значения = '0' и '00000'

In [416]:
df_v13[df_v13.zipcode=='0']

status propertyType                     street    baths  \
30258    active         land            Gates Canyon Rd  unknown   
83514       new     colonial  Cornejo Ricardo Descalzi   unknown   
305481  forsale     lot/land           000 U.S. Hwy 359  unknown   

                 city    sqft zipcode beds state stories      target   Pool  \
30258       Vacaville       0       0  NaN    CA     NaN    $380,000  False   
83514   Quito Ecuador      -1       0  NaN    NY     NaN     470,000  False   
305481         Laredo  243849       0  NaN    TX     NaN  $1,740,000  False   

       Year built  r_sch_mean  dist_sch_min  
30258        None         5.0          6.50  
83514        1995        -1.0         -1.00  
305481       None         4.0          7.45

Впринципе я могу предположить, что объекты подобного плана - это земли с еще не присвоенным почтовым индексом. Но так как таких строк всего 3, толучше избавлюсь от них

In [417]:
df_v13 = df_v13.drop(30258)
df_v13 = df_v13.drop(83514)
df_v13 = df_v13.drop(305481)

In [418]:
df_v13[df_v13.zipcode=='00000']

status propertyType         street    baths             city  sqft  \
308135  active      unknown  435 pescador   unknown  Foreign Country  1100   

       zipcode beds state stories   target   Pool Year built  r_sch_mean  \
308135   00000  NaN    OS     NaN  125,000  False       1972        -1.0   

        dist_sch_min  
308135          -1.0

Сокращения OS для штата в интернете я не нашел ни для USA, ни для Мексики. Удалю эту строку, как ошибочную.

In [419]:
df_v13 = df_v13.drop(308135)

Далее идут индексы с первым нулем в названии. Насколько я смог понять - это действительно так и есть.

In [420]:
df_v13.zipcode.sort_values().unique()[:100]

array(['02108', '02109', '02110', '02111', '02113', '02114', '02115',
       '02116', '02118', '02119', '02120', '02121', '02122', '02124',
       '02125', '02126', '02127', '02128', '02129', '02130', '02131',
       '02132', '02134', '02135', '02136', '02199', '02210', '02215',
       '02467', '04666', '04901', '04937', '04957', '04963', '05345',
       '05441', '05441-4400', '05443', '05444', '05445', '05448', '05450',
       '05454', '05455', '05456', '05457', '05461', '05462', '05464',
       '05469', '05472', '05473', '05478', '05482', '05483', '05487',
       '05488', '05491', '05642', '07004', '07004-1106', '07004-1300',
       '07004-1413', '07004-1528', '07004-1607', '07004-1809',
       '07004-1878', '07004-1935', '07004-2116', '07004-2137',
       '07004-2214', '08701', '10001', '10002', '10003', '10004', '10005',
       '10006', '10007', '10009', '10010', '10011', '10012', '10013',
       '10014', '10016', '10017', '10018', '10019', '10021', '10022',
       '10023', '10024'

А вот странные индексы из двойного числа... Посмотрим на них

In [421]:
df_v13[df_v13.zipcode=='07004-2214']

status propertyType           street    baths           city  sqft  \
210416  active    townhouse  4 CHRISTINA Ct   unknown  Fairfield Twp  2400   

           zipcode beds state stories   target   Pool Year built  r_sch_mean  \
210416  07004-2214  NaN    NJ     3.0  535,000  False       2011         7.0   

        dist_sch_min  
210416           0.9

Карты показывают, что индекс у этого объекта: 1331 Waterville Mountain Rd, Bakersfield, VT 05441, USA. То есть без второй приставки. Посмотрю есть ли еще подобные индексы в базе.

In [422]:
df_v13[df_v13.zipcode.str.contains('.*-.*',na=False, regex=True)]

status  propertyType                  street    baths     city  sqft  \
3654    active           log          718 Powell Dr     1,500  Raleigh  1936   
5192    active      bungalow     915 Lake Boone Trl     2,500  Raleigh  1742   
7155    active      bungalow      1109 Virginia Ave     1,750   Durham  1194   
7545    active   traditional       3117 Henslowe Dr   unknown  Raleigh  1674   
8586    active  transitional        1209 Graedon Dr   unknown  Raleigh  6517   
...        ...           ...                     ...      ...      ...   ...   
363119  active      bungalow         3313 Garner Rd   unknown  Raleigh  1463   
363874  active   traditional           2625 Iman Dr   unknown  Raleigh  2933   
364948  active       spanish  14510 SW Lantern Ln N   unknown  Houston  1692   
365635  active   traditional      7303 Sweet Bay Ln   unknown  Raleigh  1520   
370201  active       unknown          5022 Saxon Dr   unknown  Houston    -1   

           zipcode   beds state stories     target   Pool Year built  \
3654    27606-1626  Baths    NC     1.5    315,000  False       1928   
5192    27607-6632  Baths    NC     NaN    475,000  False       1950   
7155    27705-3261  Baths    NC     NaN    284,900  False       1940   
7545    27603-2692    NaN    NC       2    245,000  False       1986   
8586    27603-3986    NaN    NC       2  1,599,000  False       2014   
...            ...    ...   ...     ...        ...    ...        ...   
363119  27610-5617    NaN    NC     NaN    250,000  False       1929   
363874  27615-3876    NaN    NC       1    340,000  False       1994   
364948  77015-2522    NaN    TX       1    139,999  False       1970   
365635  27615-6225    NaN    NC       2    197,000  False       1984   
370201  77092-5540    NaN    TX     NaN    130,000  False       None   

        r_sch_mean  dist_sch_min  
3654           6.0           0.9  
5192           6.0           0.2  
7155           3.7           0.5  
7545           5.0           2.3  
8586           5.0           3.2  
...            ...           ...  
363119         5.3           8.6  
363874         4.7           0.8  
364948         5.0           0.3  
365635         4.3           0.9  
370201         2.7           0.4  

[240 rows x 15 columns]

Делаю вывод, что это либо какая-то ошибка, либо я чего-то не знаю в разрезе этой темы. В любом случае таких строк не так много, поэтому обрежем обозначение, оставив только первую часть.

In [423]:
vvv = df_v13[df_v13.zipcode.str.contains('.*-.*',na=False, regex=True)]['zipcode']
vvv

3654      27606-1626
5192      27607-6632
7155      27705-3261
7545      27603-2692
8586      27603-3986
             ...    
363119    27610-5617
363874    27615-3876
364948    77015-2522
365635    27615-6225
370201    77092-5540
Name: zipcode, Length: 240, dtype: object

In [424]:
# Отрежем все, что после -
df_v13.zipcode = df_v13.zipcode.str.replace("-.+",'', regex=True)

In [425]:
df_v13.zipcode.nunique()

4317

In [426]:
df_v13.zipcode.sort_values().unique()[4200:]

array(['98201', '98203', '98204', '98206', '98208', '98223', '98225',
       '98226', '98229', '98236', '98270', '98271', '98275', '98290',
       '98292', '98296', '98303', '98310', '98311', '98312', '98321',
       '98327', '98332', '98333', '98335', '98337', '98338', '98342',
       '98346', '98354', '98359', '98360', '98366', '98367', '98370',
       '98371', '98372', '98373', '98374', '98375', '98380', '98387',
       '98388', '98390', '98391', '98392', '98402', '98403', '98404',
       '98405', '98406', '98407', '98408', '98409', '98418', '98421',
       '98422', '98424', '98439', '98443', '98444', '98445', '98446',
       '98465', '98466', '98467', '98489', '98498', '98499', '98501',
       '98502', '98503', '98506', '98512', '98513', '98516', '98580',
       '98606', '98607', '98642', '98660', '98661', '98662', '98663',
       '98664', '98665', '98682', '98683', '98684', '98685', '98686',
       '98798', '98901', '98902', '98903', '98908', '99004', '99005',
       '99016', '990

___

**Переходим к признаку beds**

In [427]:
df_v13.beds.isna().sum()

np.int64(90985)

In [428]:
df_v13.beds.nunique()

1183

In [429]:
df_v13.beds.unique().tolist()

['4',
 '3 Beds',
 '5 Beds',
 nan,
 '2 Beds',
 '3',
 '4 Beds',
 '3 bd',
 'Baths',
 '4 bd',
 '5 bd',
 '8 Beds',
 '2',
 '2 bd',
 '2.0',
 '5',
 '1',
 '3.0',
 '6 Beds',
 'Bath',
 '12 Beds',
 '6',
 '14',
 '0.25 acres',
 '6 bd',
 '-- bd',
 '7',
 '5.0',
 '4.0',
 ' ',
 '7 Beds',
 '1 bd',
 '9 Beds',
 '0.44 acres',
 '0',
 '1.43 acres',
 '0.32 acres',
 '8,637 sqft',
 '7.0',
 '8',
 '16 Beds',
 '9.7 acres',
 '1.0',
 '16 bd',
 '10,310 sqft',
 '6,250 sqft',
 '3.02 acres',
 '2 acres',
 '5,000 sqft',
 '0.96 acres',
 '6.0',
 '13 bd',
 '6.31 acres',
 '0.6 acres',
 '9',
 '5,662 sqft',
 '2,200 sqft',
 '10',
 '18 Beds',
 '10 Beds',
 '0.46 acres',
 '0.59 acres',
 '20 Beds',
 '0.0',
 '2,874 sqft',
 '0.26 acres',
 '10 bd',
 '32',
 '0.4 acres',
 '2,178 sqft',
 '6,351 sqft',
 '4,356 sqft',
 '5 acres',
 '0.55 acres',
 '5,501 sqft',
 '8,001 sqft',
 '0.7 acres',
 '1.69 acres',
 '0.88 acres',
 '0.34 acres',
 '13 Beds',
 '1.5 acres',
 '0.97 acres',
 '7,405 sqft',
 '7 bd',
 '8.43 acres',
 '1,502 sqft',
 '8,712 sqft',
 

Не смог придумать, как использовать этот признак. У него полная каша в данных. Данные могут быть как в acres и sqft, так и в простом количестве комнат. Видимо придется дропнуть этот признак.

In [430]:
df_v13 = df_v13.drop('beds', axis=1)

___
**Переходим к признаку state**

In [431]:
df_v13.state.isna().sum()

np.int64(0)

In [432]:
df_v13.state.nunique()

38

In [433]:
df_v13.state.unique()

array(['NC', 'WA', 'CA', 'TX', 'FL', 'PA', 'TN', 'IA', 'NY', 'OR', 'DC',
       'NV', 'AZ', 'GA', 'IL', 'NJ', 'MA', 'OH', 'IN', 'UT', 'MI', 'VT',
       'MD', 'CO', 'VA', 'KY', 'MO', 'WI', 'ME', 'MS', 'OK', 'SC', 'MT',
       'DE', 'Fl', 'BA', 'AL', 'OT'], dtype=object)

Тут вопросов нет.

___
**Переходим к признаку stories**

In [434]:
df_v13.stories.isna().sum()

np.int64(129515)

многовато пропусков! Но предполагаю, что это лоты с типом участок земли, где нет строения. Проверим.

In [435]:
df_v13[df_v13.stories.isna()]

status   propertyType                    street    baths  \
0            active  single family            240 Heather Ln      3.5   
4           forsale       lot/land            1524 Kiscoe St  unknown   
7            active        unknown           6094 Mingle Dr   unknown   
8            active  single family             11182 Owl Ave        2   
10          forsale           coop  14205 Roosevelt Ave #512        2   
...             ...            ...                       ...      ...   
377020       active           land        Homestead Dr Lot 1  unknown   
377023  foreclosure           coop      460 Ovington Ave #1I  unknown   
377027      forsale  single family          24080 Tuscany Ct        5   
377028      forsale  single family           653 NE 15th Ter  unknown   
377042    undefined        unknown           7810 Pereida St  unknown   

                  city  sqft zipcode state stories      target   Pool  \
0       Southern Pines  2900   28387    NC     NaN    $418,000  False   
4             Palm Bay    -1   32908    FL     NaN      $5,000  False   
7              Memphis    -1   38115    TN     NaN      68,000  False   
8           Mason City  3588   50401    IA     NaN    $244,900  False   
10            Flushing  1300   11354    NY     NaN    $669,000  False   
...                ...   ...     ...   ...     ...         ...    ...   
377020      Columbiana     0   44408    OH     NaN     $45,000  False   
377023        Brooklyn   520   11209    NY     NaN    $246,900  False   
377027  Bonita Springs  5992   34134    FL     NaN  $2,495,000   True   
377028     Gainesville  1740   32641    FL     NaN    $110,000  False   
377042         Houston    -1   77028    TX     NaN     $34,500  False   

       Year built  r_sch_mean  dist_sch_min  
0            2019         5.2          2.70  
4            None         4.7          3.03  
7            1976         2.7          0.40  
8            1970         3.8          5.60  
10           1965         5.0          0.30  
...           ...         ...           ...  
377020       None         8.3          2.00  
377023       1950         6.0          0.12  
377027       2006         5.5          2.06  
377028       1945         4.0          1.83  
377042       None        -1.0          0.50  

[129515 rows x 14 columns]

In [436]:
df_v13[df_v13.stories.isna()].propertyType.value_counts()

propertyType
single family    37368
unknown          27422
lot/land         18516
condo            18175
land             10164
                 ...  
queen anne           1
fairway house        1
moorage              1
warehouse            1
prairie              1
Name: count, Length: 124, dtype: int64

Как видим, предположение не подтвердилось. Пропусков хватает на разных типах.  
Либо удалять такой признак, либо, если не удалять вижу только один выход, заполнить пропуски, например - None.
В курсе нас учили, что признаки с таким количеством пропусков(34%) не несут информации для построения модели. Я склоняюсь удалить этот признак. Но в качестве тренировки пока оставлю его, приведу в порядок, а позже при построении модели можно будет посмотреть значимость каждого из признаков.

In [437]:
df_v13.stories = df_v13.stories.fillna('')

In [438]:
df_v13.stories.nunique()

347

In [439]:
df_v13.stories.sort_values().unique()

array(['', ', 1', ', 2', ', 3', '0', '0.0', '1', '1 1/2 Levels',
       '1 1/2 Story', '1 Level', '1 Level, 1.5 Level', '1 Level, 2 Level',
       '1 Level, Condo', '1 Level, Condo, Site Built',
       '1 Level, Non-Site Built', '1 Level, Site Built',
       '1 Level, Site Built, Townhouse', '1 Level, Split Foyer',
       '1 Level, Townhouse', '1 Leveland + Loft', '1 Story',
       '1 Story Basement', '1 Story, 2 Story', '1 Story, Hillside',
       '1 Story, Multi Level', '1 Story, Split Level',
       '1 Story, Townhouse', '1 Story/F.R.O.G.', '1 Story/Ranch', '1, 1',
       '1-2 Stories', '1-2 Stories, 3-4 Stories', '1.0', '1.00', '1.000',
       '1.0000', '1.2', '1.30', '1.3000', '1.5', '1.5 Level',
       '1.5 Level, Site Built', '1.5 Level, Site Built, Tri-Level',
       '1.5 Stories', '1.5 Story', '1.5 Story/Basement', '1.5, 2', '1.50',
       '1.500', '1.5000', '1.7', '1.70', '1.7000', '1.75', '10', '10.0',
       '1002.0', '11', '11.0', '11.00', '1120.0', '12', '12.0', '13',
   

In [440]:
df_v13[df_v13.stories=='None']

Empty DataFrame
Columns: [status, propertyType, street, baths, city, sqft, zipcode, state, stories, target, Pool, Year built, r_sch_mean, dist_sch_min]
Index: []

Хотя, посмотрев более пристально на значения, снова убеждаюсь, что качество наших данных хуже некуда! Помимо различного и странного (дробного например '1, 1 или '1.2'), тут же присутствуют значения типов домов ('Farm House', 'Log Home'). Все-таки придется удалить данный признак.

In [441]:
df_v13 = df_v13.drop('stories', axis=1)

___

**Переходим к непосредственно к целевому признаку target**

In [442]:
df_v13.target.isna().sum()

np.int64(2441)

Такие строки нам остается только откинуть

In [443]:
df_v13 = df_v13.dropna(subset=['target'])

In [444]:
df_v13.shape

(374298, 13)

In [445]:
df_v13.target.sort_values().unique()

array(['$1', '$1,000', '$1,000,000', ..., '999,995', '999,998', '999,999'],
      dtype=object)

Есть значения цены за месяц

In [446]:
df_v13[df_v13.target=='$1,000/mo']

status  propertyType                         street    baths  \
28076   forrent  multi family      5250 S Rainbow Blvd #2056  unknown   
51319   forrent     townhouse            9254 Forest Ln #107  unknown   
230166  forrent  multi family  870 Mayson Turner Rd NW #1118  unknown   

             city  sqft zipcode state     target   Pool Year built  \
28076   Las Vegas   744   89118    NV  $1,000/mo  False       1997   
51319      Dallas   748   75243    TX  $1,000/mo   True       1982   
230166    Atlanta   768   30314    GA  $1,000/mo  False       2007   

        r_sch_mean  dist_sch_min  
28076          5.5          0.31  
51319          5.7          0.55  
230166         2.0          1.53

Такие значения это скорее всего аренда.

In [447]:
df_v13[df_v13.target.str.contains('/mo',regex=True)]

status   propertyType                   street    baths  \
547     forrent  single family  4323 N Central Park Ave      3.5   
609     forrent   multi family    220 Boylston St #1412        2   
2075    forrent  single family          2830 NE 56th Ct        4   
3025    forrent   multi family            411 Kline Aly      2.5   
3645    forrent   multi family  240 E Illinois St #2011        2   
...         ...            ...                      ...      ...   
371654  forrent   multi family       9436 Turrentine Dr      1.5   
372321  forrent      townhouse            34 Jonquil Pl      2.5   
374149  forrent  single family       8864 Devonshire Dr        2   
375410  forrent      townhouse        2217 W Seybert St  unknown   
376835  forrent  single family      3819 Alabama Ave NE        2   

                    city  sqft zipcode state      target   Pool Year built  \
547              Chicago  3300   60618    IL   $5,500/mo  False       1913   
609               Boston  1673    2116    MA  $10,500/mo  False       1985   
2075     Fort Lauderdale  2400   33308    FL   $6,390/mo   True       1965   
3025         Clarksville  1280   37040    TN   $1,200/mo  False       2014   
3645             Chicago  1473   60611    IL   $3,600/mo   True       2003   
...                  ...   ...     ...   ...         ...    ...        ...   
371654           El Paso  1050   79925    TX     $890/mo  False       None   
372321     The Woodlands  2601   77375    TX   $2,500/mo  False       2014   
374149        Fort Worth  2000   76131    TX   $2,000/mo  False       2016   
375410      Philadelphia   720   19121    PA   $1,500/mo  False       1920   
376835  Saint Petersburg  1304   33703    FL   $1,900/mo  False       1961   

        r_sch_mean  dist_sch_min  
547            2.3          0.13  
609           -1.0         -1.00  
2075           4.0          1.19  
3025           8.0          0.68  
3645           5.5          0.72  
...            ...           ...  
371654         6.0          1.01  
372321         7.0          4.74  
374149         5.3          1.59  
375410         2.0          0.34  
376835         3.7          1.56  

[398 rows x 13 columns]

In [448]:
df_v13[df_v13.target.str.contains('/mo',regex=True)].status.unique()

array(['forrent'], dtype=object)

Да, видим абсолютную корреляцию со значением 'forrent' в признаке типа.

Теперь нужно выкинуть все символы, оставив только цифры

In [449]:
# Такой шаблон регулярки удалит все символы кроме цифр
df_v13.loc[:,'target'] = df_v13.loc[:,'target'].str.replace('[^0-9]','',regex=True)

In [450]:
df_v13

status   propertyType                    street    baths  \
0          active  single family            240 Heather Ln      3.5   
1         forsale  single family         12911 E Heroy Ave        3   
2         forsale  single family         2005 Westridge Rd        2   
3         forsale  single family       4311 Livingston Ave        8   
4         forsale       lot/land            1524 Kiscoe St  unknown   
...           ...            ...                       ...      ...   
377039  undefined  single family         20800 NE 23rd Ave      6.0   
377040    forsale          condo  3530 N Lake Shore Dr #4B        3   
377041    forsale  single family         15509 Linden Blvd        3   
377042  undefined        unknown           7810 Pereida St  unknown   
377043  undefined  single family          5983 Midcrown Dr      2.0   

                  city  sqft zipcode state   target   Pool Year built  \
0       Southern Pines  2900   28387    NC   418000  False       2019   
1       Spokane Valley  1947   99216    WA   310000  False       2019   
2          Los Angeles  3000   90049    CA  2895000   True       1961   
3               Dallas  6457   75205    TX  2395000  False       2006   
4             Palm Bay    -1   32908    FL     5000  False       None   
...                ...   ...     ...   ...      ...    ...        ...   
377039           Miami  4017   33180    FL  1249000   True       1990   
377040         Chicago  2000   60657    IL   674999  False       1924   
377041         Jamaica  1152   11434    NY   528000  False       1950   
377042         Houston    -1   77028    TX    34500  False       None   
377043     San Antonio  1462   78218    TX   204900  False       2019   

        r_sch_mean  dist_sch_min  
0              5.2          2.70  
1              4.0          1.01  
2              6.7          1.19  
3              9.0          0.10  
4              4.7          3.03  
...            ...           ...  
377039         5.0          1.10  
377040         4.3          0.40  
377041         4.5          0.48  
377042        -1.0          0.50  
377043         4.0          0.30  

[374298 rows x 13 columns]

In [451]:
df_v13.target.sort_values().unique()

array(['1', '1000', '10000', ..., '999998', '999999', '9999999'],
      dtype=object)

In [452]:
# Теперь можно перевести признак в числовой
df_v13.target = df_v13.target.astype(int)

In [453]:
df_v13.info()

<class 'pandas.core.frame.DataFrame'>
Index: 374298 entries, 0 to 377043
Data columns (total 13 columns):
 #   Column        Non-Null Count   Dtype  
---  ------        --------------   -----  
 0   status        374298 non-null  object 
 1   propertyType  374298 non-null  object 
 2   street        374296 non-null  object 
 3   baths         374298 non-null  object 
 4   city          374298 non-null  object 
 5   sqft          374298 non-null  int64  
 6   zipcode       374298 non-null  object 
 7   state         374298 non-null  object 
 8   target        374298 non-null  int64  
 9   Pool          374298 non-null  bool   
 10  Year built    374298 non-null  object 
 11  r_sch_mean    374298 non-null  float64
 12  dist_sch_min  374298 non-null  float64
dtypes: bool(1), float64(2), int64(2), object(8)
memory usage: 37.5+ MB


Минимальное значение = 1, очень странное. Смею предположить что это снова опечатка.

In [454]:
# Посмотрим сколько таких значений
# df_v13[df_v13.target==df_v13.target.min()]

In [455]:
# df_v13[df_v13.target==1]

Что это значит я так и не понял. И так как таких записей мало, лучше их удалим.

In [456]:
# df_v13=df_v13.drop(df_v13[df_v13.target==1].index)

In [457]:
# Посмотрим следующий минимум
# df_v13[df_v13.target==df_v13.target.min()]

In [458]:
min_targ = df_v13.target.sort_values().unique()[:10]
min_targ

array([  1,   3,   8,  20,  25,  29,  30, 250, 393, 400])

In [459]:
df_v13[df_v13.target.isin(min_targ)]

status   propertyType                         street    baths  \
15533        active  single family          1230 Old Dickerson Rd        2   
25334     undefined  single family          3205 N High School Rd      1.0   
84943   foreclosure       lot/land              7804 Hamilton Ave  unknown   
110273       active        unknown            13460 NW 107th Ave   unknown   
135415       active        unknown                 945 SE 18 Ave     2,500   
148219       active           land                    Cummings St  unknown   
162033       active        unknown  1451 Unit 1491 N Federal Hwy   unknown   
177790       active        unknown            3301 Ravenswood Rd     1,500   
197579    undefined        unknown                 8142 Byron Ave  unknown   
205315       active           land                   Route 47 Hwy  unknown   
212576  foreclosure  single family             20731 Edgecliff Dr        3   
252233  foreclosure       lot/land           8136 Bradyville Pike  unknown   
252560       active      2 stories           114 S Washington St   unknown   
256122    undefined          condo               9115 Sea Oats Dr      3.0   
270974       active           land             Middleground Rd SW  unknown   
275697       active        unknown            Undisclosed Address  unknown   
277491  foreclosure   multi family            2902 W McMicken Ave        3   
288983       active        unknown                0 ROUTE 47 Hwy     1,750   
289078  foreclosure  single family          1230 Old Dickerson Rd        2   
300143       active        unknown               1250 NW 7th Ave   unknown   
303954  foreclosure  single family          3205 N High School Rd  unknown   
316669       active        unknown              1150 NW 72nd Ave   unknown   
320704       active           land                     Lookout Rd  unknown   
321412  foreclosure          condo               9115 Sea Oats Dr        3   
334037       active           land                     High St NW  unknown   

                   city  sqft zipcode state  target   Pool Year built  \
15533    Goodlettsville  1596   37072    TN       1  False       1940   
25334      Indianapolis  1586   46224    IN       1  False       1957   
84943        Cincinnati  2536   45231    OH       1  False       1865   
110273  Hialeah Gardens    -1   33018    FL      20  False       None   
135415     Palmetto Bay    -1   33158    FL      29  False       None   
148219          Huntley     0   60142    IL       1  False       None   
162033  Fort Lauderdale    -1   33304    FL       8  False       None   
177790      Dania Beach    -1   33312    FL       3  False       None   
197579      Miami Beach    -1   33141    FL     250  False       None   
205315          Huntley     0   60142    IL       1  False       None   
212576           Euclid  2402   44123    OH     393  False       1941   
252233     Murfreesboro    -1   37127    TN       1  False       2005   
252560      Circleville  1771   43113    OH       1  False       1920   
256122     Indianapolis  1780   46250    IN       1  False       1989   
270974        Pataskala     0   43062    OH       1  False       None   
275697            Miami    -1   33175    FL      30  False       None   
277491       Cincinnati  3226   45225    OH       1  False       1870   
288983          Huntley    -1   60142    IL       1  False       None   
289078   Goodlettsville  1596   37072    TN       1  False       1940   
300143            Miami    -1   33136    FL       3  False       None   
303954     Indianapolis  1586   46224    IN       1  False       1957   
316669            Miami    -1   33126    FL      25  False       None   
320704           Amanda     0   43102    OH       1  False       None   
321412     Indianapolis  1780   46250    IN       1  False       1989   
334037         Abingdon     0   24210    VA     400  False       None   

        r_sch_mean  dist_sch_min  
15533          2.3          0.20  
25334          

In [460]:
df_v13.target.sort_values().unique()[:20]

array([  1,   3,   8,  20,  25,  29,  30, 250, 393, 400, 500, 600, 700,
       750, 800, 825, 850, 875, 890, 900])

In [461]:
df_v13.target.sort_values().unique()[-1:-20:-1]

array([195000000, 165000000, 150000000, 129000000, 115000000, 110000000,
        98000000,  88000000,  87000000,  85000000,  82500000,  78000000,
        75000000,  69975000,  69950000,  67000000,  65000000,  63815000,
        63750000])

In [462]:
# Посмотрим на максимум
df_v13[df_v13.target==165000000]

status   propertyType              street baths           city  \
143508  forsale  single family  67 Beverly Park Ct    23  Beverly Hills   
285910  forsale  single family  67 Beverly Park Ct    23  Beverly Hills   

         sqft zipcode state     target  Pool Year built  r_sch_mean  \
143508  28660   90210    CA  165000000  True       1998         6.0   
285910  28660   90210    CA  165000000  True       1998         6.0   

        dist_sch_min  
143508          3.72  
285910          3.40

Вывод по граничным значениям признака target:  
1. К максимальным значениям у меня вопросов не возникло. Карты подтверждают, что это элитные районы, да и размер sqft у них тоже велик. Так что вполне допускаю существование таких объектов.
2. С минимальными не так все однозначно. Очень смущают цены менее 100, особенно менее 10. И если бы таких значений было 1-2 шт, то я бы их без сомнений посчитал бы ошибочными. Но таких значений более десятка. Это наводит на мысль, что это не просто опечатка, а имеет под собой какую-то логику, которую я в данной сфере не знаю. Принимаю решение также оставить эти значения.

Если бы я принял решение о причислении таких значений к выбросам, то затем можно было определить и удалить выбросы, используя метод z-оценки или метод межквартильного диапазона.

Ну теперь все признаки подготовил. Проверим еще раз на счет дубликатов и пропусков

In [463]:
df_v13=df_v13.drop('street',axis=1)

In [464]:
df_v13.isna().sum()

status          0
propertyType    0
baths           0
city            0
sqft            0
zipcode         0
state           0
target          0
Pool            0
Year built      0
r_sch_mean      0
dist_sch_min    0
dtype: int64

In [465]:
df_v13.duplicated().sum() 

np.int64(5545)

Пропусков нет, но вот дубли появились.

In [466]:
df_v13[df_v13.duplicated(keep=False)].sort_values(by=['city','zipcode','dist_sch_min'])

status propertyType    baths      city  sqft zipcode state  target  \
299196  undefined      unknown  unknown        --    -1   33185    FL   35000   
362206  undefined      unknown  unknown        --    -1   33185    FL   35000   
216223     active         land  unknown  Abingdon     0   24210    VA   39900   
259636     active         land  unknown  Abingdon     0   24210    VA   39900   
85067      active         land  unknown  Abingdon     0   24210    VA   49900   
...           ...          ...      ...       ...   ...     ...   ...     ...   
198139    forsale        condo      2.0    Yakima  1358   98903    WA  290000   
22005     forsale     lot/land  unknown    Yakima    -1   98903    WA  300000   
285598    forsale     lot/land  unknown    Yakima    -1   98903    WA  300000   
265040    forsale     lot/land  unknown    Yakima    -1   98908    WA  195000   
357901    forsale     lot/land  unknown    Yakima    -1   98908    WA  195000   

         Pool Year built  r_sch_mean  dist_sch_min  
299196  False       None         6.5          0.60  
362206  False       None         6.5          0.60  
216223  False       None         5.7          1.30  
259636  False       None         5.7          1.30  
85067   False       None         5.5          2.90  
...       ...        ...         ...           ...  
198139  False       2014         5.0          0.90  
22005   False       None         5.0          4.25  
285598  False       None         5.0          4.25  
265040  False       None         4.0          1.99  
357901  False       None         4.0          1.99  

[9851 rows x 12 columns]

In [467]:
# Удалим дубли
df_v14 = df_v13.drop_duplicates(ignore_index=True)

На этом этап EDA считаю законченным. Сохраним наш результат

In [468]:
# сохраним
df_v14.to_pickle("data/df_v14.pkl")

In [469]:
# считаем
df_v14 = pd.read_pickle("data/df_v14.pkl")

Посмотрим на распределение нашего целевого признака

In [470]:
fig, axes = plt.subplots(nrows=1, ncols=2, figsize=(15, 4))
histplot = sns.histplot(data=df_v14, x='target', ax=axes[0]);
histplot.set_title('Распределение признака «target»');
# histplot.axvline(df_v14['target'].mean(), color='red', lw=2)

boxplot = sns.boxplot(data=df_v14, x='target', ax=axes[1]);
boxplot.set_title('Распределение признака «target»');

Посмотрим на распределение нашего целевого признака в логарифмическом масштабе

In [471]:
df_v14['target_log'] = np.log(df_v14['target']) # смысла прибавлять +1 нету, т.к. нулевых значений нет

# посмотрю на графики
fig, axes = plt.subplots(nrows=1, ncols=2, figsize=(15, 4))
histplot = sns.histplot(data=df_v14, x='target_log', ax=axes[0]);
histplot.set_title('Распределение «target» в log');
boxplot = sns.boxplot(data=df_v14, x='target_log', ax=axes[1]);
boxplot.set_title('Распределение «target» в log');

Проведем проверку на нормальность при помощи графиков квантилей QQ из библиотеки scipy

In [472]:
plt.figure(figsize=(15, 4), dpi=80)
plt.subplot(1, 2, 1) # задаем сетку рисунка количество строк и столбцов
stats.probplot(df_v14['target'], plot=plt) # qq plot

plt.subplot(1, 2, 2) # располагаем второй рисунок рядом
plt.hist(df_v14['target']) # гистограмма распределения признака

plt.tight_layout() # чтобы графики не наезжали другу на друга, используем tight_layout
plt.show()

C:\Users\User\AppData\Local\Temp\ipykernel_7976\2364488281.py:9: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  plt.show()


Также, мы можем использовать функцию qqplot() из библиотеки statsmodels. Правда тут я не смог найти как управлять размерами графика. Поэтому scipy мне больше понравился.

In [473]:
fig = sm.qqplot(df_v14['target'], line='s')
plt.show()

C:\Users\User\AppData\Local\Temp\ipykernel_7976\3116143767.py:2: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  plt.show()


видим, что этот набор данных не соответствует нормальному распределению в районе правого хвоста.  
То есть по графическим тестам мы можем сказать, что данные не имеют нормальной тенденции.

Хотя график QQ не является формальным статистическим тестом, он предлагает простой способ визуально проверить, нормально ли распределен набор данных.

Проверка на нормальность с помощью тестов

Существует целый ряд статистических тестов, специально разработанных для проверки нормальности распределения данных. В общем виде проверяемую при помощи этих тестов нулевую гипотезу можно сформулировать так: «Анализируемая выборка происходит из генеральной совокупности, имеющей нормальное распределение». Если получаемая при помощи того или иного теста вероятность ошибки Р оказывается меньше некоторого заранее принятого уровня значимости (например, 0.05), нулевая гипотеза отклоняется.

Тест Шапиро-Уилка является тестом на нормальность. Он используется для определения того, соответствует ли выборка нормальному распределению .

Этот тип теста полезен для определения того, исходит ли данный набор данных из нормального распределения, что является распространенным предположением, используемым во многих статистических тестах, включая регрессию , дисперсионный анализ , t-тесты и многие другие.

Чтобы выполнить тест Шапиро-Уилка, мы можем использовать функцию scipy.stats.shapiro()

Эта функция возвращает тестовую статистику и соответствующее p-значение.

Если p-значение ниже определенного уровня значимости, то у нас есть достаточно доказательств, чтобы сказать, что данные выборки не получены из нормального распределения.

In [474]:
stats.shapiro(df_v14['target'])

c:\Users\User\AppData\Local\Programs\Python\Python39\lib\site-packages\scipy\stats\_axis_nan_policy.py:531: UserWarning: scipy.stats.shapiro: For N > 5000, computed p-value may not be accurate. Current N is 368753.
  res = hypotest_fun_out(*samples, **kwds)


ShapiroResult(statistic=np.float64(0.21406738057720698), pvalue=np.float64(8.435441656843132e-210))

Из вывода мы видим, что статистика теста равна 0.21389 , а соответствующее значение pvalue=0.0 .

Поскольку p-значение меньше 0,05, мы отвергаем нулевую гипотезу. У нас есть достаточно доказательств, чтобы сказать, что данные выборки не имеют нормального распределения.

Но мы видим предупреждение, что размер выборки должен до 5000, чтобы функция shapiro.test() работала корректно.

Тест Колмогорова-Смирнова используется для проверки того, происходит ли выборка из определенного распределения.

Выполним тест Колмогорова-Смирнова для наших данных, чтобы определить, являются ли они результатом нормального распределения:

In [475]:
stats.kstest(df_v14['target'], 'norm')

KstestResult(statistic=np.float64(0.9999538986801456), pvalue=np.float64(0.0), statistic_location=np.int64(8), statistic_sign=np.int8(-1))

Видим, что статистика теста равна 0.99995 , а соответствующее значение pvalue=0.0. Поскольку p-значение меньше 0,05, мы отвергаем нулевую гипотезу. У нас есть достаточно доказательств, чтобы сказать, что данные выборки не имеют нормального распределения.

Проверим является ли распределение признака в логарифмическом масштабе нормальным?

Проверьте свою гипотезу с помощью теста Д’Агостино-Пирсона (scipy.stats.normaltest) при уровне значимости $\alpha=0.05$.

In [476]:
_, p = stats.normaltest(df_v14.target_log)
#normaltest возвращает двустороннюю вероятность для проверки гипотезы поэтому уровень значимости делим на 2
print('p=%.2f' % p)

if p > 0.05/2:
    print('Тест на нормальность данных пройден успешно!')
else:
    print('Тест на нормальность данных НЕ пройден!')

p=0.00
Тест на нормальность данных НЕ пройден!


Наш очищенный и подготовленный набор данных еще раз прогоним через ProfileReport

In [477]:
# проведу еще раз анализ на финальном датасете
profile = ydata_profiling.ProfileReport(df_v14, title="Profiling Report after EDA")
profile.to_file("data/df_v14_report.html")

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 13/13 [00:08<00:00,  1.45it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [478]:
df_v14.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 368753 entries, 0 to 368752
Data columns (total 13 columns):
 #   Column        Non-Null Count   Dtype  
---  ------        --------------   -----  
 0   status        368753 non-null  object 
 1   propertyType  368753 non-null  object 
 2   baths         368753 non-null  object 
 3   city          368753 non-null  object 
 4   sqft          368753 non-null  int64  
 5   zipcode       368753 non-null  object 
 6   state         368753 non-null  object 
 7   target        368753 non-null  int64  
 8   Pool          368753 non-null  bool   
 9   Year built    368753 non-null  object 
 10  r_sch_mean    368753 non-null  float64
 11  dist_sch_min  368753 non-null  float64
 12  target_log    368753 non-null  float64
dtypes: bool(1), float64(3), int64(2), object(7)
memory usage: 34.1+ MB


Из отчета наблюдаем, что существует сильная корреляция между признаками state и zipcode, что вполне логично. Также считаю, что признак city имеет слишком много уникальных значений и по логике он также должен коррелировать с zipcode.  
Поэтому принимаю решение оставить только zipcode, а state и city - удалить

Перед удалением посмотрю, ради интереса, рапределение количества лотов по штатам.

In [479]:
# Переведем признак state в категориальный тип
df_v14.state = df_v14.state.astype("category")
order=df_v14.value_counts('state')

plt.rcParams['figure.figsize'] = (12,6)
fig, ax = plt.subplots()
bar = sns.barplot(data=df_v14, x="state", y='target', estimator=len, order=order.index)
bar.set_title("распределение количества лотов")
bar.set_xlabel("штат")
bar.set_ylabel("количество лотов")
plt.show()

C:\Users\User\AppData\Local\Temp\ipykernel_7976\3366254460.py:11: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  plt.show()


In [480]:
df_v15 = df_v14.drop(['state'], axis=1)

In [481]:
# на всякий случай проверю не появились ли дубли
df_v15.duplicated().sum() 

np.int64(0)

In [482]:
df_v15

status   propertyType    baths            city  sqft zipcode  \
0          active  single family      3.5  Southern Pines  2900   28387   
1         forsale  single family        3  Spokane Valley  1947   99216   
2         forsale  single family        2     Los Angeles  3000   90049   
3         forsale  single family        8          Dallas  6457   75205   
4         forsale       lot/land  unknown        Palm Bay    -1   32908   
...           ...            ...      ...             ...   ...     ...   
368748  undefined  single family      6.0           Miami  4017   33180   
368749    forsale          condo        3         Chicago  2000   60657   
368750    forsale  single family        3         Jamaica  1152   11434   
368751  undefined        unknown  unknown         Houston    -1   77028   
368752  undefined  single family      2.0     San Antonio  1462   78218   

         target   Pool Year built  r_sch_mean  dist_sch_min  target_log  
0        418000  False       2019         5.2          2.70   12.943237  
1        310000  False       2019         4.0          1.01   12.644328  
2       2895000   True       1961         6.7          1.19   14.878496  
3       2395000  False       2006         9.0          0.10   14.688894  
4          5000  False       None         4.7          3.03    8.517193  
...         ...    ...        ...         ...           ...         ...  
368748  1249000   True       1990         5.0          1.10   14.037854  
368749   674999  False       1924         4.3          0.40   13.422466  
368750   528000  False       1950         4.5          0.48   13.176852  
368751    34500  False       None        -1.0          0.50   10.448715  
368752   204900  False       2019         4.0          0.30   12.230277  

[368753 rows x 12 columns]

In [483]:
test15 = df_v15[df_v15.drop(['city'], axis=1).duplicated(keep=False)]

In [484]:
df_v14.loc[test15.index].sort_values('zipcode')

status   propertyType    baths              city  sqft zipcode state  \
253944  forsale   multi family        3           Astoria  1232   11102    NY   
47051   forsale   multi family        3            Queens  1232   11102    NY   
55583   forsale   multi family        4  Long Island City  4050   11105    NY   
149589  forsale   multi family        4           Astoria  4050   11105    NY   
269620  forsale  single family        2           Bayside  1328   11361    NY   
...         ...            ...      ...               ...   ...     ...   ...   
359158  forsale       lot/land  unknown    Salt Lake City    -1   84121    UT   
240535  forsale  single family        3    Salt Lake City  3906   84121    UT   
103918  forsale       lot/land  unknown    Salt Lake City    -1   84121    UT   
159865  forsale          condo  unknown            Venice   811   90292    CA   
227884  forsale          condo  unknown    Marina Del Rey   811   90292    CA   

         target   Pool Year built  r_sch_mean  dist_sch_min  target_log  
253944  1268000  False       1920         4.3          0.24   14.052951  
47051   1268000  False       1920         4.3          0.24   14.052951  
55583   1725000  False       1955         4.0          0.19   14.360738  
149589  1725000  False       1955         4.0          0.19   14.360738  
269620   759000  False       1930         7.7          0.25   13.539757  
...         ...    ...        ...         ...           ...         ...  
359158   289900  False       None         4.7          0.30   12.577291  
240535   689900  False       2019         4.7          0.18   13.444302  
103918   375000  False       None        -1.0         -1.00   12.834681  
159865   695000   True       2003         6.0          0.59   13.451667  
227884   695000   True       2003         6.0          0.59   13.451667  

[152 rows x 13 columns]

In [485]:
df_v12.loc[df_v12.city=='Venice'][50:]

status   propertyType                        street    baths  \
156388      forsale  single family              1647 Crescent Pl        3   
158899      forsale  single family              1601 Oakwood Ave        2   
159987      forsale  single family              2318 Clement Ave        3   
162310      forsale          condo  13700 Marina Pointe Dr #1126  unknown   
168627      forsale  single family              2335 Louella Ave        3   
172078      forsale  single family              2218 Grand Canal        5   
173542      forsale          condo  13700 Marina Pointe Dr #1819        3   
181945      forsale  single family              2020 Alberta Ave        4   
182557      forsale  single family               2319 Penmar Ave        6   
196053      forsale      apartment                538 Brooks Ave        8   
201012      forsale   multi family           1601 Oakwood Ave #A        2   
203265      forsale  single family                2309 Ocean Ave        2   
204360      forsale   multi family                634 Brooks Ave        6   
208297      forsale  single family                18 Horizon Ave        3   
210883  foreclosure  single family                835 Sunset Ave        4   
214546      forsale  single family               639 Mildred Ave        4   
214874      forsale          condo                700 Main St #3        2   
215125      forsale  single family           639 Santa Clara Ave        5   
220375      forsale   multi family                   326 4th Ave        3   
225264      forsale  single family                865 Warren Ave        3   
228235      forsale  single family              630 Woodlawn Ave        4   
230456      forsale          condo  13700 Marina Pointe Dr #1518  unknown   
236250      forsale   multi family         1025 Pleasantview Ave        4   
244084      forsale   multi family                2429 Ocean Ave        5   
244942      forsale  single family                658 Oxford Ave        3   
247237      forsale  single family                758 Sunset Ave        4   
248032      forsale  single family              2605 Grand Canal        4   
259617      forsale  single family              2490 Glencoe Ave  unknown   
263796      forsale   multi family             416 S Venice Blvd        2   
265851      forsale   multi family              2504 Pacific Ave       18   
292058      forsale   multi family                852 Brooks Ave        6   
292708      forsale  single family              447 Linnie Canal        5   
294669      forsale  single family             219 Howland Canal        3   
294978      forsale   multi family                425 Venice Way  unknown   
297347      forsale  single family               126 Thornton Pl        4   
301728      forsale  single family              1010 Harding Ave        2   
303240      forsale  single family              2410 Grand Canal        3   
303531      forsale  single family          1210 Morningside Way        8   
303597      forsale  single family             1310 Glenavon Ave        5   
311775      forsale  single family                760 Sunset Ave        4   
312688      forsale  single family              2919 Sanborn Ave        5   
317226      forsale  single family                 31 Breeze Ave        7   
323306      forsale  single family                   24 18th Ave        2   
326951      forsale  single family                  838 Marco Pl        2   
331375      forrent   multi family               700 Main St #10        2   
333666      forsale  single family             1605 Cabrillo Ave        2   
335091      forsale  single family                922 Palms Blvd        4   
340417      forsale  single family               760 Indiana Ave      3.0   
341863      forsale  single family                 37 Dudley Ave        4   
347999      forsale   multi family               808 Venice Blvd        2   
357770      forsale   multi family                  1317 6th Ave        2   
358308   

Вобщем признак города придется тоже удалять. Из-за ошибочных написаний вместо города названия района или названия локации появились дубли.

In [486]:
df_v15 = df_v15.drop(['city'], axis=1)

In [487]:
# видим, что появились дубли
df_v15.duplicated().sum() 

np.int64(76)

In [488]:
# Удалим дубли
df_v15 = df_v15.drop_duplicates(ignore_index=True)

In [489]:
df_v15

status   propertyType    baths  sqft zipcode   target   Pool  \
0          active  single family      3.5  2900   28387   418000  False   
1         forsale  single family        3  1947   99216   310000  False   
2         forsale  single family        2  3000   90049  2895000   True   
3         forsale  single family        8  6457   75205  2395000  False   
4         forsale       lot/land  unknown    -1   32908     5000  False   
...           ...            ...      ...   ...     ...      ...    ...   
368672  undefined  single family      6.0  4017   33180  1249000   True   
368673    forsale          condo        3  2000   60657   674999  False   
368674    forsale  single family        3  1152   11434   528000  False   
368675  undefined        unknown  unknown    -1   77028    34500  False   
368676  undefined  single family      2.0  1462   78218   204900  False   

       Year built  r_sch_mean  dist_sch_min  target_log  
0            2019         5.2          2.70   12.943237  
1            2019         4.0          1.01   12.644328  
2            1961         6.7          1.19   14.878496  
3            2006         9.0          0.10   14.688894  
4            None         4.7          3.03    8.517193  
...           ...         ...           ...         ...  
368672       1990         5.0          1.10   14.037854  
368673       1924         4.3          0.40   13.422466  
368674       1950         4.5          0.48   13.176852  
368675       None        -1.0          0.50   10.448715  
368676       2019         4.0          0.30   12.230277  

[368677 rows x 11 columns]

In [490]:
df_v15.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 368677 entries, 0 to 368676
Data columns (total 11 columns):
 #   Column        Non-Null Count   Dtype  
---  ------        --------------   -----  
 0   status        368677 non-null  object 
 1   propertyType  368677 non-null  object 
 2   baths         368677 non-null  object 
 3   sqft          368677 non-null  int64  
 4   zipcode       368677 non-null  object 
 5   target        368677 non-null  int64  
 6   Pool          368677 non-null  bool   
 7   Year built    368677 non-null  object 
 8   r_sch_mean    368677 non-null  float64
 9   dist_sch_min  368677 non-null  float64
 10  target_log    368677 non-null  float64
dtypes: bool(1), float64(3), int64(2), object(5)
memory usage: 28.5+ MB


## 2. Отбор и преобразование признаков

In [491]:
df_v16 = df_v15.copy()

In [492]:
# сохраним
df_v16.to_pickle("data/df_v16.pkl")

In [493]:
# считаем
df_v16 = pd.read_pickle("data/df_v16.pkl")  

Закодируем категориальные признаки в наших данных

In [494]:
cols_to_code = ['status','propertyType','Year built','zipcode','baths']

In [495]:
df_ohe = pd.get_dummies(df_v16)

In [496]:
# сохраним
df_ohe.to_pickle("data/df_ohe.pkl")

In [497]:
# считаем
df_ohe = pd.read_pickle("data/df_ohe.pkl")  

Данный енкодер нам не подходит, так как у нас очень много признаков получается и модель на последующих шагах будет крашится из-за недостатка ОЗУ (а у меня ОЗУ 32ГБ). Да и файл df_ohe.pkl стал весить 1.8ГБ.

Поэтому применим BinaryEncoder

In [498]:
enc = ce.BinaryEncoder(cols=cols_to_code)

In [499]:
df_be = enc.fit_transform(df_v16.drop(['target', 'target_log'], axis=1))

In [500]:
df_be

status_0  status_1  status_2  status_3  status_4  status_5  status_6  \
0              0         0         0         0         0         0         1   
1              0         0         0         0         0         1         0   
2              0         0         0         0         0         1         0   
3              0         0         0         0         0         1         0   
4              0         0         0         0         0         1         0   
...          ...       ...       ...       ...       ...       ...       ...   
368672         0         0         0         0         0         1         1   
368673         0         0         0         0         0         1         0   
368674         0         0         0         0         0         1         0   
368675         0         0         0         0         0         1         1   
368676         0         0         0         0         0         1         1   

        propertyType_0  propertyType_1  propertyType_2  ...  Year built_0  \
0                    0               0               0  ...             0   
1                    0               0               0  ...             0   
2                    0               0               0  ...             0   
3                    0               0               0  ...             0   
4                    0               0               0  ...             0   
...                ...             ...             ...  ...           ...   
368672               0               0               0  ...             0   
368673               0               0               0  ...             0   
368674               0               0               0  ...             0   
368675               0               0               0  ...             0   
368676               0               0               0  ...             0   

        Year built_1  Year built_2  Year built_3  Year built_4  Year built_5  \
0                  0             0             0             0             0   
1                  0             0             0             0             0   
2                  0             0             0             0             0   
3                  0             0             0             0             0   
4                  0             0             0             0             1   
...              ...           ...           ...           ...           ...   
368672             1             0             0             1             1   
368673             1             0             0             0             0   
368674             0             1             1             1             1   
368675             0             0             0             0             1   
368676             0             0             0             0             0   

        Year built_6  Year built_7  r_sch_mean  dist_sch_min  
0                  0             1         5.2          2.70  
1                  0             1         4.0          1.01  
2                  1             0         6.7          1.19  
3                  1             1         9.0          0.10  
4                  0             0         4.7          3.03  
...              ...           ...         ...           ...  
368672             0             0         5.0          1.10  
368673             1             0         4.3          0.40  
368674             1             1         4.5          0.48  
368675             0             0        -1.0          0.50  
368676             0             1         4.0          0.30  

[368677 rows x 47 columns]

In [501]:
# сохраним
df_be.to_pickle("data/df_be.pkl")

Ну вот! другое дело! Файл всего 140Мб

In [502]:
# считаем


Еще одним методом кодирования так называемых high-dimensional data является метод feature hashing. В библиотеке scikit-learn это класс sklearn.feature_extraction.FeatureHasher. У данного метода есть небольшое ухудшение accuracy из-за возможных коллизий, это происходит, когда два значения элемента в конечном итоге хэшируются по одному и тому же индексу в векторе. Но из плюсов данного метода - это скорость и небольшое потребление вычислительных ресурсов.  
Еще один метод кодирования подобных данных является Bayesian Target Encoding. У него тоже помимо определенных плюсов есть и минус - склонность к переобучению. Данный метод реализован в библиотеке bayte.  
Так что при желании можно попробовать эти методы и в итоге сравнить, как это повлияет на конечный score нашей модели. Но оставлю эту идею, для факультативного решения :=)

Теперь, когда категориальные признаки предобработаны, сформируем матрицу наблюдений X, вектор целевой переменной y и его логарифм y_log. 

In [503]:
X = df_be
y = df_v16['target']
y_log = df_v16['target_log']

Все наши модели мы будем обучать на логарифмированной версии y_log. Так как его распределение  ближе к нормальному. Не знаю имеет ли логику это мое предположение..?

Разобьём выборку на обучающую и валидационную в соотношении 70/30:

In [504]:
X_train, X_test, y_train_log, y_test_log = model_selection.train_test_split(X, y_log, test_size=0.3, random_state=42)

In [505]:
X_train.shape

(258073, 47)

*При первом варианте кодирования, когда я использовал One-Hot Encoder, можно было отобрать с помощью SelectKBest важные признаки. Но по моему мнению после BinaryEncoder уже нельзя отбирать таким способом признаки, по причине логики самого енкодера. Верно ли мое мнение, нужно уточнить у менторов.*

На данный момент у нас слишком много признаков — скорее всего, не все из них будут важны. Оставлю лишь те, которые сильнее всего связаны с целевой переменной и точно будут вносить вклад в повышение качества модели.

С помощью SelectKBest отберу 25 признаков, наилучшим образом подходящих для предсказания целевой переменной в логарифмическом масштабе. Отбор реализую по обучающей выборке, используя параметр score_func = f_regression.

In [506]:
from sklearn.feature_selection import f_regression

select = feature_selection.SelectKBest(score_func = f_regression, k=25)
z = select.fit_transform(X_train,y_train_log)

In [507]:
filter_kb = select.get_support()

features = X_train.columns
print(features[filter_kb])

Index(['status_2', 'status_5', 'propertyType_1', 'propertyType_2',
       'propertyType_5', 'propertyType_7', 'baths_0', 'baths_1', 'baths_2',
       'baths_3', 'baths_4', 'baths_5', 'baths_6', 'sqft', 'zipcode_8',
       'zipcode_12', 'Pool', 'Year built_2', 'Year built_3', 'Year built_4',
       'Year built_5', 'Year built_6', 'Year built_7', 'r_sch_mean',
       'dist_sch_min'],
      dtype='object')


Хотя код SelectKBest конечно же ошибку не даст и проведет отбор, но еще раз повторюсь, считаю это не верным решением и применять его не буду в дальнейшем.

Немасштабированные данные будут вредными при вычислении оптимальных весов. Поэтому при работе с линейной моделью и числовыми данными, как правило, рекомендуется масштабировать данные. Применим StandardScaler к нашим данным.

In [508]:
scaler = preprocessing.StandardScaler()
scaler.fit(X_train)
X_train_scaled = scaler.transform(X_train)
X_test_scaled = scaler.transform(X_test)

## 3. Решение задачи регрессии:

Измерять качество наших моделей будем по метрике RMSLE (Root Mean Squared Log Error)

$RMSLE = \sqrt{\frac{1}{n} \sum_{i=1}^{n} (log (y_i) - log (\hat{y}_i))^2}$

Для начала воспользуемся самой простой моделью регрессии, которая нам известна — классическая линейная регрессия по методу OLS (ordinary least squares).

In [509]:
reg = linear_model.LinearRegression()
reg.fit(X_train_scaled, y_train_log)
y_train_pred = reg.predict(X_train_scaled)
y_test_pred = reg.predict(X_test_scaled)

In [510]:
# исходя из формулы RMSLE нужно взять корень от MSE
print('Train RMSLE score: {:.2f}'.format(np.sqrt(metrics.mean_squared_error(y_train_log, y_train_pred))))
print('Test RMSLE score: {:.2f}'.format(np.sqrt(metrics.mean_squared_error(y_test_log, y_test_pred))))

Train RMSLE score: 1.04
Test RMSLE score: 1.04


Попробую уменьшить ошибку прогноза, воспользовавшись полиномиальной регрессией

Сгенерирую полиномиальные признаки второй степени с помощью PolynomialFeatures

In [511]:
poly = preprocessing.PolynomialFeatures(include_bias=False) # degree=2 по-умолчанию
poly.fit(X_train_scaled)

X_train_poly = poly.transform(X_train_scaled)
#Генерируем полиномиальные признаки для валидационной выборки
X_test_poly = poly.transform(X_test_scaled)

Построю модель полиномиальной регрессии второй степени на обучающей выборке

In [512]:
#Создаём объект класса LinearRegression
reg_poly = linear_model.LinearRegression()
#Обучаем модель 
reg_poly.fit(X_train_poly, y_train_log)
#Делаем предсказание для тренировочной выборки
y_train_predict_poly = reg_poly.predict(X_train_poly)
#Делаем предсказание для валидационной выборки
y_test_predict_poly = reg_poly.predict(X_test_poly)

In [513]:
# метрики для полиноминальной регрессии
print('Polynomial Train RMSLE score: {:.2f}'.format(np.sqrt(metrics.mean_squared_error(y_train_log, y_train_predict_poly))))
print('Polynomial Test RMSLE score: {:.2f}'.format(np.sqrt(metrics.mean_squared_error(y_test_log, y_test_predict_poly))))

Polynomial Train RMSLE score: 0.89
Polynomial Test RMSLE score: 0.91


Метрика уменьшились для тренировочной выборки, но сильно увеличилась для тестовой. Поэтому построим модель полиномиальной регрессии второй степени с $L_2$-регуляризацией 

In [514]:
#Создаём объект класса линейной регрессии с L2-регуляризацией
ridge_lr = linear_model.Ridge(alpha=0.2) # alpha=1 по-умолчанию
#Обучаем модель
ridge_lr.fit(X_train_poly, y_train_log)
#Делаем предсказание для тренировочной выборки
y_train_predict_poly_r = ridge_lr.predict(X_train_poly)
#Делаем предсказание для тестовой выборки
y_test_predict_poly_r = ridge_lr.predict(X_test_poly)

In [515]:
# метрики для полиноминальной регрессии
print('Polynomial-L2 Train RMSLE score: {:.2f}'.format(np.sqrt(metrics.mean_squared_error(y_train_log, y_train_predict_poly_r))))
print('Polynomial-L2 Test RMSLE score: {:.2f}'.format(np.sqrt(metrics.mean_squared_error(y_test_log, y_test_predict_poly_r))))

Polynomial-L2 Train RMSLE score: 0.89
Polynomial-L2 Test RMSLE score: 0.91


Теперь попробую модель дерева решений

In [516]:
dtr = tree.DecisionTreeRegressor()
dtr.fit(X_train_scaled, y_train_log)

y_train_predict_dtr = dtr.predict(X_train_scaled)
y_test_predict_dtr = dtr.predict(X_test_scaled)

In [517]:
# метрики для DecisionTreeRegressor
print('DecisionTreeRegressor Train RMSLE score: {:.2f}'.format(np.sqrt(metrics.mean_squared_error(y_train_log, y_train_predict_dtr))))
print('DecisionTreeRegressor Test RMSLE score: {:.2f}'.format(np.sqrt(metrics.mean_squared_error(y_test_log, y_test_predict_dtr))))

DecisionTreeRegressor Train RMSLE score: 0.16
DecisionTreeRegressor Test RMSLE score: 0.93


Явно видем признак переобучения модели!

Поиграемся с глубиной дерева решений в диапазоне от 7 до 20:

In [518]:
# Задам словарь гиперпараметров для GridSearchCV
param_grid_DTR = {
              'max_depth': list(np.arange(6,21)) # максимальная глубина дерева
              }

In [519]:
#Создаем объект класса            
grid_search_DTR = model_selection.GridSearchCV(
    estimator=tree.DecisionTreeRegressor(), 
    param_grid=param_grid_DTR,
    n_jobs = -1,
    scoring='neg_mean_squared_error')

In [520]:
# Запускаем подбор гиперпараметров
grid_search_DTR.fit(X_train_scaled, y_train_log) 

GridSearchCV(estimator=DecisionTreeRegressor(), n_jobs=-1,
             param_grid={'max_depth': [np.int64(6), np.int64(7), np.int64(8),
                                       np.int64(9), np.int64(10), np.int64(11),
                                       np.int64(12), np.int64(13), np.int64(14),
                                       np.int64(15), np.int64(16), np.int64(17),
                                       np.int64(18), np.int64(19),
                                       np.int64(20)]},
             scoring='neg_mean_squared_error')

In [521]:
# посмотрим наилучшую найденную комбинацию гиперпараметров
grid_search_DTR.best_params_

{'max_depth': np.int64(12)}

In [522]:
grid_search_DTR.best_score_

np.float64(-0.6592750158444339)

In [523]:
# раз мы явно указали метрику -MSLE, то теперь можно посмотреть ее через данный метод
_MSLE = grid_search_DTR.score(X_test_scaled, y_test_log)
_MSLE

-0.648535165636103

In [524]:
# ну и наша метрика
print('DecisionTreeRegressor Test RMSLE score: {:.2f}'.format(np.sqrt(-_MSLE)))

DecisionTreeRegressor Test RMSLE score: 0.81


Посмотрим на графики, как менялись метрики в зависимости от глубины дерева

In [525]:
RMSLE_tr=[]
RMSLE_test=[]
for n in np.arange(6,21):
    dtr2 = tree.DecisionTreeRegressor(max_depth=n)
    dtr2.fit(X_train_scaled, y_train_log)
    y_train_predict_dtr2 = dtr2.predict(X_train_scaled)
    y_test_predict_dtr2 = dtr2.predict(X_test_scaled)
    mse_gs_train = metrics.mean_squared_error(y_train_predict_dtr2, y_train_log)
    mse_gs_test = metrics.mean_squared_error(y_test_predict_dtr2, y_test_log)
    RMSLE_tr.append(round(mse_gs_train**0.5, 2))
    RMSLE_test.append(mse_gs_test**0.5) #округление лучше не использовать, график тогда ломаный получается

In [526]:
# создадим фрейм
rmsle = pd.DataFrame({"depth":np.arange(6,21),"train":RMSLE_tr,"test":RMSLE_test})

In [527]:
fig, axs = plt.subplots()
line = sns.lineplot(data=rmsle,x="depth",y="train",label="RMSLE_train")
line2 = sns.lineplot(data=rmsle,x="depth",y="test",label="RMSLE_test")
line.set_ylabel("RMSLE")
axs.grid()

## 4. Решение задачи регрессии: ансамблевые методы

Построим модель случайного леса с найденной нами ранее наилучшим параметром глубины. Парметр criterion = 'squared_error' установлен в модели по-умолчанию

In [528]:
rfr = ensemble.RandomForestRegressor(max_depth=12,
                                  n_estimators=200,
                                  min_samples_split = 20,
                                  random_state=42,
                                    n_jobs = -1)

rfr.fit(X_train_scaled, y_train_log)

y_train_predict_rfr = rfr.predict(X_train_scaled)
y_test_predict_rfr = rfr.predict(X_test_scaled)

# метрики 
print('DecisionTreeRegressor Train RMSLE score: {:.2f}'.format(np.sqrt(metrics.mean_squared_error(y_train_log, y_train_predict_rfr))))
print('DecisionTreeRegressor Test RMSLE score: {:.2f}'.format(np.sqrt(metrics.mean_squared_error(y_test_log, y_test_predict_rfr))))

DecisionTreeRegressor Train RMSLE score: 0.73
DecisionTreeRegressor Test RMSLE score: 0.76


Благодаря параллельному обучению нескольких деревьев модель случайного леса дала нам небольшой прирост качества по сравнению с обычным деревом решений.

Посмотрим, что будет при последовательном ансамблировании ↓

Построю модель градиентного бустинга над деревьями решений (GradientBoostingRegressor) 

In [529]:
gbr = ensemble.GradientBoostingRegressor(learning_rate = 0.5,
                                         max_depth=6,
                                         n_estimators=100, #количество деревьев по-умолчанию
                                         min_samples_split = 30,
                                         random_state=42 #генератор случайных чисел
                                         )
gbr.fit(X_train_scaled, y_train_log)

y_train_predict_gbr = gbr.predict(X_train_scaled)
y_test_predict_gbr = gbr.predict(X_test_scaled)

# метрики 
print('DecisionTreeRegressor Train RMSLE score: {:.2f}'.format(np.sqrt(metrics.mean_squared_error(y_train_log, y_train_predict_gbr))))
print('DecisionTreeRegressor Test RMSLE score: {:.2f}'.format(np.sqrt(metrics.mean_squared_error(y_test_log, y_test_predict_gbr))))

DecisionTreeRegressor Train RMSLE score: 0.66
DecisionTreeRegressor Test RMSLE score: 0.69


Наблюдаем существенное улучшение метрик!

Посмотрим на важность факторов для наилучшей ансамблевой модели.

In [530]:
# есть возможность вывести самые важные признаки для модели через атрибут feature_importances_
plt.rcParams['figure.figsize'] = (12,6)
feat_importances = pd.Series(gbr.feature_importances_, index=X_train.columns)
feat_importances.nlargest(12).plot(kind='barh')

<Axes: ylabel='RMSLE'>

Поскольку категориальные признаки кодировал бинарным кодированием, то не представляется возможным оценить важность этих признаков. Но а вот иерархию важности числовых признаков мы можем наблюдать. Видим, что больше всего на цену влияет параметр полезной площади, что собственно логично. Далее по важности идут параметры: средний рейтинг ближайших школ и расстояние до ближайшей школы.

Несмотря на все преимущества, у метрики RMSLE есть один недостаток — она не является интерпретируемой. Поэтому для лучшей из построенных моделей рассчитаю медианную абсолютную ошибку (MeAE, в sklearn — функция median_absolute_error) 

In [531]:
y_test = np.exp(y_test_log)
y65_test_predict = np.exp(y_test_predict_gbr)

mae_test = metrics.median_absolute_error(y_test, y65_test_predict)
mae_test

np.float64(92869.26593938365)

Ну вывод какой-то не утешительный-)))) Ошибка модели в 92 т.$ - так себе результат

Могу объяснить это только тем, что в наших входных данных целевой признак имеет диапазон от 1$ до более чем 2 млн.

## 5. построение прогноза

Перед созданием прогноза для новых объектов необходимо произвести все манипуляции с данными, которые мы производили с тренировочной выборкой. Но! Считаю это не совсем логичным. Поскольку при анализе начальных данных многие признаки были признаны не пригодными для будущей модели и отброшены, то логичнее построить сервис предсказания, запрашивая только те признаки, которые явно участвуют в модели предсказания. То есть запрос входных данных для новых объектов перед подачей на вход модели должен иметь формат нашего очищенного фрейма df_v16.

In [532]:
df_v16.head()

status   propertyType    baths  sqft zipcode   target   Pool Year built  \
0   active  single family      3.5  2900   28387   418000  False       2019   
1  forsale  single family        3  1947   99216   310000  False       2019   
2  forsale  single family        2  3000   90049  2895000   True       1961   
3  forsale  single family        8  6457   75205  2395000  False       2006   
4  forsale       lot/land  unknown    -1   32908     5000  False       None   

   r_sch_mean  dist_sch_min  target_log  
0         5.2          2.70   12.943237  
1         4.0          1.01   12.644328  
2         6.7          1.19   14.878496  
3         9.0          0.10   14.688894  
4         4.7          3.03    8.517193

In [533]:
df_v16.columns

Index(['status', 'propertyType', 'baths', 'sqft', 'zipcode', 'target', 'Pool',
       'Year built', 'r_sch_mean', 'dist_sch_min', 'target_log'],
      dtype='object')

In [534]:
# Структура должна быть такая
df_v16.drop(['target','target_log'],axis=1).loc[1].values

array(['forsale', 'single family', '3', np.int64(1947), '99216',
       np.False_, '2019', np.float64(4.0), np.float64(1.01)], dtype=object)

In [535]:
cols = df_v16.drop(['target','target_log'],axis=1).columns

In [536]:
# Создадим первый запрос
request = [['active', 'single family', '3.5', 2900, '28387', True, '2019', 5.2, 2.7]]

Далее проводим последовательно те-же самые манипуляции, что и над тестовой выборкой:
 - BinaryEncoder,
 - StandardScaler,
 - непосредственно само предсказание с помощью GradientBoostingRegressor

In [537]:
req = pd.DataFrame(request, columns=cols)

In [538]:
req

status   propertyType baths  sqft zipcode  Pool Year built  r_sch_mean  \
0  active  single family   3.5  2900   28387  True       2019         5.2   

   dist_sch_min  
0           2.7

In [539]:
# Первый шаг - BinaryEncoder
req_be = enc.transform(req)

In [540]:
req_be

status_0  status_1  status_2  status_3  status_4  status_5  status_6  \
0         0         0         0         0         0         0         1   

   propertyType_0  propertyType_1  propertyType_2  ...  Year built_0  \
0               0               0               0  ...             0   

   Year built_1  Year built_2  Year built_3  Year built_4  Year built_5  \
0             0             0             0             0             0   

   Year built_6  Year built_7  r_sch_mean  dist_sch_min  
0             0             1         5.2           2.7  

[1 rows x 47 columns]

In [541]:
# Второй шаг - StandardScaler
req_ss = scaler.transform(req_be)

In [542]:
req_ss

array([[-0.01349638, -0.04113762, -0.15887867, -0.15900681, -0.23394976,
        -1.42117549,  1.20161271, -0.0165889 , -0.06748517, -0.14325964,
        -0.2632709 , -0.58385166, -0.49217336, -0.6289556 ,  0.38767074,
        -0.02619777, -0.13741722, -0.35145695, -0.46904309, -0.92598167,
        -1.06968652,  0.63795802,  0.01639186, -0.02887546, -0.3681234 ,
        -0.65866113, -0.82613311, -0.8827927 , -0.93628801, -0.96725455,
        -0.97948372, -1.01848739, -0.97600399, -0.98567642, -1.03598995,
         0.95418932,  2.86295811, -0.09739455, -0.55083458, -0.76727985,
        -0.66875279, -0.76902073, -1.04177904, -0.81941174,  1.01228518,
         0.18438112,  0.25026036]])

In [543]:
# Третий шаг - предсказание
req_predict_log = rfr.predict(req_ss)

In [544]:
req_predict_log

array([12.93702653])

In [545]:
# перевод из логарифмической шкалы в изначальную
req_predict = np.exp(req_predict_log)

In [546]:
req_predict

array([415412.18974643])

Можно все это обернуть в функцию для удобства

In [547]:
def final_predict(rec_list):
    req_f = pd.DataFrame([rec_list], columns=cols)
    req_be_f = enc.transform(req_f)
    req_ss_f = scaler.transform(req_be_f)
    req_predict_log_f = rfr.predict(req_ss_f)
    return round(np.exp(req_predict_log_f[0]))

Попробую второй запрос прогнать через данную функцию

In [548]:
request2 = ['forsale', 'single family', '3', 1947, '99216', True, '2019', 4.0, 1.01]

In [549]:
final_predict(request2)

364651

In [550]:
request3 = ['foreclosure', 'condo','3', 1780, '46250', False, '1989',  3.7, 1.71]
final_predict(request3)

240733

## 6. Подготовка модели к продакшену

Теперь, когда модель отработана и проверена, можно готовить ее к запуску в production

Поразмыслив, я пришел в выводу, что на этом этапе деление наших подготовленных данный на выборки train и test уже не имеет смысла, раз модель уже отточена. И поэтому подготовку пайплайна можно делать на полном наборе данных.  
**Вопрос к проверяющим менторам** - верен ли этот мой вывод?

Наши подготовленные данные находятся в переменной df_v16

In [551]:
df_v16

status   propertyType    baths  sqft zipcode   target   Pool  \
0          active  single family      3.5  2900   28387   418000  False   
1         forsale  single family        3  1947   99216   310000  False   
2         forsale  single family        2  3000   90049  2895000   True   
3         forsale  single family        8  6457   75205  2395000  False   
4         forsale       lot/land  unknown    -1   32908     5000  False   
...           ...            ...      ...   ...     ...      ...    ...   
368672  undefined  single family      6.0  4017   33180  1249000   True   
368673    forsale          condo        3  2000   60657   674999  False   
368674    forsale  single family        3  1152   11434   528000  False   
368675  undefined        unknown  unknown    -1   77028    34500  False   
368676  undefined  single family      2.0  1462   78218   204900  False   

       Year built  r_sch_mean  dist_sch_min  target_log  
0            2019         5.2          2.70   12.943237  
1            2019         4.0          1.01   12.644328  
2            1961         6.7          1.19   14.878496  
3            2006         9.0          0.10   14.688894  
4            None         4.7          3.03    8.517193  
...           ...         ...           ...         ...  
368672       1990         5.0          1.10   14.037854  
368673       1924         4.3          0.40   13.422466  
368674       1950         4.5          0.48   13.176852  
368675       None        -1.0          0.50   10.448715  
368676       2019         4.0          0.30   12.230277  

[368677 rows x 11 columns]

In [552]:
# Создаём пайплайн, который включает все наши шаги по подготовке данных и обучению модели
pipe = Pipeline([  
  ('BinaryEncoder', enc),
  ('StandardScaler', scaler),
  ('GradientBoostingRegressor', gbr)
  ])

In [553]:
# Входными данными для пайплайна будут
X_p = df_v16.drop(['target', 'target_log'], axis=1)
y_p = df_v16['target_log']

In [554]:
# Обучаем пайплайн
pipe.fit(X_p, y_p)

Pipeline(steps=[('BinaryEncoder',
                 BinaryEncoder(cols=['status', 'propertyType', 'Year built',
                                     'zipcode', 'baths'],
                               mapping=[{'col': 'status',
                                         'mapping':      status_0  status_1  status_2  status_3  status_4  status_5  status_6
 1          0         0         0         0         0         0         1
 2          0         0         0         0         0         1         0
 3          0         0         0         0         0         1         1
 4          0         0         0         0         1         0         0
 5          0         0         0         0         1         0         1
..        ...       ...       ...       ...       ...       ...       ...
 92         1         0         1         1         1         0         0
 93         1         0         1         1         1         0         1
 94         1         0         1         1         1         1         0
-1          0         0         0         0         0         0         0
-2          0         0         0         0         0         0         0

[96 rows x 7 columns]},
                                        {'col': 'propertyType',
                                         'm...
                                         'mapping':       baths_0  baths_1  baths_2  baths_3  baths_4  baths_5  baths_6
 1          0        0        0        0        0        0        1
 2          0        0        0        0        0        1        0
 3          0        0        0        0        0        1        1
 4          0        0        0        0        1        0        0
 5          0        0        0        0        1        0        1
...       ...      ...      ...      ...      ...      ...      ...
 112        1        1        1        0        0        0        0
 113        1        1        1        0        0        0        1
 114        1        1        1        0        0        1        0
-1          0        0        0        0        0        0        0
-2          0        0        0        0        0        0        0

[116 rows x 7 columns]}])),
                ('StandardScaler', StandardScaler()),
                ('GradientBoostingRegressor',
                 GradientBoostingRegressor(learning_rate=0.5, max_depth=6,
                                           min_samples_split=30,
                                           random_state=42))])

Сериализуем нашу обученную модель.

In [555]:
# Сериализуем и записываем результат в файл
with open('diplom_pipeline.pkl', 'wb') as output:
    pickle.dump(pipe, output)

Проверю работоспособность

In [556]:
# Десериализуем pipeline из файла
with open('diplom_pipeline.pkl', 'rb') as pkl_file:
    loaded_pipe = pickle.load(pkl_file)

In [557]:
# сделаю предсказание
request3 = ['foreclosure', 'condo','3', 1780, '46250', False, '1989',  3.7, 1.71]
req_f = pd.DataFrame([request3], columns=cols)
log_pred = loaded_pipe.predict(req_f)

In [558]:
# Переведем из логарифмического предсказания в обычные доллары
round(np.exp(log_pred[0]))

34938

Сразу есть мысли для дальнейшего улучшения логики работы сервиса. Если например пользователь не знает некоторые признаки. Можно в финальный пайплайн добавить кастомный трансформер, в который занести список наиболее часто используемых значений по каждому признаку, и тогда, когда пользователь передаст на вход модели список с некоторыми пустыми значениями, то можно проанализировать наличие таких пустых значений и произвести подстановку из этого заранее подготовленного списка. Реализовывать сейчас это не стану, но логику пропишу для понимания. Выглядеть будет примерно так.

In [559]:
class MyTransformer(TransformerMixin, BaseEstimator):
    '''Шаблон кастомного трансформера'''

    def __init__(self):
        '''Здесь прописывается инициализация параметров, не зависящих от данных.'''
        pass


    def fit(self, X, y=None):
        '''
        Здесь прописывается «обучение» трансформера.
        Вычисляются необходимые для работы трансформера параметры (если они нужны).
        '''
        return self


    def transform(self, rec_list):
        '''Здесь прописываются действия с данными.'''
        # тут будет код по заполнению пропущенных значений по каждому признаку - значениями из заданного словаря.
        return req_f

Тогда итоговый пайплайн будет выглядеть так

In [560]:
pipe2 = Pipeline([  
  ('FeatureEngineering', MyTransformer()),
  ('BinaryEncoder', enc),
  ('StandardScaler', scaler),
  ('GradientBoostingRegressor', gbr)
  ])

### Воспроизводимость и контейнеризация

Выполним важное для вывода модели в production требование по изоляции зависимостей и создадим файл requirements.txt 

In [561]:
pip freeze > requirements.txt

Note: you may need to restart the kernel to use updated packages.


### Контейнеризация Docker

Базовый образ, который буду использовать для своего контейнера — tiangolo/uwsgi-nginx-flask.  
Образ этот создан на базе ОС Linux, и в нём уже настроено взаимодействие серверов uWSGI и NGINX через сокеты.

Вся необходимая структура и сам конфигурационный файл для создания Docker образа находится в директории diplom_web.

Образ создаем командой, находясь в терминале нашего проекта:

     docker build -t diplom . 

Теперь нужно запустить, созданный контейнер.  
Делается это с помощью команды docker run. Запустим контейнер на 5000 порту:

    docker run -p 5000:5000 diplom python server.py

Далее выполним POST-запрос.  
Запустим в соседнем терминале скрипт для отправки запросов на 'http://localhost/predict'. В скрипте прописаны параметры гипотетического нового объекта недвижимости.

    python3 test/client.py


Меняя в строке запроса в файле client.py параметры предполагаемого объекта мы будем получать новое предсказание.

Подготовленный контейнер с обученной моделью размещен в моем репозитории https://github.com/Aleksandrbaik/Diplom-/

## Заключение

Таким образом на данном этапе мы имеем рабочий сервис с обученной моделью по поставленной нам задаче предсказания цены нового лота недвижимости.  
Далее, при необходимости можно будет обернуть данный сервис в дружелюбный для пользователя интерфейс.

На этом работу над проектом считаю законченной.